In [1]:
import pandas as pd
import mysql.connector
from sqlalchemy import create_engine

# Replace with your own database credentials
db_config = {
    "host": "db00",
    "user": "root",
    "password": "Local1234567",
    "database": "osticket_1-10-1_live"
}
# Create a SQLAlchemy engine using the MySQL connector connection
engine = create_engine(f"mysql+mysqlconnector://{db_config['user']}:{db_config['password']}@{db_config['host']}/{db_config['database']}")

# Define your SQL query
query = """
    SELECT 
        CONCAT(st.firstname, ' ', st.lastname) AS 'AssignedTo',
        te.name AS AssignedToTeam,
        t.created AS created,
        t.updated AS updated,
        Title.value AS Title,
        Classification.value AS Classification,
        Topic.value AS Topic,
        tre.body AS Text
    FROM 
        ost_ticket t
        JOIN ost_ticket_status ts ON (t.status_id = ts.id)
        JOIN ost_department d ON (t.dept_id = d.id)
        JOIN ost_thread tr ON (t.ticket_id = tr.object_id)
        JOIN ost_thread_entry tre ON (tr.id = tre.thread_id AND tre.type = 'M' AND tre.pid = 0)
        JOIN ost_form_entry f1 ON (t.ticket_id = f1.object_id AND f1.form_id = 2)
        LEFT JOIN ost_staff st ON (t.staff_id = st.staff_id)
        LEFT JOIN ost_team te ON (t.team_id = te.team_id)
        LEFT JOIN ost_form_entry_values Title ON (f1.id = Title.entry_id AND Title.field_id = 5 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Priority ON (f1.id = Priority.entry_id AND Priority.field_id = 7 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Classification ON (f1.id = Classification.entry_id AND Classification.field_id = 29 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Topic ON (f1.id = Topic.entry_id AND Topic.field_id = 31 AND f1.form_id = 2)
    WHERE 
        d.name = 'TABZ FLS'
    ORDER BY 
        created DESC
    LIMIT 5000
"""

# Use SQLAlchemy engine to execute the query and load data into a DataFrame
df = pd.read_sql(query, engine)


In [2]:
print(df)

              AssignedTo AssignedToTeam             created  \
0                   None            NAV 2023-09-08 15:04:20   
1     Patrik Platzgummer            NAV 2023-09-08 14:00:42   
2     Patrik Platzgummer            NAV 2023-09-08 13:57:39   
3           Daniele Neri            NAV 2023-09-08 13:34:50   
4     Patrik Platzgummer            NAV 2023-09-08 13:16:04   
...                  ...            ...                 ...   
4995        Daniele Neri    H/S Support 2023-03-13 15:10:04   
4996        Daniele Neri    H/S Support 2023-03-13 15:10:04   
4997     Arashdeep Singh    H/S Support 2023-03-13 15:07:02   
4998        Daniele Neri            NAV 2023-03-13 15:01:25   
4999        Daniele Neri            NAV 2023-03-13 15:01:25   

                 updated                                              Title  \
0    2023-09-08 15:04:20                                      WSHP-23.11636   
1    2023-09-08 14:17:25                                        Item weight   
2    2

In [3]:
# List of columns to keep (exclude the ones you want to remove)
columns_to_keep = ['Title', 'Topic', 'Text']

# Create a new DataFrame with only the selected columns
df = df[columns_to_keep]

# df now contains only columns A and B
print(df)

                                                  Title  \
0                                         WSHP-23.11636   
1                                           Item weight   
2                                    Modifica campo Nav   
3                                      metodo pagamento   
4               Darren Johnston bolle spedizioni Canada   
...                                                 ...   
4995  PC-Sala formazione, controllo dei port TCP e i...   
4996  PC-Sala formazione, controllo dei port TCP e i...   
4997                     Netzwerk und Kameraeinstellung   
4998                               Lieferschein Drucken   
4999                               Lieferschein Drucken   

                                                  Topic  \
0                                 {"22":"Dynamics NAV"}   
1                                 {"22":"Dynamics NAV"}   
2                                 {"22":"Dynamics NAV"}   
3                                 {"22":"Dynamics NAV"}

In [4]:
import re

values_to_keep = [
    '{"16":"User identity management, Permissions, Badge, Mail"}',
    '{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}',
    '{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}'
]

# Use str.contains to create a boolean mask, replace NaN with False, and then filter
mask = df['Topic'].str.contains('|'.join(map(re.escape, values_to_keep))).fillna(False)
filtered_df = df[mask]

# Print the filtered DataFrame
print(filtered_df)

                                 Title  \
6                              Procall   
7        Stampante uffico contabilita´   
10                            Tastiera   
11    Outlook  Termine erstellen TEams   
12                IDEpro Authenticator   
...                                ...   
4987                  Microsoft Teams    
4988             Fixtelefon geht nicht   
4992                carattere mancante   
4993                carattere mancante   
4997    Netzwerk und Kameraeinstellung   

                                                  Topic  \
6     {"12":"Standard Software: Operating systems, M...   
7     {"11":"Hardware, Telephony, Smartphones, Monit...   
10    {"11":"Hardware, Telephony, Smartphones, Monit...   
11    {"12":"Standard Software: Operating systems, M...   
12    {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
4987  {"12":"Standard Software: Operating systems, M...   
4988  {"11":"Hardware, 

In [5]:
# Reset the index to start from 0
filtered_df = filtered_df.reset_index(drop=True)

# Print the filtered DataFrame
print(filtered_df)

                                 Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2719                  Microsoft Teams    
2720             Fixtelefon geht nicht   
2721                carattere mancante   
2722                carattere mancante   
2723    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2719  {"12":"Standard Software: Operating systems, M...   
2720  {"11":"Hardware, 

In [6]:
from IPython.display import display, HTML

display(HTML('<style>.output { overflow-x: scroll; white-space: nowrap; }</style>'))
filtered_df

Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2719                  Microsoft Teams    
2720             Fixtelefon geht nicht   
2721                carattere mancante   
2722                carattere mancante   
2723    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2719  {"12":"Standard Software: Operating systems, M...   
2720  {"11":"Hardware, Telephony, Smartphones, Monit...   
2721  {"12":"Standard Software: Operating systems, M...   
2722  {"12":"Standard Software: Operating systems, M...   
2723  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
0     <p>Procall funktioniert nicht richtig.</p> <p>...  
1     <p>Ciao</p> <p>La stampante nel nostro ufficio...  
2     <p>Ciao,</p> <p>la mia tastiera purtropppo non...  
3     <p>Ciao,</p> <p>da oggi non vedo piu il link p...  
4     <p>Ciao,</p> <p>Ho bisogno di accedere a IDEpr...  
...                                                 ...  
2719  <p>Ciao,</p> <p>è tutto il giorno che riscontr...  
2720  <p>Hallo,</p> <p>Fixtelefon geht nicht.</p> <p...  
2721  <p>Devo tradurre una presentazione su power po...  
2722                   <p>ora funziona grazie mille</p>  
2723  <p>Hallo, </p> <p><br /></p> <p>ich habe keine...  

[2724 rows x 3 columns]

In [7]:
pip install beautifulsoup4

Note: you may need to restart the kernel to use updated packages.


In [8]:
#keep only the text

In [9]:
# Assuming you have a DataFrame named 'df' and you want to see all rows of the 'column_name' column
column_name = 'Text'
pd.set_option('display.max_rows', None)  # Set the option to display all rows
print(filtered_df[column_name])
pd.reset_option('display.max_rows')  # Reset the option to its default value

0       <p>Procall funktioniert nicht richtig.</p> <p>...
1       <p>Ciao</p> <p>La stampante nel nostro ufficio...
2       <p>Ciao,</p> <p>la mia tastiera purtropppo non...
3       <p>Ciao,</p> <p>da oggi non vedo piu il link p...
4       <p>Ciao,</p> <p>Ho bisogno di accedere a IDEpr...
5       Ciao,<br />lui deve acceder all'appartamento A...
6       <p>Ciao,<br />purtroppo hanno fatto un pò casi...
7       <p>Ciao,</p> <p>Volevo sapere se riceviamo anc...
8       <p>Ciao Manuel,</p> <p>Grazie. Sarebbe possibi...
9       <p>Ciao Francesco,</p> <p>Grazie tanto. Mi con...
10                                          <p>Grazie</p>
11      <p>Hallo, ich bekomme immer einen Fehler dass ...
12                     <p>169 578 378</p> <p>nqpdezyw</p>
13      <p>Ciao,</p> <p>Per favore reattivare l'utente...
14      <p>Ciao</p> <p>Mi poete collegare per favore q...
15      <p>Ciao,</p> <p>la stampante Verkauf PCV on pr...
16      <p>Egregi Signori,</p> <p>Vi prego di programm...
17      <p>Hel

In [10]:
import pandas as pd
from bs4 import BeautifulSoup
import re

In [11]:
def remove_html_tags(text):
    # Parse the HTML content using BeautifulSoup
    soup = BeautifulSoup(text, 'html.parser')
    
    # Remove HTML tags and extract only the text
    text = soup.get_text()
    
    # Remove any remaining special characters
    pattern = r'[^a-zA-Z0-9\s]'
    return re.sub(pattern, '', text)

# Apply the remove_html_tags function to the DataFrame columns containing HTML data
filtered_df['Text'] = filtered_df['Text'].apply(remove_html_tags)


C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\1070994409.py:3: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, 'html.parser')


In [12]:
column_name = 'Text'
pd.set_option('display.max_rows', None)  # Set the option to display all rows
print(filtered_df[column_name])
pd.reset_option('display.max_rows')  # Reset the option to its default value

0       Procall funktioniert nicht richtig habe schon ...
1       Ciao La stampante nel nostro ufficio non funzi...
2       Ciao la mia tastiera purtropppo non funziona p...
3       Ciao da oggi non vedo piu il link per il teams...
4       Ciao Ho bisogno di accedere a IDEpro ma quando...
5       Ciaolui deve acceder allappartamento AgostiniB...
6       Ciaopurtroppo hanno fatto un p casinoPotete pe...
7       Ciao Volevo sapere se riceviamo ancora una not...
8       Ciao Manuel Grazie Sarebbe possibile avere una...
9       Ciao Francesco Grazie tanto Mi confermi che ma...
10                                                 Grazie
11      Hallo ich bekomme immer einen Fehler dass die ...
12                                   169 578 378 nqpdezyw
13      Ciao Per favore reattivare lutente TAEE Mikola...
14      Ciao Mi poete collegare per favore questa stam...
15      Ciao la stampante Verkauf PCV on prtserv01  bl...
16      Egregi Signori Vi prego di programmare il badg...
17      Hello 

In [13]:
filtered_df.to_csv('cleaned_data.csv', index=False)

In [14]:
df = pd.read_csv('cleaned_data.csv')
df

Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2719                  Microsoft Teams    
2720             Fixtelefon geht nicht   
2721                carattere mancante   
2722                carattere mancante   
2723    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2719  {"12":"Standard Software: Operating systems, M...   
2720  {"11":"Hardware, Telephony, Smartphones, Monit...   
2721  {"12":"Standard Software: Operating systems, M...   
2722  {"12":"Standard Software: Operating systems, M...   
2723  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
0     Procall funktioniert nicht richtig habe schon ...  
1     Ciao La stampante nel nostro ufficio non funzi...  
2     Ciao la mia tastiera purtropppo non funziona p...  
3     Ciao da oggi non vedo piu il link per il teams...  
4     Ciao Ho bisogno di accedere a IDEpro ma quando...  
...                                                 ...  
2719  Ciao  tutto il giorno che riscontro problemi c...  
2720              Hallo Fixtelefon geht nicht LG Niklas  
2721  Devo tradurre una presentazione su power point...  
2722                          ora funziona grazie mille  
2723  Hallo   ich habe keinen Zugriff auaf das Netzw...  

[2724 rows x 3 columns]

In [15]:
df = df.dropna()

# The df_cleaned DataFrame will contain only rows with no NaN values
df

Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2719                  Microsoft Teams    
2720             Fixtelefon geht nicht   
2721                carattere mancante   
2722                carattere mancante   
2723    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2719  {"12":"Standard Software: Operating systems, M...   
2720  {"11":"Hardware, Telephony, Smartphones, Monit...   
2721  {"12":"Standard Software: Operating systems, M...   
2722  {"12":"Standard Software: Operating systems, M...   
2723  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
0     Procall funktioniert nicht richtig habe schon ...  
1     Ciao La stampante nel nostro ufficio non funzi...  
2     Ciao la mia tastiera purtropppo non funziona p...  
3     Ciao da oggi non vedo piu il link per il teams...  
4     Ciao Ho bisogno di accedere a IDEpro ma quando...  
...                                                 ...  
2719  Ciao  tutto il giorno che riscontro problemi c...  
2720              Hallo Fixtelefon geht nicht LG Niklas  
2721  Devo tradurre una presentazione su power point...  
2722                          ora funziona grazie mille  
2723  Hallo   ich habe keinen Zugriff auaf das Netzw...  

[2591 rows x 3 columns]

In [16]:
df.to_csv('final_data.csv', index=False)

In [17]:
df = pd.read_csv('final_data.csv')
df

Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2586                  Microsoft Teams    
2587             Fixtelefon geht nicht   
2588                carattere mancante   
2589                carattere mancante   
2590    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2586  {"12":"Standard Software: Operating systems, M...   
2587  {"11":"Hardware, Telephony, Smartphones, Monit...   
2588  {"12":"Standard Software: Operating systems, M...   
2589  {"12":"Standard Software: Operating systems, M...   
2590  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
0     Procall funktioniert nicht richtig habe schon ...  
1     Ciao La stampante nel nostro ufficio non funzi...  
2     Ciao la mia tastiera purtropppo non funziona p...  
3     Ciao da oggi non vedo piu il link per il teams...  
4     Ciao Ho bisogno di accedere a IDEpro ma quando...  
...                                                 ...  
2586  Ciao  tutto il giorno che riscontro problemi c...  
2587              Hallo Fixtelefon geht nicht LG Niklas  
2588  Devo tradurre una presentazione su power point...  
2589                          ora funziona grazie mille  
2590  Hallo   ich habe keinen Zugriff auaf das Netzw...  

[2591 rows x 3 columns]

In [18]:
#DELETE CONFIDENTIAL MESSAGE

import pandas as pd
import re

# Create or load your DataFrame 'df' with columns 'Title', 'Topic', and 'Text'

# Define a regular expression pattern to match the confidential message
confidential_pattern = re.compile(r"(?i)THIS MESSAGE INCLUDING ANY ATTACHMENTS CONTAINS CONFIDENTIAL INFORMATION.*?PROHIBITED", re.DOTALL)

# Function to remove text containing the confidential message
def remove_confidential_text(text):
    return re.sub(confidential_pattern, '', text)

# Apply the function to the 'Text' column
df['Text'] = df['Text'].apply(remove_confidential_text)

# Display the modified DataFrame
print(df)


                                 Title  \
0                              Procall   
1        Stampante uffico contabilita´   
2                             Tastiera   
3     Outlook  Termine erstellen TEams   
4                 IDEpro Authenticator   
...                                ...   
2586                  Microsoft Teams    
2587             Fixtelefon geht nicht   
2588                carattere mancante   
2589                carattere mancante   
2590    Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2586  {"12":"Standard Software: Operating systems, M...   
2587  {"11":"Hardware, 

In [19]:
import pandas as pd

desired_value = r'{"16":"User identity management, Permissions, Badge, Mail"}'

df_1 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_1

Title  \
5            NOSAL MIROSLAV - Badge / ACCESS   
6                                Licenze CRM   
7                           Password Windows   
8                           Password Windows   
9                           Password Windows   
...                                      ...   
2549                             Licenze CRM   
2550                             Licenze CRM   
2571  indirizzo Mail engo.parts@engo-ice.com   
2583                       TechnoAlpin Cloud   
2584                           Folder Access   

                                                  Topic  \
5     {"16":"User identity management, Permissions, ...   
6     {"16":"User identity management, Permissions, ...   
7     {"16":"User identity management, Permissions, ...   
8     {"16":"User identity management, Permissions, ...   
9     {"16":"User identity management, Permissions, ...   
...                                                 ...   
2549  {"16":"User identity management, Permissions, ...   
2550  {"16":"User identity management, Permissions, ...   
2571  {"16":"User identity management, Permissions, ...   
2583  {"16":"User identity management, Permissions, ...   
2584  {"16":"User identity management, Permissions, ...   

                                                   Text  
5     Ciaolui deve acceder allappartamento AgostiniB...  
6     Ciaopurtroppo hanno fatto un p casinoPotete pe...  
7     Ciao Volevo sapere se riceviamo ancora una not...  
8     Ciao Manuel Grazie Sarebbe possibile avere una...  
9     Ciao Francesco Grazie tanto Mi confermi che ma...  
...                                                 ...  
2549  Ciaopotremmo per favore assegnare la licenza d...  
2550  Ah upps sorry dovrebbe arrivare lunedi pensavo...  
2571  Ciao Birgit ci ha creato il nuovo indirizzo ma...  
2583  I am selecting to reset the password but it do...  
2584          Hi  I need to get access to these folders  

[894 rows x 3 columns]

In [20]:
# Reset the index to start from 0
df_1 = df_1.reset_index(drop=True)
df_1

Title  \
0           NOSAL MIROSLAV - Badge / ACCESS   
1                               Licenze CRM   
2                          Password Windows   
3                          Password Windows   
4                          Password Windows   
..                                      ...   
889                             Licenze CRM   
890                             Licenze CRM   
891  indirizzo Mail engo.parts@engo-ice.com   
892                       TechnoAlpin Cloud   
893                           Folder Access   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
889  {"16":"User identity management, Permissions, ...   
890  {"16":"User identity management, Permissions, ...   
891  {"16":"User identity management, Permissions, ...   
892  {"16":"User identity management, Permissions, ...   
893  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    Ciaolui deve acceder allappartamento AgostiniB...  
1    Ciaopurtroppo hanno fatto un p casinoPotete pe...  
2    Ciao Volevo sapere se riceviamo ancora una not...  
3    Ciao Manuel Grazie Sarebbe possibile avere una...  
4    Ciao Francesco Grazie tanto Mi confermi che ma...  
..                                                 ...  
889  Ciaopotremmo per favore assegnare la licenza d...  
890  Ah upps sorry dovrebbe arrivare lunedi pensavo...  
891  Ciao Birgit ci ha creato il nuovo indirizzo ma...  
892  I am selecting to reset the password but it do...  
893          Hi  I need to get access to these folders  

[894 rows x 3 columns]

In [21]:
import pandas as pd

# Convert the 'Text' column to uppercase
df_1['Text'] = df_1['Text'].str.upper()

df_1

Title  \
0           NOSAL MIROSLAV - Badge / ACCESS   
1                               Licenze CRM   
2                          Password Windows   
3                          Password Windows   
4                          Password Windows   
..                                      ...   
889                             Licenze CRM   
890                             Licenze CRM   
891  indirizzo Mail engo.parts@engo-ice.com   
892                       TechnoAlpin Cloud   
893                           Folder Access   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
889  {"16":"User identity management, Permissions, ...   
890  {"16":"User identity management, Permissions, ...   
891  {"16":"User identity management, Permissions, ...   
892  {"16":"User identity management, Permissions, ...   
893  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    CIAOLUI DEVE ACCEDER ALLAPPARTAMENTO AGOSTINIB...  
1    CIAOPURTROPPO HANNO FATTO UN P CASINOPOTETE PE...  
2    CIAO VOLEVO SAPERE SE RICEVIAMO ANCORA UNA NOT...  
3    CIAO MANUEL GRAZIE SAREBBE POSSIBILE AVERE UNA...  
4    CIAO FRANCESCO GRAZIE TANTO MI CONFERMI CHE MA...  
..                                                 ...  
889  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...  
890  AH UPPS SORRY DOVREBBE ARRIVARE LUNEDI PENSAVO...  
891  CIAO BIRGIT CI HA CREATO IL NUOVO INDIRIZZO MA...  
892  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...  
893          HI  I NEED TO GET ACCESS TO THESE FOLDERS  

[894 rows x 3 columns]

In [22]:
import pandas as pd

desired_value = r'{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}'  # Note the 'r' before the string for a raw string

df_2 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_2

Title  \
0                                 Procall   
3        Outlook  Termine erstellen TEams   
4                    IDEpro Authenticator   
10    digitale Prüfprotokoll non funziona   
11                          Adobe Lizenz    
...                                   ...   
2580                              Phising   
2586                     Microsoft Teams    
2588                   carattere mancante   
2589                   carattere mancante   
2590       Netzwerk und Kameraeinstellung   

                                                  Topic  \
0     {"12":"Standard Software: Operating systems, M...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
10    {"12":"Standard Software: Operating systems, M...   
11    {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2580  {"12":"Standard Software: Operating systems, M...   
2586  {"12":"Standard Software: Operating systems, M...   
2588  {"12":"Standard Software: Operating systems, M...   
2589  {"12":"Standard Software: Operating systems, M...   
2590  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
0     Procall funktioniert nicht richtig habe schon ...  
3     Ciao da oggi non vedo piu il link per il teams...  
4     Ciao Ho bisogno di accedere a IDEpro ma quando...  
10                                               Grazie  
11    Hallo ich bekomme immer einen Fehler dass die ...  
...                                                 ...  
2580  Quando clicco nel outlook su Phising melden mi...  
2586  Ciao  tutto il giorno che riscontro problemi c...  
2588  Devo tradurre una presentazione su power point...  
2589                          ora funziona grazie mille  
2590  Hallo   ich habe keinen Zugriff auaf das Netzw...  

[814 rows x 3 columns]

In [23]:
# Reset the index to start from 0
df_2 = df_2.reset_index(drop=True)
df_2

Title  \
0                                Procall   
1       Outlook  Termine erstellen TEams   
2                   IDEpro Authenticator   
3    digitale Prüfprotokoll non funziona   
4                          Adobe Lizenz    
..                                   ...   
809                              Phising   
810                     Microsoft Teams    
811                   carattere mancante   
812                   carattere mancante   
813       Netzwerk und Kameraeinstellung   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
809  {"12":"Standard Software: Operating systems, M...   
810  {"12":"Standard Software: Operating systems, M...   
811  {"12":"Standard Software: Operating systems, M...   
812  {"12":"Standard Software: Operating systems, M...   
813  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    Procall funktioniert nicht richtig habe schon ...  
1    Ciao da oggi non vedo piu il link per il teams...  
2    Ciao Ho bisogno di accedere a IDEpro ma quando...  
3                                               Grazie  
4    Hallo ich bekomme immer einen Fehler dass die ...  
..                                                 ...  
809  Quando clicco nel outlook su Phising melden mi...  
810  Ciao  tutto il giorno che riscontro problemi c...  
811  Devo tradurre una presentazione su power point...  
812                          ora funziona grazie mille  
813  Hallo   ich habe keinen Zugriff auaf das Netzw...  

[814 rows x 3 columns]

In [24]:
df_2['Text'] = df_2['Text'].str.upper()

df_2

Title  \
0                                Procall   
1       Outlook  Termine erstellen TEams   
2                   IDEpro Authenticator   
3    digitale Prüfprotokoll non funziona   
4                          Adobe Lizenz    
..                                   ...   
809                              Phising   
810                     Microsoft Teams    
811                   carattere mancante   
812                   carattere mancante   
813       Netzwerk und Kameraeinstellung   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
809  {"12":"Standard Software: Operating systems, M...   
810  {"12":"Standard Software: Operating systems, M...   
811  {"12":"Standard Software: Operating systems, M...   
812  {"12":"Standard Software: Operating systems, M...   
813  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    PROCALL FUNKTIONIERT NICHT RICHTIG HABE SCHON ...  
1    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...  
2    CIAO HO BISOGNO DI ACCEDERE A IDEPRO MA QUANDO...  
3                                               GRAZIE  
4    HALLO ICH BEKOMME IMMER EINEN FEHLER DASS DIE ...  
..                                                 ...  
809  QUANDO CLICCO NEL OUTLOOK SU PHISING MELDEN MI...  
810  CIAO  TUTTO IL GIORNO CHE RISCONTRO PROBLEMI C...  
811  DEVO TRADURRE UNA PRESENTAZIONE SU POWER POINT...  
812                          ORA FUNZIONA GRAZIE MILLE  
813  HALLO   ICH HABE KEINEN ZUGRIFF AUAF DAS NETZW...  

[814 rows x 3 columns]

In [25]:
import pandas as pd

desired_value = r'{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}'

df_3 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_3

Title  \
1     Stampante uffico contabilita´   
2                          Tastiera   
14                        Stampante   
15               stampante bloccata   
18                       new laptop   
...                             ...   
2579         stampante non funziona   
2581          problemi con wi-fi PC   
2582         need BITLOCK password    
2585                        Headset   
2587          Fixtelefon geht nicht   

                                                  Topic  \
1     {"11":"Hardware, Telephony, Smartphones, Monit...   
2     {"11":"Hardware, Telephony, Smartphones, Monit...   
14    {"11":"Hardware, Telephony, Smartphones, Monit...   
15    {"11":"Hardware, Telephony, Smartphones, Monit...   
18    {"11":"Hardware, Telephony, Smartphones, Monit...   
...                                                 ...   
2579  {"11":"Hardware, Telephony, Smartphones, Monit...   
2581  {"11":"Hardware, Telephony, Smartphones, Monit...   
2582  {"11":"Hardware, Telephony, Smartphones, Monit...   
2585  {"11":"Hardware, Telephony, Smartphones, Monit...   
2587  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                   Text  
1     Ciao La stampante nel nostro ufficio non funzi...  
2     Ciao la mia tastiera purtropppo non funziona p...  
14    Ciao Mi poete collegare per favore questa stam...  
15    Ciao la stampante Verkauf PCV on prtserv01  bl...  
18    Hi I need to order a new laptop for me Could y...  
...                                                 ...  
2579  ok grazie  non lo sappevo  faccio subito la pr...  
2581  Il PC non riconosce le reti esterne si sconnet...  
2582  this ticket is submitted  for Lindazhangtechno...  
2585  Ich bin seit ein paar Tagen mit Martin Hofer z...  
2587              Hallo Fixtelefon geht nicht LG Niklas  

[883 rows x 3 columns]

In [26]:
# Reset the index to start from 0
df_3 = df_3.reset_index(drop=True)
df_3

Title  \
0    Stampante uffico contabilita´   
1                         Tastiera   
2                        Stampante   
3               stampante bloccata   
4                       new laptop   
..                             ...   
878         stampante non funziona   
879          problemi con wi-fi PC   
880         need BITLOCK password    
881                        Headset   
882          Fixtelefon geht nicht   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
878  {"11":"Hardware, Telephony, Smartphones, Monit...   
879  {"11":"Hardware, Telephony, Smartphones, Monit...   
880  {"11":"Hardware, Telephony, Smartphones, Monit...   
881  {"11":"Hardware, Telephony, Smartphones, Monit...   
882  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    Ciao La stampante nel nostro ufficio non funzi...  
1    Ciao la mia tastiera purtropppo non funziona p...  
2    Ciao Mi poete collegare per favore questa stam...  
3    Ciao la stampante Verkauf PCV on prtserv01  bl...  
4    Hi I need to order a new laptop for me Could y...  
..                                                 ...  
878  ok grazie  non lo sappevo  faccio subito la pr...  
879  Il PC non riconosce le reti esterne si sconnet...  
880  this ticket is submitted  for Lindazhangtechno...  
881  Ich bin seit ein paar Tagen mit Martin Hofer z...  
882              Hallo Fixtelefon geht nicht LG Niklas  

[883 rows x 3 columns]

In [27]:
df_3['Text'] = df_3['Text'].str.upper()

df_3

Title  \
0    Stampante uffico contabilita´   
1                         Tastiera   
2                        Stampante   
3               stampante bloccata   
4                       new laptop   
..                             ...   
878         stampante non funziona   
879          problemi con wi-fi PC   
880         need BITLOCK password    
881                        Headset   
882          Fixtelefon geht nicht   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
878  {"11":"Hardware, Telephony, Smartphones, Monit...   
879  {"11":"Hardware, Telephony, Smartphones, Monit...   
880  {"11":"Hardware, Telephony, Smartphones, Monit...   
881  {"11":"Hardware, Telephony, Smartphones, Monit...   
882  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZI...  
1    CIAO LA MIA TASTIERA PURTROPPPO NON FUNZIONA P...  
2    CIAO MI POETE COLLEGARE PER FAVORE QUESTA STAM...  
3    CIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BL...  
4    HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD Y...  
..                                                 ...  
878  OK GRAZIE  NON LO SAPPEVO  FACCIO SUBITO LA PR...  
879  IL PC NON RICONOSCE LE RETI ESTERNE SI SCONNET...  
880  THIS TICKET IS SUBMITTED  FOR LINDAZHANGTECHNO...  
881  ICH BIN SEIT EIN PAAR TAGEN MIT MARTIN HOFER Z...  
882              HALLO FIXTELEFON GEHT NICHT LG NIKLAS  

[883 rows x 3 columns]

# MOST USED WORDS

# df_1
{"16":"User identity management, Permissions, Badge, Mail"}

In [28]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

In [29]:
import nltk
nltk.download('stopwords')

# Tokenize and remove stopwords
stop_words = set(stopwords.words('english'))
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in stop_words])


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [30]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('stopwords')
nltk.download('punkt')

# Tokenize and remove stopwords for the 'Text' column
stop_words = set(stopwords.words('english'))
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in stop_words])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_1['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(100)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('per', 316), ('di', 308), ('grazie', 266), ('e', 247), ('il', 237), ('ciao', 232), ('non', 216), ('che', 183), ('la', 182), ('badge', 138), ('da', 124), ('mi', 119), ('bitte', 114), ('mail', 112), ('hallo', 106), ('come', 101), ('le', 99), ('die', 99), ('un', 98), ('saluti', 94), ('al', 94), ('technoalpin', 93), ('prego', 91), ('email', 89), ('danke', 81), ('favore', 80), ('una', 80), ('con', 80), ('von', 80), ('please', 79), ('39', 76), ('via', 73), ('und', 71), ('ich', 69), ('ha', 69), ('fr', 69), ('mille', 67), ('potete', 67), ('anche', 66), ('der', 65), ('password', 64), ('nicht', 61), ('2', 60), ('outlook', 58), ('hello', 58), ('1', 57), ('se', 56), ('ho', 56), ('0471', 53), ('sono', 51), ('del', 50), ('manuel', 50), ('hi', 50), ('licenza', 49), ('den', 49), ('vi', 47), ('si', 46), ('id', 44), ('ad', 43), ('das', 43), ('ta', 43), ('im', 42), ('agostini', 42), ('accesso', 41), ('nuovo', 40), ('buongiorno', 38), ('account', 38), ('0', 38), ('horst', 37), ('alle', 36), ('pi', 36), 

In [31]:
#It includes a custom list of words to remove

import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella']


# Tokenize and remove stopwords from the 'Text' column
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_1['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('badge', 138), ('mail', 112), ('email', 89), ('password', 64), ('outlook', 58), ('licenza', 49), ('accesso', 41), ('account', 38), ('accedere', 33), ('pc', 33), ('access', 30), ('diritti', 30), ('nav', 26), ('computer', 25), ('server', 25), ('vpn', 25), ('crm', 23), ('send', 21), ('sap', 21), ('mensa', 21), ('concur', 20), ('message', 20), ('porte', 19), ('laptop', 19), ('phone', 18), ('microsoft', 18), ('ufficio', 17), ('fino', 16), ('persone', 16), ('emails', 16)]


In [32]:
import pandas as pd

# Create keywords for each subset
keywords = {
    'df_1_email': ['message', 'mail', 'email', 'emails', 'account', 'sender', 'recipient',
                   'microsoft', 'outlook', 'password', 'attachments', 'send','licenza'],
    'df_2_rights': ['badge', 'accedere', 'diritti', 'access', 'porte', 'mensa', 'accesso'],
    'df_3_computer': ['pc', 'laptop', 'computer', 'phone', 'password'],
    'df_4_software': ['server', 'nav', 'vpn', 'crm', 'sap', 'concur']
}

# Initialize empty DataFrames for each subset
subset_dfs = {key: pd.DataFrame(columns=['Text']) for key in keywords.keys()}

# Iterate through each row in df_1 and assign it to the appropriate subset
for index, row in df_1.iterrows():
    text = row['Text']
    for subset_name, subset_keywords in keywords.items():
        if any(keyword in text.lower() for keyword in subset_keywords):
            subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)

# Now, you have four subsets in separate DataFrames
df_1_email = subset_dfs['df_1_email']
df_2_rights = subset_dfs['df_2_rights']
df_3_computer = subset_dfs['df_3_computer']
df_4_software = subset_dfs['df_4_software']

# You can access and work with each subset as needed
print("df_1_email:")
print(df_1_email)

print("\ndf_2_rights:")
print(df_2_rights)

print("\ndf_3_computer:")
print(df_3_computer)

print("\ndf_4_software:")
print(df_4_software)


C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method 

df_1_email:
                                                  Text
0    CIAOPURTROPPO HANNO FATTO UN P CASINOPOTETE PE...
1    CIAO VOLEVO SAPERE SE RICEVIAMO ANCORA UNA NOT...
2    CIAO MANUEL GRAZIE SAREBBE POSSIBILE AVERE UNA...
3    CIAOPOSSIAMO PER FAVORE ASSEGNARE UNA LICENZA ...
4    HALLO BITTE MEINE EMAIL SIGNATUR VON TECHNOALP...
..                                                 ...
311                      153 359 970 PASSWORD BBKHGJUF
312  CIAO NO IN REALT MI SUCCEDE IN UFFICIO SENZA H...
313  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...
314  CIAO BIRGIT CI HA CREATO IL NUOVO INDIRIZZO MA...
315  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...

[316 rows x 1 columns]

df_2_rights:
                                                  Text
0    EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADG...
1    CIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   C...
2    BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO B...
3    THIS MORNING I SET THE NEW PASSWORD ON MY COMP...
4    CIAO MANUE

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\4151013874.py:20: FutureWarning: The frame.append method 

## df_1_email

In [33]:
import pandas as pd

words_to_check = ['message', 'mail', 'email', 'emails', 'account', 'sender', 'recipient',
                   'microsoft', 'outlook', 'password', 'attachments', 'send','licenza']
# Initialize an empty DataFrame to store the matching rows
df_1_email = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_email = df_1_email.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_email = df_1_email.reset_index(drop=True)

df_1_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[

Title  \
0                Receiving error message on Surface   
1                                           Outlook   
2                                      Mail history   
3    outlook is continuously closing automatically    
4    outlook is continuously closing automatically    
..                                              ...   
545                                     Licenze CRM   
546                                     Licenza CRM   
547                                     Licenza CRM   
548                                     Licenza CRM   
549                                     Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
545  {"16":"User identity management, Permissions, ...   
546  {"16":"User identity management, Permissions, ...   
547  {"16":"User identity management, Permissions, ...   
548  {"16":"User identity management, Permissions, ...   
549  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...   
1    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...   
2    HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022...   
3    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...   
4    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...   
..                                                 ...   
545  CIAOPOTREMMO PER FAVORE CAMBIARE LA LICENZA DI...   
546  CIAOPOTETE PER FAVORE ASSEGNARE A PATRICK SCHG...   
547  CIAOPOTETE PER FAVORE ASSEGNARE UNA LICENZA FU...   
548  CIAOPOTREMMO PER FAVORE ASSEGNARE A DIETMAR MA...   
549  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...   

                                                tokens  
0    [receiving, error, message, surface, opening, ...  
1    [karima, guerbaa, absent, until, september, 15...  
2     [would, like, retrieve, outlook, 2022, messages]  
3    [very, sorry, outlook, still, closing, its, ow...  
4    [very, sorry, outlook, still, closing, its, ow...  
..                                                 ...  
545  [ciaopotremmo, licenza, bill, wang, jason, wu,...  
546  [ciaopotete, schgaguler, licenza, member, crmi...  
547  [ciaopotete, licenza, full, crm, florian, mayr...  
548  [ciaopotremmo, dietmar, mair, licenza, memberg...  
549  [ciaopotremmo, licenza, werner, pixner, andrej...  

[550 rows x 4 columns]

In [34]:
df_1_email

Title  \
0                Receiving error message on Surface   
1                                           Outlook   
2                                      Mail history   
3    outlook is continuously closing automatically    
4    outlook is continuously closing automatically    
..                                              ...   
545                                     Licenze CRM   
546                                     Licenza CRM   
547                                     Licenza CRM   
548                                     Licenza CRM   
549                                     Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
545  {"16":"User identity management, Permissions, ...   
546  {"16":"User identity management, Permissions, ...   
547  {"16":"User identity management, Permissions, ...   
548  {"16":"User identity management, Permissions, ...   
549  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...   
1    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...   
2    HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022...   
3    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...   
4    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...   
..                                                 ...   
545  CIAOPOTREMMO PER FAVORE CAMBIARE LA LICENZA DI...   
546  CIAOPOTETE PER FAVORE ASSEGNARE A PATRICK SCHG...   
547  CIAOPOTETE PER FAVORE ASSEGNARE UNA LICENZA FU...   
548  CIAOPOTREMMO PER FAVORE ASSEGNARE A DIETMAR MA...   
549  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...   

                                                tokens  
0    [receiving, error, message, surface, opening, ...  
1    [karima, guerbaa, absent, until, september, 15...  
2     [would, like, retrieve, outlook, 2022, messages]  
3    [very, sorry, outlook, still, closing, its, ow...  
4    [very, sorry, outlook, still, closing, its, ow...  
..                                                 ...  
545  [ciaopotremmo, licenza, bill, wang, jason, wu,...  
546  [ciaopotete, schgaguler, licenza, member, crmi...  
547  [ciaopotete, licenza, full, crm, florian, mayr...  
548  [ciaopotremmo, dietmar, mair, licenza, memberg...  
549  [ciaopotremmo, licenza, werner, pixner, andrej...  

[550 rows x 4 columns]

In [35]:
df_1_email = df_1_email.drop(columns='tokens')
df_1_email

Title  \
0                Receiving error message on Surface   
1                                           Outlook   
2                                      Mail history   
3    outlook is continuously closing automatically    
4    outlook is continuously closing automatically    
..                                              ...   
545                                     Licenze CRM   
546                                     Licenza CRM   
547                                     Licenza CRM   
548                                     Licenza CRM   
549                                     Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
545  {"16":"User identity management, Permissions, ...   
546  {"16":"User identity management, Permissions, ...   
547  {"16":"User identity management, Permissions, ...   
548  {"16":"User identity management, Permissions, ...   
549  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...  
1    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...  
2    HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022...  
3    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...  
4    HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSIN...  
..                                                 ...  
545  CIAOPOTREMMO PER FAVORE CAMBIARE LA LICENZA DI...  
546  CIAOPOTETE PER FAVORE ASSEGNARE A PATRICK SCHG...  
547  CIAOPOTETE PER FAVORE ASSEGNARE UNA LICENZA FU...  
548  CIAOPOTREMMO PER FAVORE ASSEGNARE A DIETMAR MA...  
549  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...  

[550 rows x 3 columns]

# df_1_rights

In [36]:
#df_2_rights
import pandas as pd

words_to_check = ['badge', 'accedere', 'diritti', 'access', 'porte', 'mensa', 'accesso']
# Initialize an empty DataFrame to store the matching rows
df_1_rights = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_rights = df_1_rights.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_rights = df_1_rights.reset_index(drop=True)

df_1_rights

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.appe

Title  \
0    attivazione badge n. 10147 per nuova collabora...   
1                                       Martin Gajdos    
2                                 Autorizzazione Badge   
3                             Appartamento HQ Agostini   
4                            Badge n. 1031 Anja Höller   
..                                                 ...   
370  accesso a taiotmysqldb.mysql.database.azure.co...   
371                                  IT Admin for Engo   
372             Accesso a cartelle per Lorenzo Sartori   
373                                    PC Alyssa Klotz   
374                 Dare accesso di lettura a cartelle   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
370  {"16":"User identity management, Permissions, ...   
371  {"16":"User identity management, Permissions, ...   
372  {"16":"User identity management, Permissions, ...   
373  {"16":"User identity management, Permissions, ...   
374  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADG...   
1    CIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   C...   
2    BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO B...   
3    CIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV...   
4    CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO P...   
..                                                 ...   
370  LACCESSO AL MYSQL SERVER ESTERNO  BLOCCATO TAI...   
371  CIAO  MI HANNO ASSEGNATO IL SUPPORT DELLIT PER...   
372  BUONGIORNO CORTESEMENTE  POSSIBILE DARE ACCESS...   
373  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...   
374  BUONGIORNO VI CHIEDO DI DARE ACCESSO A DAVID M...   

                                                tokens  
0    [programmare, badge, 10147, segue, accesso, po...  
1    [badge, gajdos, stessi, accessi, altri, saldat...  
2    [avrei, abilitare, badge, accessi, autorizzazi...  
3    [abilitare, badge, nosal, miroslav, stano, jur...  
4    [aver, impostato, tutto, anjavolevo, avvisarvi...  
..                                                 ...  
370  [mysql, server, esterno, bloccato, taiotmysqld...  
371  [assegnato, support, dellit, engo, volevo, chi...  
372  [cortesemente, accesso, lettura, lorenzo, sart...  
373  [nell, ufficio, denver, c, pc, alyssa, sempre,...  
374  [accesso, david, mahlknecht, carlo, seguente, ...  

[375 rows x 4 columns]

In [37]:
df_1_rights

Title  \
0    attivazione badge n. 10147 per nuova collabora...   
1                                       Martin Gajdos    
2                                 Autorizzazione Badge   
3                             Appartamento HQ Agostini   
4                            Badge n. 1031 Anja Höller   
..                                                 ...   
370  accesso a taiotmysqldb.mysql.database.azure.co...   
371                                  IT Admin for Engo   
372             Accesso a cartelle per Lorenzo Sartori   
373                                    PC Alyssa Klotz   
374                 Dare accesso di lettura a cartelle   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
370  {"16":"User identity management, Permissions, ...   
371  {"16":"User identity management, Permissions, ...   
372  {"16":"User identity management, Permissions, ...   
373  {"16":"User identity management, Permissions, ...   
374  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADG...   
1    CIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   C...   
2    BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO B...   
3    CIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV...   
4    CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO P...   
..                                                 ...   
370  LACCESSO AL MYSQL SERVER ESTERNO  BLOCCATO TAI...   
371  CIAO  MI HANNO ASSEGNATO IL SUPPORT DELLIT PER...   
372  BUONGIORNO CORTESEMENTE  POSSIBILE DARE ACCESS...   
373  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...   
374  BUONGIORNO VI CHIEDO DI DARE ACCESSO A DAVID M...   

                                                tokens  
0    [programmare, badge, 10147, segue, accesso, po...  
1    [badge, gajdos, stessi, accessi, altri, saldat...  
2    [avrei, abilitare, badge, accessi, autorizzazi...  
3    [abilitare, badge, nosal, miroslav, stano, jur...  
4    [aver, impostato, tutto, anjavolevo, avvisarvi...  
..                                                 ...  
370  [mysql, server, esterno, bloccato, taiotmysqld...  
371  [assegnato, support, dellit, engo, volevo, chi...  
372  [cortesemente, accesso, lettura, lorenzo, sart...  
373  [nell, ufficio, denver, c, pc, alyssa, sempre,...  
374  [accesso, david, mahlknecht, carlo, seguente, ...  

[375 rows x 4 columns]

In [38]:
df_1_rights = df_1_rights.drop(columns='tokens')
df_1_rights

Title  \
0    attivazione badge n. 10147 per nuova collabora...   
1                                       Martin Gajdos    
2                                 Autorizzazione Badge   
3                             Appartamento HQ Agostini   
4                            Badge n. 1031 Anja Höller   
..                                                 ...   
370  accesso a taiotmysqldb.mysql.database.azure.co...   
371                                  IT Admin for Engo   
372             Accesso a cartelle per Lorenzo Sartori   
373                                    PC Alyssa Klotz   
374                 Dare accesso di lettura a cartelle   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
370  {"16":"User identity management, Permissions, ...   
371  {"16":"User identity management, Permissions, ...   
372  {"16":"User identity management, Permissions, ...   
373  {"16":"User identity management, Permissions, ...   
374  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADG...  
1    CIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   C...  
2    BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO B...  
3    CIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV...  
4    CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO P...  
..                                                 ...  
370  LACCESSO AL MYSQL SERVER ESTERNO  BLOCCATO TAI...  
371  CIAO  MI HANNO ASSEGNATO IL SUPPORT DELLIT PER...  
372  BUONGIORNO CORTESEMENTE  POSSIBILE DARE ACCESS...  
373  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...  
374  BUONGIORNO VI CHIEDO DI DARE ACCESSO A DAVID M...  

[375 rows x 3 columns]

# df_1_computer

In [39]:
#df_3_computer
import pandas as pd

words_to_check = ['pc', 'laptop', 'computer', 'phone', 'password']
# Initialize an empty DataFrame to store the matching rows
df_1_computer = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_computer = df_1_computer.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_computer = df_1_computer.reset_index(drop=True)

df_1_computer

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df

Title  \
0                            PASSWORD WINDOWS bloccato   
1                                            Signatura   
2    Intranet/Protime/abilitazione badge per produz...   
3                    New PC - Pb connexions to Servers   
4                                           SAP Concur   
..                                                 ...   
128                                    PC Alyssa Klotz   
129                                             Radix    
130                                      Email account   
131                               Problema invio mail    
132                                  TechnoAlpin Cloud   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
128  {"16":"User identity management, Permissions, ...   
129  {"16":"User identity management, Permissions, ...   
130  {"16":"User identity management, Permissions, ...   
131  {"16":"User identity management, Permissions, ...   
132  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...   
1    CIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUT...   
2    CIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRA...   
3    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...   
4    HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...   
..                                                 ...   
128  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...   
129  CIAO MI SERVIREBBE IL VOSTRO ADMIN PASSWORD PE...   
130  HI MANUEL CAU YOU PLEASE SEND ME THE PASSWORD ...   
131                      153 359 970 PASSWORD BBKHGJUF   
132  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...   

                                                tokens  
0    [penso, yu, yang, cambiato, password, tempo, e...  
1    [ciaomi, mia, signatura, nelloutlook, dopo, ca...  
2    [ragazzi, vorrei, accedere, rete, intranet, vi...  
3          [pc, cant, connect, servers, tafr, et, tab]  
4    [access, sapconcur, cant, login, because, forg...  
..                                                 ...  
128  [nell, ufficio, denver, c, pc, alyssa, sempre,...  
129  [servirebbe, vostro, admin, password, poter, i...  
130  [cau, send, password, monashitechnoalpincomtha...  
131                [153, 359, 970, password, bbkhgjuf]  
132  [selecting, reset, password, does, send, anyth...  

[133 rows x 4 columns]

In [40]:
df_1_computer

Title  \
0                            PASSWORD WINDOWS bloccato   
1                                            Signatura   
2    Intranet/Protime/abilitazione badge per produz...   
3                    New PC - Pb connexions to Servers   
4                                           SAP Concur   
..                                                 ...   
128                                    PC Alyssa Klotz   
129                                             Radix    
130                                      Email account   
131                               Problema invio mail    
132                                  TechnoAlpin Cloud   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
128  {"16":"User identity management, Permissions, ...   
129  {"16":"User identity management, Permissions, ...   
130  {"16":"User identity management, Permissions, ...   
131  {"16":"User identity management, Permissions, ...   
132  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...   
1    CIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUT...   
2    CIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRA...   
3    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...   
4    HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...   
..                                                 ...   
128  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...   
129  CIAO MI SERVIREBBE IL VOSTRO ADMIN PASSWORD PE...   
130  HI MANUEL CAU YOU PLEASE SEND ME THE PASSWORD ...   
131                      153 359 970 PASSWORD BBKHGJUF   
132  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...   

                                                tokens  
0    [penso, yu, yang, cambiato, password, tempo, e...  
1    [ciaomi, mia, signatura, nelloutlook, dopo, ca...  
2    [ragazzi, vorrei, accedere, rete, intranet, vi...  
3          [pc, cant, connect, servers, tafr, et, tab]  
4    [access, sapconcur, cant, login, because, forg...  
..                                                 ...  
128  [nell, ufficio, denver, c, pc, alyssa, sempre,...  
129  [servirebbe, vostro, admin, password, poter, i...  
130  [cau, send, password, monashitechnoalpincomtha...  
131                [153, 359, 970, password, bbkhgjuf]  
132  [selecting, reset, password, does, send, anyth...  

[133 rows x 4 columns]

In [41]:
df_1_computer = df_1_computer.drop(columns='tokens')
df_1_computer

Title  \
0                            PASSWORD WINDOWS bloccato   
1                                            Signatura   
2    Intranet/Protime/abilitazione badge per produz...   
3                    New PC - Pb connexions to Servers   
4                                           SAP Concur   
..                                                 ...   
128                                    PC Alyssa Klotz   
129                                             Radix    
130                                      Email account   
131                               Problema invio mail    
132                                  TechnoAlpin Cloud   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
128  {"16":"User identity management, Permissions, ...   
129  {"16":"User identity management, Permissions, ...   
130  {"16":"User identity management, Permissions, ...   
131  {"16":"User identity management, Permissions, ...   
132  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...  
1    CIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUT...  
2    CIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRA...  
3    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...  
4    HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...  
..                                                 ...  
128  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...  
129  CIAO MI SERVIREBBE IL VOSTRO ADMIN PASSWORD PE...  
130  HI MANUEL CAU YOU PLEASE SEND ME THE PASSWORD ...  
131                      153 359 970 PASSWORD BBKHGJUF  
132  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...  

[133 rows x 3 columns]

# df_1_software

In [42]:
#df_1_software
import pandas as pd

words_to_check = ['server', 'nav', 'vpn', 'crm', 'sap', 'concur']
# Initialize an empty DataFrame to store the matching rows
df_1_software = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_software = df_1_software.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_software = df_1_software.reset_index(drop=True)

df_1_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_s

Title  \
0                             L-server   
1                             L-server   
2    New PC - Pb connexions to Servers   
3                      Permission disk   
4      Uscita mail info@epowertrac.com   
..                                 ...   
164           Concur Andrej Mladenoski   
165                             Concur   
166           Conto user ANTOINE PAULY   
167  SAP Concur for Patrick Schgaguler   
168                  Sap Concur Login    

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
164  {"16":"User identity management, Permissions, ...   
165  {"16":"User identity management, Permissions, ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN ...   
1    OK ABER WIR KOENNEN NICHT SERVER FINDEN UND OF...   
2    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...   
3    CIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE ...   
4    DOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSI...   
..                                                 ...   
164  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...   
165  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...   
166  CIAO IL CONTO SAP CONCUR  STATO CREATO PER ANT...   
167  HI WE NOTED THAT THE ACCESS FOR SAP CONCUR FOR...   
168  CIAO MANUEL MI SPIACE DISTURBARTI MA TI CONFER...   

                                                tokens  
0    [koennen, lserver, installieren, fuer, neue, k...  
1              [aber, koennen, server, finden, offnen]  
2          [pc, cant, connect, servers, tafr, et, tab]  
3    [contattato, stephane, detto, dato, diritti, q...  
4    [dopo, cambiamento, server, mandare, email, da...  
..                                                 ...  
164  [impostare, lutente, andrej, mladenoski, utent...  
165  [dear, all, create, concur, account, employee,...  
166  [conto, sap, concur, stato, creato, antoine, p...  
167  [noted, access, sap, concur, our, newly, emplo...  
168  [spiace, disturbarti, confermo, password, micr...  

[169 rows x 4 columns]

In [43]:
df_1_software

Title  \
0                             L-server   
1                             L-server   
2    New PC - Pb connexions to Servers   
3                      Permission disk   
4      Uscita mail info@epowertrac.com   
..                                 ...   
164           Concur Andrej Mladenoski   
165                             Concur   
166           Conto user ANTOINE PAULY   
167  SAP Concur for Patrick Schgaguler   
168                  Sap Concur Login    

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
164  {"16":"User identity management, Permissions, ...   
165  {"16":"User identity management, Permissions, ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN ...   
1    OK ABER WIR KOENNEN NICHT SERVER FINDEN UND OF...   
2    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...   
3    CIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE ...   
4    DOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSI...   
..                                                 ...   
164  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...   
165  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...   
166  CIAO IL CONTO SAP CONCUR  STATO CREATO PER ANT...   
167  HI WE NOTED THAT THE ACCESS FOR SAP CONCUR FOR...   
168  CIAO MANUEL MI SPIACE DISTURBARTI MA TI CONFER...   

                                                tokens  
0    [koennen, lserver, installieren, fuer, neue, k...  
1              [aber, koennen, server, finden, offnen]  
2          [pc, cant, connect, servers, tafr, et, tab]  
3    [contattato, stephane, detto, dato, diritti, q...  
4    [dopo, cambiamento, server, mandare, email, da...  
..                                                 ...  
164  [impostare, lutente, andrej, mladenoski, utent...  
165  [dear, all, create, concur, account, employee,...  
166  [conto, sap, concur, stato, creato, antoine, p...  
167  [noted, access, sap, concur, our, newly, emplo...  
168  [spiace, disturbarti, confermo, password, micr...  

[169 rows x 4 columns]

In [44]:
df_1_software = df_1_software.drop(columns='tokens')
df_1_software

Title  \
0                             L-server   
1                             L-server   
2    New PC - Pb connexions to Servers   
3                      Permission disk   
4      Uscita mail info@epowertrac.com   
..                                 ...   
164           Concur Andrej Mladenoski   
165                             Concur   
166           Conto user ANTOINE PAULY   
167  SAP Concur for Patrick Schgaguler   
168                  Sap Concur Login    

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
164  {"16":"User identity management, Permissions, ...   
165  {"16":"User identity management, Permissions, ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN ...  
1    OK ABER WIR KOENNEN NICHT SERVER FINDEN UND OF...  
2    I HAVE A NEW PC BUT I CANT CONNECT SERVERS TAF...  
3    CIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE ...  
4    DOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSI...  
..                                                 ...  
164  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...  
165  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...  
166  CIAO IL CONTO SAP CONCUR  STATO CREATO PER ANT...  
167  HI WE NOTED THAT THE ACCESS FOR SAP CONCUR FOR...  
168  CIAO MANUEL MI SPIACE DISTURBARTI MA TI CONFER...  

[169 rows x 3 columns]

# df_2
{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}

In [45]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella', 'problem', 'poi', 'digitale','also','du', 'problema', 'io', 
                    'es', 'here', 'pdf', 'devo', 'as','marco','41', 'provato', 'install', 
                    'tutto', 'eine','va', 'sempre', 'open','work','do','programma','one']

# Tokenize and remove stopwords from the 'Text' column
df_2['tokens'] = df_2['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_2['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('pc', 59), ('email', 57), ('outlook', 54), ('teams', 44), ('installare', 40), ('pw', 34), ('mail', 33), ('nav', 32), ('laptop', 31), ('password', 29), ('office', 25), ('computer', 24), ('accedere', 23), ('citrix', 23), ('vpn', 22), ('accesso', 21), ('message', 20), ('prfprotokoll', 19), ('vdi', 18), ('server', 18), ('passwort', 17), ('microsoft', 17), ('acrobat', 17), ('edge', 16), ('app', 15), ('emails', 15), ('vedo', 14), ('account', 14), ('messaggio', 14), ('br', 14)]


# df_2_pc

In [46]:
#df_2_pc
import pandas as pd

words_to_check = ['pc', 'computer', 'accedere', 'pw', 'password',
                  'laptop', 'passwort', 'pwd', 'login', 'accesso']

# Initialize an empty DataFrame to store the matching rows
df_2_pc = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_pc = df_2_pc.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_pc = df_2_pc.reset_index(drop=True)

df_2_pc

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\Mat

Title  \
0                                       VPN & Navision   
1                                 Probleme mit Procall   
2                                             Navision   
3       Update a Windows 10 urgente (Win 7 installato)   
4                             problemi linceza Mapedit   
..                                                 ...   
272                 Accesso servse licenza Codewarrior   
273        Accesso VPN e verifica collegamenti disco L   
274  Accesso http://web01/erticket/scp/login.php pe...   
275       Installare accesso VPN/CITRIX sul mio Laptop   
276                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
272  {"12":"Standard Software: Operating systems, M...   
273  {"12":"Standard Software: Operating systems, M...   
274  {"12":"Standard Software: Operating systems, M...   
275  {"12":"Standard Software: Operating systems, M...   
276  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...   
1    HALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEI...   
2    HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTR...   
3    SERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN ...   
4    CIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC E...   
..                                                 ...   
272  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...   
273  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...   
274  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...   
275  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...   
276  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...   

                                                tokens  
0    [installare, dynamics, nav, pc, vpn, accedere,...  
1    [nach, einem, neustart, meines, pc, scheint, p...  
2             [pc, nav, italie, austria, doesnt, best]  
3    [servirebbe, linstallazione, windows, 10, pc, ...  
4    [arashdeep, scusami, riavviato, pc, ed, ora, b...  
..                                                 ...  
272  [stesso, segnalato, risolto, gennaio, febbraio...  
273  [necessito, configurare, laptop, allaccesso, t...  
274  [chiedere, voi, ticketing, system, technoalpin...  
275  [installare, accesso, vpncitrix, laptop, urgen...  
276  [ciaomi, radix, citrix, seguente, utente, patr...  

[277 rows x 4 columns]

In [47]:
df_2_pc

Title  \
0                                       VPN & Navision   
1                                 Probleme mit Procall   
2                                             Navision   
3       Update a Windows 10 urgente (Win 7 installato)   
4                             problemi linceza Mapedit   
..                                                 ...   
272                 Accesso servse licenza Codewarrior   
273        Accesso VPN e verifica collegamenti disco L   
274  Accesso http://web01/erticket/scp/login.php pe...   
275       Installare accesso VPN/CITRIX sul mio Laptop   
276                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
272  {"12":"Standard Software: Operating systems, M...   
273  {"12":"Standard Software: Operating systems, M...   
274  {"12":"Standard Software: Operating systems, M...   
275  {"12":"Standard Software: Operating systems, M...   
276  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...   
1    HALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEI...   
2    HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTR...   
3    SERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN ...   
4    CIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC E...   
..                                                 ...   
272  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...   
273  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...   
274  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...   
275  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...   
276  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...   

                                                tokens  
0    [installare, dynamics, nav, pc, vpn, accedere,...  
1    [nach, einem, neustart, meines, pc, scheint, p...  
2             [pc, nav, italie, austria, doesnt, best]  
3    [servirebbe, linstallazione, windows, 10, pc, ...  
4    [arashdeep, scusami, riavviato, pc, ed, ora, b...  
..                                                 ...  
272  [stesso, segnalato, risolto, gennaio, febbraio...  
273  [necessito, configurare, laptop, allaccesso, t...  
274  [chiedere, voi, ticketing, system, technoalpin...  
275  [installare, accesso, vpncitrix, laptop, urgen...  
276  [ciaomi, radix, citrix, seguente, utente, patr...  

[277 rows x 4 columns]

In [48]:
df_2_pc = df_2_pc.drop(columns='tokens')
df_2_pc

Title  \
0                                       VPN & Navision   
1                                 Probleme mit Procall   
2                                             Navision   
3       Update a Windows 10 urgente (Win 7 installato)   
4                             problemi linceza Mapedit   
..                                                 ...   
272                 Accesso servse licenza Codewarrior   
273        Accesso VPN e verifica collegamenti disco L   
274  Accesso http://web01/erticket/scp/login.php pe...   
275       Installare accesso VPN/CITRIX sul mio Laptop   
276                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
272  {"12":"Standard Software: Operating systems, M...   
273  {"12":"Standard Software: Operating systems, M...   
274  {"12":"Standard Software: Operating systems, M...   
275  {"12":"Standard Software: Operating systems, M...   
276  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...  
1    HALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEI...  
2    HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTR...  
3    SERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN ...  
4    CIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC E...  
..                                                 ...  
272  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...  
273  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...  
274  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...  
275  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...  
276  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...  

[277 rows x 3 columns]

# df_2_email

In [49]:
#df_2_email
import pandas as pd

words_to_check = ['message', 'email', 'outlook', 'emails', 
                  'mail', 'accedere', 'pw', 'password', 'passwort', 
                  'recipient', 'attachments', 'pwd', 'microsoft', 'office', 'app', 'login', 'accesso']


# Initialize an empty DataFrame to store the matching rows
df_2_email = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_email = df_2_email.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_email = df_2_email.reset_index(drop=True)

df_2_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word

Title  \
0                                    WG: Fehlermeldung   
1                     Virtual Machine can`t be started   
2    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
3                                        Outlook issue   
4    Linda Zhang - Excel is not working over Citrix...   
..                                                 ...   
462                 Accesso servse licenza Codewarrior   
463        Accesso VPN e verifica collegamenti disco L   
464  Accesso http://web01/erticket/scp/login.php pe...   
465       Installare accesso VPN/CITRIX sul mio Laptop   
466                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
462  {"12":"Standard Software: Operating systems, M...   
463  {"12":"Standard Software: Operating systems, M...   
464  {"12":"Standard Software: Operating systems, M...   
465  {"12":"Standard Software: Operating systems, M...   
466  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...   
1    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...   
2     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...   
3    HELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ...   
4    CIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN...   
..                                                 ...   
462  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...   
463  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...   
464  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...   
465  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...   
466  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...   

                                                tokens  
0    [absender, whitelist, setzen, wichtig, fehlerm...  
1    [press, cirtix, remote, desktop, symbol, conne...  
2    [ultimamente, abbiamo, problemi, grossi, mail,...  
3    [helloafter, changed, password, cant, connect,...  
4    [linda, zhang, accessing, italian, system, cit...  
..                                                 ...  
462  [stesso, segnalato, risolto, gennaio, febbraio...  
463  [necessito, configurare, laptop, allaccesso, t...  
464  [chiedere, voi, ticketing, system, technoalpin...  
465  [installare, accesso, vpncitrix, laptop, urgen...  
466  [ciaomi, radix, citrix, seguente, utente, patr...  

[467 rows x 4 columns]

In [50]:
df_2_email

Title  \
0                                    WG: Fehlermeldung   
1                     Virtual Machine can`t be started   
2    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
3                                        Outlook issue   
4    Linda Zhang - Excel is not working over Citrix...   
..                                                 ...   
462                 Accesso servse licenza Codewarrior   
463        Accesso VPN e verifica collegamenti disco L   
464  Accesso http://web01/erticket/scp/login.php pe...   
465       Installare accesso VPN/CITRIX sul mio Laptop   
466                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
462  {"12":"Standard Software: Operating systems, M...   
463  {"12":"Standard Software: Operating systems, M...   
464  {"12":"Standard Software: Operating systems, M...   
465  {"12":"Standard Software: Operating systems, M...   
466  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...   
1    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...   
2     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...   
3    HELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ...   
4    CIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN...   
..                                                 ...   
462  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...   
463  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...   
464  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...   
465  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...   
466  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...   

                                                tokens  
0    [absender, whitelist, setzen, wichtig, fehlerm...  
1    [press, cirtix, remote, desktop, symbol, conne...  
2    [ultimamente, abbiamo, problemi, grossi, mail,...  
3    [helloafter, changed, password, cant, connect,...  
4    [linda, zhang, accessing, italian, system, cit...  
..                                                 ...  
462  [stesso, segnalato, risolto, gennaio, febbraio...  
463  [necessito, configurare, laptop, allaccesso, t...  
464  [chiedere, voi, ticketing, system, technoalpin...  
465  [installare, accesso, vpncitrix, laptop, urgen...  
466  [ciaomi, radix, citrix, seguente, utente, patr...  

[467 rows x 4 columns]

In [51]:
df_2_email = df_2_email.drop(columns = 'tokens')
df_2_email

Title  \
0                                    WG: Fehlermeldung   
1                     Virtual Machine can`t be started   
2    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
3                                        Outlook issue   
4    Linda Zhang - Excel is not working over Citrix...   
..                                                 ...   
462                 Accesso servse licenza Codewarrior   
463        Accesso VPN e verifica collegamenti disco L   
464  Accesso http://web01/erticket/scp/login.php pe...   
465       Installare accesso VPN/CITRIX sul mio Laptop   
466                       nuovo accesi radix su citrix   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
462  {"12":"Standard Software: Operating systems, M...   
463  {"12":"Standard Software: Operating systems, M...   
464  {"12":"Standard Software: Operating systems, M...   
465  {"12":"Standard Software: Operating systems, M...   
466  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...  
1    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...  
2     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...  
3    HELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ...  
4    CIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN...  
..                                                 ...  
462  STESSO PROBLEMA SEGNALATO E RISOLTO A GENNAIO ...  
463  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...  
464  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...  
465  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...  
466  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...  

[467 rows x 3 columns]

# df_2_access

In [52]:
#df_2_access
import pandas as pd

words_to_check = ['teams', 'login', 'accesso', 'accedere', 'pw', 'password']


# Initialize an empty DataFrame to store the matching rows
df_2_access = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_access = df_2_access.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_access = df_2_access.reset_index(drop=True)

df_2_access

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(d

Title  \
0    Outlook  Termine erstellen TEams   
1     Collegamento MS TEAMS e OUTLOOK   
2             MSTeams - Guest contact   
3         Camera non funziona da casa   
4              Blocco Outlook e Teams   
..                                ...   
187             Downloading adobe pro   
188  ONE DRIVE TECHNOALPIN EPOWERTRAC   
189                    Setup nuovo PC   
190                    Update Windows   
191                           Mapedit   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
187  {"12":"Standard Software: Operating systems, M...   
188  {"12":"Standard Software: Operating systems, M...   
189  {"12":"Standard Software: Operating systems, M...   
190  {"12":"Standard Software: Operating systems, M...   
191  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...   
1    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...   
2    CIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER I...   
3    CIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA C...   
4    BUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO...   
..                                                 ...   
187  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...   
188  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...   
189  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...   
190  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...   
191  CAN YOU ALSO GIVE ME SIGNING DETAILS USERNAME ...   

                                                tokens  
0    [vedo, piu, link, teams, meeting, creo, appunt...  
1    [collegamento, tra, programmi, sopracitati, fi...  
2    [nostro, partner, finlandia, manu, laari, manu...  
3    [qualche, settimana, camera, computer, home, o...  
4    [presente, outlook, teams, compare, messaggio,...  
..                                                 ...  
187  [trying, adobe, pro, will, let, had, old, inst...  
188  [accesso, vedo, 10, cartelle, drive, epowertra...  
189  [lid, rimane, password, aveva, timeout, qui, q...  
190  [update, windows, viewer, 545, 489, 361passwor...  
191       [give, signing, details, username, password]  

[192 rows x 4 columns]

In [53]:
df_2_access

Title  \
0    Outlook  Termine erstellen TEams   
1     Collegamento MS TEAMS e OUTLOOK   
2             MSTeams - Guest contact   
3         Camera non funziona da casa   
4              Blocco Outlook e Teams   
..                                ...   
187             Downloading adobe pro   
188  ONE DRIVE TECHNOALPIN EPOWERTRAC   
189                    Setup nuovo PC   
190                    Update Windows   
191                           Mapedit   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
187  {"12":"Standard Software: Operating systems, M...   
188  {"12":"Standard Software: Operating systems, M...   
189  {"12":"Standard Software: Operating systems, M...   
190  {"12":"Standard Software: Operating systems, M...   
191  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...   
1    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...   
2    CIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER I...   
3    CIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA C...   
4    BUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO...   
..                                                 ...   
187  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...   
188  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...   
189  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...   
190  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...   
191  CAN YOU ALSO GIVE ME SIGNING DETAILS USERNAME ...   

                                                tokens  
0    [vedo, piu, link, teams, meeting, creo, appunt...  
1    [collegamento, tra, programmi, sopracitati, fi...  
2    [nostro, partner, finlandia, manu, laari, manu...  
3    [qualche, settimana, camera, computer, home, o...  
4    [presente, outlook, teams, compare, messaggio,...  
..                                                 ...  
187  [trying, adobe, pro, will, let, had, old, inst...  
188  [accesso, vedo, 10, cartelle, drive, epowertra...  
189  [lid, rimane, password, aveva, timeout, qui, q...  
190  [update, windows, viewer, 545, 489, 361passwor...  
191       [give, signing, details, username, password]  

[192 rows x 4 columns]

In [54]:
df_2_access = df_2_access.drop(columns = 'tokens')
df_2_access

Title  \
0    Outlook  Termine erstellen TEams   
1     Collegamento MS TEAMS e OUTLOOK   
2             MSTeams - Guest contact   
3         Camera non funziona da casa   
4              Blocco Outlook e Teams   
..                                ...   
187             Downloading adobe pro   
188  ONE DRIVE TECHNOALPIN EPOWERTRAC   
189                    Setup nuovo PC   
190                    Update Windows   
191                           Mapedit   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
187  {"12":"Standard Software: Operating systems, M...   
188  {"12":"Standard Software: Operating systems, M...   
189  {"12":"Standard Software: Operating systems, M...   
190  {"12":"Standard Software: Operating systems, M...   
191  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...  
1    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...  
2    CIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER I...  
3    CIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA C...  
4    BUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO...  
..                                                 ...  
187  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...  
188  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...  
189  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...  
190  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...  
191  CAN YOU ALSO GIVE ME SIGNING DETAILS USERNAME ...  

[192 rows x 3 columns]

# df_2_software

In [55]:
#df_2_software
import pandas as pd

words_to_check = ['installare', 'nav', 'citrix', 'vpn', 'edge', 'acrobat', 'prfprotokoll', 'vdi', 'server']

# Initialize an empty DataFrame to store the matching rows
df_2_software = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_software = df_2_software.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_software = df_2_software.reset_index(drop=True)

df_2_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df

Title  \
0                             Office365 x C255   
1                               VPN & Navision   
2                Please install Solid Edge SP7   
3     ACROBAT READER 64-bit per deploy #140129   
4    installazione profile e creazione account   
..                                         ...   
205                   Aggiornamento Docfinance   
206          Indirizzo E-Mail per l'utente NDF   
207          Indirizzo E-Mail per l'utente NDF   
208                  Unable to log in on mail.   
209          Excel per Server profile-app-prod   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
205  {"12":"Standard Software: Operating systems, M...   
206  {"12":"Standard Software: Operating systems, M...   
207  {"12":"Standard Software: Operating systems, M...   
208  {"12":"Standard Software: Operating systems, M...   
209  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...   
1    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...   
2    CIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO S...   
3    CIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT ...   
4    CIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  I...   
..                                                 ...   
205  CIAO LA MIGRAZIONE SUL NUOVO SERVER SEMBRA AND...   
206  VOGLIAMO CHE LNDF CI MANDA UN EMAIL NEL CASO Q...   
207  SERVONO PER UN SERVIZIO DI TRISOFT CHE DEVE MA...   
208  OUR SERVICE TECHNICAN IS UNABLE TO RECIVE MAIL...   
209  CI SERVIREBBE EXCEL SUL SERVER PROFILEAPPPROD ...   

                                                tokens  
0    [installare, word, excel, ed, outlook, macchin...  
1    [installare, dynamics, nav, pc, vpn, accedere,...  
2    [ciaomi, installare, pack, solid, edge, sp7gra...  
3    [riapro, questione, acrobat, reader, 64bit, im...  
4    [discusso, voce, department, installare, softw...  
..                                                 ...  
205  [migrazione, server, sembra, andata, bene, err...  
206  [vogliamo, lndf, manda, email, caso, problemi,...  
207  [servono, servizio, trisoft, deve, mandare, em...  
208  [our, technican, unable, recive, mail, his, la...  
209        [servirebbe, excel, server, profileappprod]  

[210 rows x 4 columns]

In [56]:
df_2_software

Title  \
0                             Office365 x C255   
1                               VPN & Navision   
2                Please install Solid Edge SP7   
3     ACROBAT READER 64-bit per deploy #140129   
4    installazione profile e creazione account   
..                                         ...   
205                   Aggiornamento Docfinance   
206          Indirizzo E-Mail per l'utente NDF   
207          Indirizzo E-Mail per l'utente NDF   
208                  Unable to log in on mail.   
209          Excel per Server profile-app-prod   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
205  {"12":"Standard Software: Operating systems, M...   
206  {"12":"Standard Software: Operating systems, M...   
207  {"12":"Standard Software: Operating systems, M...   
208  {"12":"Standard Software: Operating systems, M...   
209  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...   
1    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...   
2    CIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO S...   
3    CIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT ...   
4    CIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  I...   
..                                                 ...   
205  CIAO LA MIGRAZIONE SUL NUOVO SERVER SEMBRA AND...   
206  VOGLIAMO CHE LNDF CI MANDA UN EMAIL NEL CASO Q...   
207  SERVONO PER UN SERVIZIO DI TRISOFT CHE DEVE MA...   
208  OUR SERVICE TECHNICAN IS UNABLE TO RECIVE MAIL...   
209  CI SERVIREBBE EXCEL SUL SERVER PROFILEAPPPROD ...   

                                                tokens  
0    [installare, word, excel, ed, outlook, macchin...  
1    [installare, dynamics, nav, pc, vpn, accedere,...  
2    [ciaomi, installare, pack, solid, edge, sp7gra...  
3    [riapro, questione, acrobat, reader, 64bit, im...  
4    [discusso, voce, department, installare, softw...  
..                                                 ...  
205  [migrazione, server, sembra, andata, bene, err...  
206  [vogliamo, lndf, manda, email, caso, problemi,...  
207  [servono, servizio, trisoft, deve, mandare, em...  
208  [our, technican, unable, recive, mail, his, la...  
209        [servirebbe, excel, server, profileappprod]  

[210 rows x 4 columns]

In [57]:
df_2_software = df_2_software.drop(columns = 'tokens')
df_2_software

Title  \
0                             Office365 x C255   
1                               VPN & Navision   
2                Please install Solid Edge SP7   
3     ACROBAT READER 64-bit per deploy #140129   
4    installazione profile e creazione account   
..                                         ...   
205                   Aggiornamento Docfinance   
206          Indirizzo E-Mail per l'utente NDF   
207          Indirizzo E-Mail per l'utente NDF   
208                  Unable to log in on mail.   
209          Excel per Server profile-app-prod   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
205  {"12":"Standard Software: Operating systems, M...   
206  {"12":"Standard Software: Operating systems, M...   
207  {"12":"Standard Software: Operating systems, M...   
208  {"12":"Standard Software: Operating systems, M...   
209  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...  
1    CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC...  
2    CIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO S...  
3    CIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT ...  
4    CIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  I...  
..                                                 ...  
205  CIAO LA MIGRAZIONE SUL NUOVO SERVER SEMBRA AND...  
206  VOGLIAMO CHE LNDF CI MANDA UN EMAIL NEL CASO Q...  
207  SERVONO PER UN SERVIZIO DI TRISOFT CHE DEVE MA...  
208  OUR SERVICE TECHNICAN IS UNABLE TO RECIVE MAIL...  
209  CI SERVIREBBE EXCEL SUL SERVER PROFILEAPPPROD ...  

[210 rows x 3 columns]

# df_3
{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}

In [58]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella', 'problem', 'poi', 'digitale','also','du', 'problema', 'io', 
                    'es', 'here', 'pdf', 'devo', 'as','marco','41', 'provato', 'install', 
                    'tutto', 'eine','va', 'sempre', 'open','work','do','programma','one', 
                    'verificare','message','installato', '3306', 'high','ufficio', 'problemi', 
                    'uno','prone','t41', 'netprodclientsofficewlan','abbiamo', 'avere', 
                    'vulnerability', 'fa', 'francesco', 'sarebbe', 'installare', 'purtroppo', 'avete',
                    '75', 'fatto', 'multiple', 'dos', 'funktioniert','vecchio', 'domani','qualche',
                    'numero', 'piu', 'volta']

# Tokenize and remove stopwords from the 'Text' column
df_3['tokens'] = df_3['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_3['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('stampante', 105), ('laptop', 100), ('pc', 93), ('telefono', 45), ('docking', 44), ('stampare', 33), ('station', 30), ('monitor', 30), ('printer', 30), ('drucker', 28), ('fisso', 27), ('rete', 27), ('zebra', 25), ('cavo', 24), ('computer', 24), ('stampa', 22), ('schermo', 21), ('tastiera', 20), ('software', 20), ('pw', 20), ('mia', 18), ('cellulare', 18), ('usb', 18), ('mail', 18), ('password', 18), ('ein', 18), ('office', 18), ('possiamo', 18), ('ogni', 18), ('secondo', 17)]


# df_3_printer

In [59]:
#df_3_printer
import pandas as pd

words_to_check = ['stampante', 'stampare', 'printer', 'drucker', 'zebra', 'stampa']

# Initialize an empty DataFrame to store the matching rows
df_3_printer = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_printer = df_3_printer.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_printer = df_3_printer.reset_index(drop=True)

df_3_printer

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.

Title  \
0                  Stampante uffico contabilita´   
1                                      Stampante   
2                             stampante bloccata   
3          stampante service secondo piano sopra   
4                     Stampante zebra non stampa   
..                                           ...   
328  Problema accesso cartella \\Controller-TX30   
329        Installation SECURE PRINTER (GANG VK)   
330                                    Stampante   
331           RE: Ticket #513035 Assigned to you   
332                       stampante non funziona   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
328  {"11":"Hardware, Telephony, Smartphones, Monit...   
329  {"11":"Hardware, Telephony, Smartphones, Monit...   
330  {"11":"Hardware, Telephony, Smartphones, Monit...   
331  {"11":"Hardware, Telephony, Smartphones, Monit...   
332  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZI...   
1    CIAO MI POETE COLLEGARE PER FAVORE QUESTA STAM...   
2    CIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BL...   
3    LA STAMPANTE SERVICE SECONDO PIANO NON ULTIMA ...   
4               STAMPANTE ZEBRA NON STAMPA DA NAVISION   
..                                                 ...   
328  CIAO A TUTTI NON RIUSCIAMO AD ACCEDERE ALLA CA...   
329  CIAO PREGO INSTALLARE LA POSSIBILITA DI STAMPA...   
330     CIAO LA STAMPANTE HP2891F8 NON FUNZIONA GRAZIE   
331   CIAO   BASTA CHE RIAVVIA IL PC DA DOVE VUOLE ...   
332  CIAO FRANCESCO LA STAMPANTE DI ERNESTO ANCORA ...   

                                                tokens  
0    [stampante, nostro, venuto, fuori, manca, cart...  
1                        [poete, collegare, stampante]  
2    [stampante, verkauf, pcv, prtserv01, bloccata,...  
3    [stampante, secondo, piano, ultima, lavori, d,...  
4                 [stampante, zebra, stampa, navision]  
..                                                 ...  
328  [riusciamo, accedere, controllertx30, quindi, ...  
329  [possibilita, stampare, secure, printer, secon...  
330                              [stampante, hp2891f8]  
331  [basta, riavvia, pc, dove, vuole, stampare, za...  
332              [stampante, ernesto, rimane, offline]  

[333 rows x 4 columns]

In [60]:
df_3_printer

Title  \
0                  Stampante uffico contabilita´   
1                                      Stampante   
2                             stampante bloccata   
3          stampante service secondo piano sopra   
4                     Stampante zebra non stampa   
..                                           ...   
328  Problema accesso cartella \\Controller-TX30   
329        Installation SECURE PRINTER (GANG VK)   
330                                    Stampante   
331           RE: Ticket #513035 Assigned to you   
332                       stampante non funziona   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
328  {"11":"Hardware, Telephony, Smartphones, Monit...   
329  {"11":"Hardware, Telephony, Smartphones, Monit...   
330  {"11":"Hardware, Telephony, Smartphones, Monit...   
331  {"11":"Hardware, Telephony, Smartphones, Monit...   
332  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZI...   
1    CIAO MI POETE COLLEGARE PER FAVORE QUESTA STAM...   
2    CIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BL...   
3    LA STAMPANTE SERVICE SECONDO PIANO NON ULTIMA ...   
4               STAMPANTE ZEBRA NON STAMPA DA NAVISION   
..                                                 ...   
328  CIAO A TUTTI NON RIUSCIAMO AD ACCEDERE ALLA CA...   
329  CIAO PREGO INSTALLARE LA POSSIBILITA DI STAMPA...   
330     CIAO LA STAMPANTE HP2891F8 NON FUNZIONA GRAZIE   
331   CIAO   BASTA CHE RIAVVIA IL PC DA DOVE VUOLE ...   
332  CIAO FRANCESCO LA STAMPANTE DI ERNESTO ANCORA ...   

                                                tokens  
0    [stampante, nostro, venuto, fuori, manca, cart...  
1                        [poete, collegare, stampante]  
2    [stampante, verkauf, pcv, prtserv01, bloccata,...  
3    [stampante, secondo, piano, ultima, lavori, d,...  
4                 [stampante, zebra, stampa, navision]  
..                                                 ...  
328  [riusciamo, accedere, controllertx30, quindi, ...  
329  [possibilita, stampare, secure, printer, secon...  
330                              [stampante, hp2891f8]  
331  [basta, riavvia, pc, dove, vuole, stampare, za...  
332              [stampante, ernesto, rimane, offline]  

[333 rows x 4 columns]

In [61]:
df_3_printer = df_3_printer.drop(columns = 'tokens')
df_3_printer

Title  \
0                  Stampante uffico contabilita´   
1                                      Stampante   
2                             stampante bloccata   
3          stampante service secondo piano sopra   
4                     Stampante zebra non stampa   
..                                           ...   
328  Problema accesso cartella \\Controller-TX30   
329        Installation SECURE PRINTER (GANG VK)   
330                                    Stampante   
331           RE: Ticket #513035 Assigned to you   
332                       stampante non funziona   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
328  {"11":"Hardware, Telephony, Smartphones, Monit...   
329  {"11":"Hardware, Telephony, Smartphones, Monit...   
330  {"11":"Hardware, Telephony, Smartphones, Monit...   
331  {"11":"Hardware, Telephony, Smartphones, Monit...   
332  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZI...  
1    CIAO MI POETE COLLEGARE PER FAVORE QUESTA STAM...  
2    CIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BL...  
3    LA STAMPANTE SERVICE SECONDO PIANO NON ULTIMA ...  
4               STAMPANTE ZEBRA NON STAMPA DA NAVISION  
..                                                 ...  
328  CIAO A TUTTI NON RIUSCIAMO AD ACCEDERE ALLA CA...  
329  CIAO PREGO INSTALLARE LA POSSIBILITA DI STAMPA...  
330     CIAO LA STAMPANTE HP2891F8 NON FUNZIONA GRAZIE  
331   CIAO   BASTA CHE RIAVVIA IL PC DA DOVE VUOLE ...  
332  CIAO FRANCESCO LA STAMPANTE DI ERNESTO ANCORA ...  

[333 rows x 3 columns]

# df_3_docking

In [62]:
#df_3_docking
import pandas as pd
words_to_check = ['docking', 'cavo', 'rete', 'lan', 'station']

# Initialize an empty DataFrame to store the matching rows
df_3_docking = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_docking = df_3_docking.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_docking = df_3_docking.reset_index(drop=True)

df_3_docking

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.

Title  \
0                                  Adapter USB per LAN   
1                                      Docking station   
2                                               Laptop   
3    spostamento ufficio Michele Valbusa + inserime...   
4                                      Screen blackout   
..                                                 ...   
160                                         new laptop   
161      Collegamento Docking station mDP non funziona   
162      Collegamento Docking station mDP non funziona   
163         Docking Station non funziona correttamente   
164                                    Nuovo posto PLC   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
160  {"11":"Hardware, Telephony, Smartphones, Monit...   
161  {"11":"Hardware, Telephony, Smartphones, Monit...   
162  {"11":"Hardware, Telephony, Smartphones, Monit...   
163  {"11":"Hardware, Telephony, Smartphones, Monit...   
164  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN...   
1    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...   
2    BUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO C...   
3    BUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409...   
4    HELLO  IM HERE TO ASK YOU ABOUT A THING THAT H...   
..                                                 ...   
160  DATI TEAMVIEWER 1726129643 X85I1W2T  COSE DA I...   
161  BUONGIORNO IL COLLEGAMENTO TRA LAPTOPDOCKING S...   
162  CIAO HO CONTROLLATO LA DOCKING STATION PURTROP...   
163  QUANDO ACCENDO IL PC LA DOCKING STATION NON MI...   
164  CIAO MI POTETE INSTALLARE DOMANI PER STEFANIE ...   

                                                tokens  
0    [manca, adattatore, usb, lan, ne, dovrei, riti...  
1    [mattina, comunicazione, tra, docking, station...  
2    [vorrei, sostituire, pc, fisso, portatile, doc...  
3    [larrivo, teresa, buffa, 0409, spostarmi, sar,...  
4    [ask, about, thing, happened, morning, went, o...  
..                                                 ...  
160  [dati, 1726129643, x85i1w2t, cose, impostare, ...  
161  [collegamento, tra, laptopdocking, station, mo...  
162  [controllato, docking, station, dopo, laggiorn...  
163  [accendo, pc, docking, station, andare, tastie...  
164  [stefanie, gummerer, seguente, cosa, deskop, g...  

[165 rows x 4 columns]

In [63]:
df_3_docking

Title  \
0                                  Adapter USB per LAN   
1                                      Docking station   
2                                               Laptop   
3    spostamento ufficio Michele Valbusa + inserime...   
4                                      Screen blackout   
..                                                 ...   
160                                         new laptop   
161      Collegamento Docking station mDP non funziona   
162      Collegamento Docking station mDP non funziona   
163         Docking Station non funziona correttamente   
164                                    Nuovo posto PLC   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
160  {"11":"Hardware, Telephony, Smartphones, Monit...   
161  {"11":"Hardware, Telephony, Smartphones, Monit...   
162  {"11":"Hardware, Telephony, Smartphones, Monit...   
163  {"11":"Hardware, Telephony, Smartphones, Monit...   
164  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN...   
1    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...   
2    BUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO C...   
3    BUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409...   
4    HELLO  IM HERE TO ASK YOU ABOUT A THING THAT H...   
..                                                 ...   
160  DATI TEAMVIEWER 1726129643 X85I1W2T  COSE DA I...   
161  BUONGIORNO IL COLLEGAMENTO TRA LAPTOPDOCKING S...   
162  CIAO HO CONTROLLATO LA DOCKING STATION PURTROP...   
163  QUANDO ACCENDO IL PC LA DOCKING STATION NON MI...   
164  CIAO MI POTETE INSTALLARE DOMANI PER STEFANIE ...   

                                                tokens  
0    [manca, adattatore, usb, lan, ne, dovrei, riti...  
1    [mattina, comunicazione, tra, docking, station...  
2    [vorrei, sostituire, pc, fisso, portatile, doc...  
3    [larrivo, teresa, buffa, 0409, spostarmi, sar,...  
4    [ask, about, thing, happened, morning, went, o...  
..                                                 ...  
160  [dati, 1726129643, x85i1w2t, cose, impostare, ...  
161  [collegamento, tra, laptopdocking, station, mo...  
162  [controllato, docking, station, dopo, laggiorn...  
163  [accendo, pc, docking, station, andare, tastie...  
164  [stefanie, gummerer, seguente, cosa, deskop, g...  

[165 rows x 4 columns]

In [64]:
df_3_docking = df_3_docking.drop(columns = 'tokens')
df_3_docking

Title  \
0                                  Adapter USB per LAN   
1                                      Docking station   
2                                               Laptop   
3    spostamento ufficio Michele Valbusa + inserime...   
4                                      Screen blackout   
..                                                 ...   
160                                         new laptop   
161      Collegamento Docking station mDP non funziona   
162      Collegamento Docking station mDP non funziona   
163         Docking Station non funziona correttamente   
164                                    Nuovo posto PLC   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
160  {"11":"Hardware, Telephony, Smartphones, Monit...   
161  {"11":"Hardware, Telephony, Smartphones, Monit...   
162  {"11":"Hardware, Telephony, Smartphones, Monit...   
163  {"11":"Hardware, Telephony, Smartphones, Monit...   
164  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN...  
1    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...  
2    BUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO C...  
3    BUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409...  
4    HELLO  IM HERE TO ASK YOU ABOUT A THING THAT H...  
..                                                 ...  
160  DATI TEAMVIEWER 1726129643 X85I1W2T  COSE DA I...  
161  BUONGIORNO IL COLLEGAMENTO TRA LAPTOPDOCKING S...  
162  CIAO HO CONTROLLATO LA DOCKING STATION PURTROP...  
163  QUANDO ACCENDO IL PC LA DOCKING STATION NON MI...  
164  CIAO MI POTETE INSTALLARE DOMANI PER STEFANIE ...  

[165 rows x 3 columns]

# df_3_tcp

In [65]:
#df_3_tcp
import pandas as pd
words_to_check = ['tcp', 'windows']

# Initialize an empty DataFrame to store the matching rows
df_3_tcp = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_tcp = df_3_tcp.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_tcp = df_3_tcp.reset_index(drop=True)

df_3_tcp

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\589532251.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_tcp = df_3_tcp.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\589532251.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_tcp = df_3_tcp.append(df_3[word_mask])


Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...   
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...   

                                              tokens  
0  [servus, haben, unserem, bro, saviese, tach, e...  
1  [daccordo, faccio, poter, ricevere, pc, fisso,...  
2  [parte, windows, 11, resto, ora, appuntamento,...  
3  [meinem, drucker, einstellungen, festlegen, do...  
4  [furlotti, first, line, support, holding, 1959...  
5  [able, log, into, computer, username, password...  
6  [473713, avevamo, aggiornato, driver, sia, tra...  
7  [entschuldigung, aber, diese, seite, verfgbar,...  
8  [computer, lenovo, thinkpad, x1, carbon, 7th, ...  
9  [local, printer, doesnt, properly, since, upda...

In [66]:
df_3_tcp

Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...   
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...   

                                              tokens  
0  [servus, haben, unserem, bro, saviese, tach, e...  
1  [daccordo, faccio, poter, ricevere, pc, fisso,...  
2  [parte, windows, 11, resto, ora, appuntamento,...  
3  [meinem, drucker, einstellungen, festlegen, do...  
4  [furlotti, first, line, support, holding, 1959...  
5  [able, log, into, computer, username, password...  
6  [473713, avevamo, aggiornato, driver, sia, tra...  
7  [entschuldigung, aber, diese, seite, verfgbar,...  
8  [computer, lenovo, thinkpad, x1, carbon, 7th, ...  
9  [local, printer, doesnt, properly, since, upda...

In [67]:
df_3_tcp = df_3_tcp.drop(columns= 'tokens')
df_3_tcp

Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...  
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...  
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...  
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...  
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...  
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...  
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...  
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...

# df_3_db 

In [68]:
#df_3_db
import pandas as pd
words_to_check = ['oracle', 'mysql', 'windows', 'mariadb']

# Initialize an empty DataFrame to store the matching rows
df_3_db = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_db = df_3_db.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_db = df_3_db.reset_index(drop=True)

df_3_db

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])


Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...   
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...   

                                              tokens  
0  [servus, haben, unserem, bro, saviese, tach, e...  
1  [daccordo, faccio, poter, ricevere, pc, fisso,...  
2  [parte, windows, 11, resto, ora, appuntamento,...  
3  [meinem, drucker, einstellungen, festlegen, do...  
4  [furlotti, first, line, support, holding, 1959...  
5  [able, log, into, computer, username, password...  
6  [473713, avevamo, aggiornato, driver, sia, tra...  
7  [entschuldigung, aber, diese, seite, verfgbar,...  
8  [computer, lenovo, thinkpad, x1, carbon, 7th, ...  
9  [local, printer, doesnt, properly, since, upda...

In [69]:
df_3_db

Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...   
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...   

                                              tokens  
0  [servus, haben, unserem, bro, saviese, tach, e...  
1  [daccordo, faccio, poter, ricevere, pc, fisso,...  
2  [parte, windows, 11, resto, ora, appuntamento,...  
3  [meinem, drucker, einstellungen, festlegen, do...  
4  [furlotti, first, line, support, holding, 1959...  
5  [able, log, into, computer, username, password...  
6  [473713, avevamo, aggiornato, driver, sia, tra...  
7  [entschuldigung, aber, diese, seite, verfgbar,...  
8  [computer, lenovo, thinkpad, x1, carbon, 7th, ...  
9  [local, printer, doesnt, properly, since, upda...

In [70]:
df_3_db = df_3_db.drop(columns = 'tokens')
df_3_db

Title  \
0             neuer printer einbindung nicht möglich   
1                              PC per ATASS-Schulung   
2         Stampanti non funzionanti (accesso negato)   
3  Drucker Einstellung Doppelseitig und Farbe nic...   
4                                  cambio smartphone   
5                                      ticket 381298   
6                        Docking station no ethernet   
7  für die elektronische Übermittlung statistisch...   
8               ThinkPad Docking station no ethernet   
9                               Printer out of order   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   
9  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...  
1  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...  
2  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...  
3  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...  
4   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...  
5   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
6  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
7   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...  
8  COMPUTER LENOVO THINKPAD X1 CARBON 7TH SYSTEM ...  
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...

# df_3_pc

In [71]:
#df_3_pc
import pandas as pd
words_to_check = ['laptop', 'pc', 'schermo', 'fisso', 'tastiera', 'monitor', 
                  'computer', 'cavo', 'pw', 'usb', 'telefono']


# Initialize an empty DataFrame to store the matching rows
df_3_pc = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_pc = df_3_pc.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_pc = df_3_pc.reset_index(drop=True)

df_3_pc

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\Mat

Title  \
0                          new laptop   
1        Probleme mit Hotspot Ausland   
2                     Docking station   
3            laptop LENOVO X1 carbon    
4                 Teams und Kopfhörer   
..                                ...   
383       Collegamento telefono fisso   
384   Telefono FISSO non funziona più   
385          Chiamate verso l'esterno   
386                 Telefono Cordless   
387  sostituzione cellulare aziendale   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
383  {"11":"Hardware, Telephony, Smartphones, Monit...   
384  {"11":"Hardware, Telephony, Smartphones, Monit...   
385  {"11":"Hardware, Telephony, Smartphones, Monit...   
386  {"11":"Hardware, Telephony, Smartphones, Monit...   
387  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD Y...   
1    HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SIC...   
2    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...   
3    CIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LEN...   
4    HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER...   
..                                                 ...   
383  CIAO POTETE COLLEGARMI IL TELEFONO FISSO NUMER...   
384                     TELEFONO FISSO NON FUNZIONA PI   
385  BUON POMERIGGIO NON RIESCO AD EFFETTURARE CHIA...   
386  BUONGIORNO  ATTUALMENTE MI  STATO FORNITO UN T...   
387  LA BATTERIA DEL TELEFONO NON MANTIENE PI LA CA...   

                                                tokens  
0    [order, laptop, give, some, advice, which, sui...  
1    [seit, kurzem, aufgefallen, sich, mein, laptop...  
2    [mattina, comunicazione, tra, docking, station...  
3    [valutare, sostituzione, quanto, lento, sia, a...  
4    [laptop, airpods, verbunden, aber, hre, teamsa...  
..                                                 ...  
383       [collegarmi, telefono, fisso, telefono, 125]  
384                                  [telefono, fisso]  
385  [buon, pomeriggio, effetturare, chiamateverso,...  
386  [attualmente, stato, fornito, telefono, fisso,...  
387  [batteria, telefono, mantiene, carica, mattina...  

[388 rows x 4 columns]

In [72]:
df_3_pc

Title  \
0                          new laptop   
1        Probleme mit Hotspot Ausland   
2                     Docking station   
3            laptop LENOVO X1 carbon    
4                 Teams und Kopfhörer   
..                                ...   
383       Collegamento telefono fisso   
384   Telefono FISSO non funziona più   
385          Chiamate verso l'esterno   
386                 Telefono Cordless   
387  sostituzione cellulare aziendale   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
383  {"11":"Hardware, Telephony, Smartphones, Monit...   
384  {"11":"Hardware, Telephony, Smartphones, Monit...   
385  {"11":"Hardware, Telephony, Smartphones, Monit...   
386  {"11":"Hardware, Telephony, Smartphones, Monit...   
387  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD Y...   
1    HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SIC...   
2    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...   
3    CIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LEN...   
4    HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER...   
..                                                 ...   
383  CIAO POTETE COLLEGARMI IL TELEFONO FISSO NUMER...   
384                     TELEFONO FISSO NON FUNZIONA PI   
385  BUON POMERIGGIO NON RIESCO AD EFFETTURARE CHIA...   
386  BUONGIORNO  ATTUALMENTE MI  STATO FORNITO UN T...   
387  LA BATTERIA DEL TELEFONO NON MANTIENE PI LA CA...   

                                                tokens  
0    [order, laptop, give, some, advice, which, sui...  
1    [seit, kurzem, aufgefallen, sich, mein, laptop...  
2    [mattina, comunicazione, tra, docking, station...  
3    [valutare, sostituzione, quanto, lento, sia, a...  
4    [laptop, airpods, verbunden, aber, hre, teamsa...  
..                                                 ...  
383       [collegarmi, telefono, fisso, telefono, 125]  
384                                  [telefono, fisso]  
385  [buon, pomeriggio, effetturare, chiamateverso,...  
386  [attualmente, stato, fornito, telefono, fisso,...  
387  [batteria, telefono, mantiene, carica, mattina...  

[388 rows x 4 columns]

In [73]:
df_3_pc = df_3_pc.drop(columns = 'tokens')
df_3_pc

Title  \
0                          new laptop   
1        Probleme mit Hotspot Ausland   
2                     Docking station   
3            laptop LENOVO X1 carbon    
4                 Teams und Kopfhörer   
..                                ...   
383       Collegamento telefono fisso   
384   Telefono FISSO non funziona più   
385          Chiamate verso l'esterno   
386                 Telefono Cordless   
387  sostituzione cellulare aziendale   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
383  {"11":"Hardware, Telephony, Smartphones, Monit...   
384  {"11":"Hardware, Telephony, Smartphones, Monit...   
385  {"11":"Hardware, Telephony, Smartphones, Monit...   
386  {"11":"Hardware, Telephony, Smartphones, Monit...   
387  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD Y...  
1    HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SIC...  
2    CIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TR...  
3    CIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LEN...  
4    HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER...  
..                                                 ...  
383  CIAO POTETE COLLEGARMI IL TELEFONO FISSO NUMER...  
384                     TELEFONO FISSO NON FUNZIONA PI  
385  BUON POMERIGGIO NON RIESCO AD EFFETTURARE CHIA...  
386  BUONGIORNO  ATTUALMENTE MI  STATO FORNITO UN T...  
387  LA BATTERIA DEL TELEFONO NON MANTIENE PI LA CA...  

[388 rows x 3 columns]

# df_3_vulnerabilities

In [74]:
#df_3_vulnerabilities
import pandas as pd
words_to_check = ['vulnerabilities']

# Initialize an empty DataFrame to store the matching rows
df_3_vulnerabilities = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_vulnerabilities = df_3_vulnerabilities.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_vulnerabilities = df_3_vulnerabilities.reset_index(drop=True)
df_3_vulnerabilities= df_3_vulnerabilities.drop(columns = 'tokens')
df_3_vulnerabilities

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\155574697.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_vulnerabilities = df_3_vulnerabilities.append(df_3[word_mask])


Empty DataFrame
Columns: [Title, Topic, Text]
Index: []

In [75]:
df_3_vulnerabilities

Empty DataFrame
Columns: [Title, Topic, Text]
Index: []

# df_3_email

In [76]:
#df_3_email
import pandas as pd
words_to_check = ['mail']

# Initialize an empty DataFrame to store the matching rows
df_3_email = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_email = df_3_email.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_email = df_3_email.reset_index(drop=True)
df_3_email= df_3_email.drop(columns = 'tokens')
df_3_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\750117258.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_email = df_3_email.append(df_3[word_mask])


Title  \
0                             Numero telefonico   
1                                  Nr telefono    
2                       Info for ticket 582224    
3                               Screen blackout   
4                   Toner stampante ACS 1247109   
5                   Cellulare e ProCall a Laura   
6                                Neues ThinkPad   
7                                    Smartphone   
8                                    Smartphone   
9                   e-mail salvata su stampante   
10                              Nuova Stampante   
11   scansione collegata alla mail non funziona   
12  Mobile email access / technician Aldo Lauri   
13                         Outlook su cellulare   
14           Cellulare perso Roessler Christian   
15                    mails in entrata bloccati   
16                            cambio smartphone   
17            ADD email to Printer for scanning   
18                         App Concur Cellulare   
19       E-mail Adresse e PC per Bruno Campaner   
20        WG: Fernzugriff Visualisierungsserver   
21                                Problemi ENGO   
22                               Email in Handy   
23                          Internet Engo lento   
24       Bluescreen issue - Christine Oberhofer   
25                                Postage meter   
26           possible virus and email signature   
27    Acesso int0101 per la app atasspro mobile   
28                   Plotter wird nicht erkannt   
29                   Plotter wird nicht erkannt   
30                       Stampante non funziona   
31           RE: Ticket #513035 Assigned to you   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0   BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NO...  
1   SALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO ...  
2   HELLO FRANCESCO THX NOW WORK FOR MY  I WILL MA...  
3   I CALLED HIM AND SENT A MAIL WITH PHOTO THE SC...  
4   BUONGIORNO  FINITO IL TONER DELLA STAMPANTE XE...  
5   CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA ...  
6   HALLO  BITTE DAS THINKPAD FR BIANCA ZANONA EIN...  
7   BUONGIORNO PER LUTILIZZO

In [77]:
df_3_email

Title  \
0                             Numero telefonico   
1                                  Nr telefono    
2                       Info for ticket 582224    
3                               Screen blackout   
4                   Toner stampante ACS 1247109   
5                   Cellulare e ProCall a Laura   
6                                Neues ThinkPad   
7                                    Smartphone   
8                                    Smartphone   
9                   e-mail salvata su stampante   
10                              Nuova Stampante   
11   scansione collegata alla mail non funziona   
12  Mobile email access / technician Aldo Lauri   
13                         Outlook su cellulare   
14           Cellulare perso Roessler Christian   
15                    mails in entrata bloccati   
16                            cambio smartphone   
17            ADD email to Printer for scanning   
18                         App Concur Cellulare   
19       E-mail Adresse e PC per Bruno Campaner   
20        WG: Fernzugriff Visualisierungsserver   
21                                Problemi ENGO   
22                               Email in Handy   
23                          Internet Engo lento   
24       Bluescreen issue - Christine Oberhofer   
25                                Postage meter   
26           possible virus and email signature   
27    Acesso int0101 per la app atasspro mobile   
28                   Plotter wird nicht erkannt   
29                   Plotter wird nicht erkannt   
30                       Stampante non funziona   
31           RE: Ticket #513035 Assigned to you   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0   BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NO...  
1   SALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO ...  
2   HELLO FRANCESCO THX NOW WORK FOR MY  I WILL MA...  
3   I CALLED HIM AND SENT A MAIL WITH PHOTO THE SC...  
4   BUONGIORNO  FINITO IL TONER DELLA STAMPANTE XE...  
5   CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA ...  
6   HALLO  BITTE DAS THINKPAD FR BIANCA ZANONA EIN...  
7   BUONGIORNO PER LUTILIZZO

# df_3_software

In [78]:
#df_3_software
import pandas as pd
words_to_check = ['software', 'server']

# Initialize an empty DataFrame to store the matching rows
df_3_software = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_software = df_3_software.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_software = df_3_software.reset_index(drop=True)
df_3_software= df_3_software.drop(columns = 'tokens')
df_3_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\916185259.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_software = df_3_software.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_10704\916185259.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_software = df_3_software.append(df_3[word_mask])


Title  \
0                                    PC running slow.   
1             Monitor non si collega con il portatile   
2                                    Modula Scaffale    
3                                    Modula Scaffale    
4   Neues Notebook SPS-Programmierer TAEE Peter Št...   
5                                     Sostituzione PC   
6                      PC   C 238  startet nicht mehr   
7                                         PC Showroom   
8                                      Scanner defekt   
9                                      Scanner defekt   
10                                     Vecchio Laptop   
11                               Laptop LCU TestBench   
12                               Laptop LCU TestBench   
13                               Support per altro PC   
14                   2 old laptops for emergency duty   
15   Two old Laptops for Data Tracking/ Measurements    
16                  laptop for Test Bench lance pipes   
17                                Internet Engo lento   
18                     Salve, Cavo 5m USB a micro USB   
19                          PC C133 non raggiungibile   
20                                   Modula Scaffale    
21                Kein Zugriff auf Server für Telefon   
22                                             IP KNX   
23                            Nuovi Uffici Epowertrac   
24              WG: Fernzugriff Visualisierungsserver   
25  für die elektronische Übermittlung statistisch...   
26                                         Server MFD   
27                                         Server MFD   
28                                         Server MFD   
29                  Zebra Printer doesnt work anymore   
30                           Laptop neuer Mitarbeiter   
31             Espandere memoria sul PROFILE-SQL-PROD   
32                             Problemi Server Serv03   
33          Acesso int0101 per la app atasspro mobile   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   
32  {"11":"Hardware, Telephony, Smartphones, Monit...   
33  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  


In [79]:
df_3_software

Title  \
0                                    PC running slow.   
1             Monitor non si collega con il portatile   
2                                    Modula Scaffale    
3                                    Modula Scaffale    
4   Neues Notebook SPS-Programmierer TAEE Peter Št...   
5                                     Sostituzione PC   
6                      PC   C 238  startet nicht mehr   
7                                         PC Showroom   
8                                      Scanner defekt   
9                                      Scanner defekt   
10                                     Vecchio Laptop   
11                               Laptop LCU TestBench   
12                               Laptop LCU TestBench   
13                               Support per altro PC   
14                   2 old laptops for emergency duty   
15   Two old Laptops for Data Tracking/ Measurements    
16                  laptop for Test Bench lance pipes   
17                                Internet Engo lento   
18                     Salve, Cavo 5m USB a micro USB   
19                          PC C133 non raggiungibile   
20                                   Modula Scaffale    
21                Kein Zugriff auf Server für Telefon   
22                                             IP KNX   
23                            Nuovi Uffici Epowertrac   
24              WG: Fernzugriff Visualisierungsserver   
25  für die elektronische Übermittlung statistisch...   
26                                         Server MFD   
27                                         Server MFD   
28                                         Server MFD   
29                  Zebra Printer doesnt work anymore   
30                           Laptop neuer Mitarbeiter   
31             Espandere memoria sul PROFILE-SQL-PROD   
32                             Problemi Server Serv03   
33          Acesso int0101 per la app atasspro mobile   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   
32  {"11":"Hardware, Telephony, Smartphones, Monit...   
33  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  


# SUMMARIZATION

# Creation of blocks 

## df_1_email

In [80]:
pip install --upgrade requests


Note: you may need to restart the kernel to use updated packages.


In [81]:
pip install transformers


Note: you may need to restart the kernel to use updated packages.


In [82]:
#specify number of rows in each chunk
n=2
#split DataFrame into chunks
list_df = [df_1_email[i:i+n] for i in range(0,len(df_1_email),n)]
    #print(list_df)

In [83]:
len(list_df)

275

In [84]:
list_df[274]

Title                                              Topic  \
548  Licenza CRM  {"16":"User identity management, Permissions, ...   
549  Licenze CRM  {"16":"User identity management, Permissions, ...   

                                                  Text  
548  CIAOPOTREMMO PER FAVORE ASSEGNARE A DIETMAR MA...  
549  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...

In [85]:
def put_together():
    list1=[]
    for index in range(0,274):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [86]:
summ_block = put_together()
summ_block

Result 0:
I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHEN OPENING OUTLOOK TEAMS OTHER COMPUTER PROGRAMS  I AM NOT RECEIVING EMAILS OR CAN SEND ANY EMAILS NO SURFACE PROGRAMS ARE WORKING CANNOT COPY ANYTHING THE MESSAGE ON SURFACE IS YOUR COMPUTER S TRUSTED PLATFORM MODULE HAS MALFUNCTIONED  ERROR CODE 80090016HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15 SICK LEAVE COULD YOU WRITE A MESSAGE OF ABSENCE ON HIS OUTLOOK EMAIL IN FRENCH BONJOUR JE SUIS ACTUELLEMENT ABSENTE ET SERAI DE RETOUR LE 18 SEPTEMBRE EN CAS DURGENCE VOUS POUVEZ CONTACTER  COMPTAFOURNISSEURTECHNOALPINCOM BIEN CORDIALEMENT BEST REGARDS

Result 1:
HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022 MESSAGES THANK YOUHI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE IS EVEN A NEW FAULT  THE MAILBOX IS SHOWING ME MORE UNREAD MESSAGES THAN I CAN SEE IN THE INBOX  COULD YOU PLEASE CHECK THANK YOU IN ADVANCE  DRTHE 

Result 2:
HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THE

['I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHEN OPENING OUTLOOK TEAMS OTHER COMPUTER PROGRAMS\xa0 I AM NOT RECEIVING EMAILS OR CAN SEND ANY EMAILS NO SURFACE PROGRAMS ARE WORKING CANNOT COPY ANYTHING THE MESSAGE ON SURFACE IS YOUR COMPUTER S TRUSTED PLATFORM MODULE HAS MALFUNCTIONED\xa0 ERROR CODE 80090016HI KARIMA GUERBAA\xa0IS ABSENT UNTIL SEPTEMBER 15\xa0SICK LEAVE COULD YOU WRITE A MESSAGE OF ABSENCE ON HIS OUTLOOK EMAIL IN FRENCH BONJOUR JE SUIS ACTUELLEMENT ABSENTE ET SERAI DE RETOUR LE 18 SEPTEMBRE EN CAS DURGENCE VOUS POUVEZ CONTACTER  COMPTAFOURNISSEURTECHNOALPINCOM BIEN CORDIALEMENT BEST REGARDS',
 'HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022 MESSAGES THANK YOUHI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE IS EVEN A NEW FAULT\xa0 THE MAILBOX IS SHOWING ME MORE UNREAD MESSAGES THAN I CAN\xa0SEE IN THE INBOX  COULD YOU PLEASE CHECK THANK YOU IN ADVANCE  DRTHE ',
 'HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE I

In [87]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 274):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [88]:
blocks_to_skip = [4,5,47,110,140,168,169,173,174,176,195,204,234,241,242,244,248,250]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHEN OPENING OUTLOOK TEAMS OTHER COMPUTER PROGRAMS  I AM NOT RECEIVING EMAILS OR CAN SEND ANY EMAILS NO SURFACE PROGRAMS ARE WORKING CANNOT COPY ANYTHING THE MESSAGE ON SURFACE IS YOUR COMPUTER S TRUSTED PLATFORM MODULE HAS MALFUNCTIONED  ERROR CODE 80090016HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15 SICK LEAVE COULD YOU WRITE A MESSAGE OF ABSENCE ON HIS OUTLOOK EMAIL IN FRENCH BONJOUR JE SUIS ACTUELLEMENT ABSENTE ET SERAI DE RETOUR LE 18 SEPTEMBRE EN CAS DURGENCE VOUS POUVEZ CONTACTER  COMPTAFOURNISSEURTECHNOALPINCOM BIEN CORDIALEMENT BEST REGARDS

Result 1:
HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022 MESSAGES THANK YOUHI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE IS EVEN A NEW FAULT  THE MAILBOX IS SHOWING ME MORE UNREAD MESSAGES THAN I CAN SEE IN THE INBOX  COULD YOU PLEASE CHECK THANK YOU IN ADVANCE  DRTHE 

Result 2:
HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THE

In [89]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHEN OPENING OUTLOOK TEAMS OTHER COMPUTER PROGRAMS  I AM NOT RECEIVING EMAILS OR CAN SEND ANY EMAILS NO SURFACE PROGRAMS ARE WORKING CANNOT COPY ANYTHING THE MESSAGE ON SURFACE IS YOUR COMPUTER S TRUSTED PLATFORM MODULE HAS MALFUNCTIONED  ERROR CODE 80090016HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15 SICK LEAVE COULD YOU WRITE A MESSAGE OF ABSENCE ON HIS OUTLOOK EMAIL IN FRENCH BONJOUR JE SUIS ACTUELLEMENT ABSENTE ET SERAI DE RETOUR LE 18 SEPTEMBRE EN CAS DURGENCE VOUS POUVEZ CONTACTER  COMPTAFOURNISSEURTECHNOALPINCOM BIEN CORDIALEMENT BEST REGARDS

Result 1:
HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022 MESSAGES THANK YOUHI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE IS EVEN A NEW FAULT  THE MAILBOX IS SHOWING ME MORE UNREAD MESSAGES THAN I CAN SEE IN THE INBOX  COULD YOU PLEASE CHECK THANK YOU IN ADVANCE  DRTHE 

Result 2:
HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THE

['I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHEN OPENING OUTLOOK TEAMS OTHER COMPUTER PROGRAMS\xa0 I AM NOT RECEIVING EMAILS OR CAN SEND ANY EMAILS NO SURFACE PROGRAMS ARE WORKING CANNOT COPY ANYTHING THE MESSAGE ON SURFACE IS YOUR COMPUTER S TRUSTED PLATFORM MODULE HAS MALFUNCTIONED\xa0 ERROR CODE 80090016HI KARIMA GUERBAA\xa0IS ABSENT UNTIL SEPTEMBER 15\xa0SICK LEAVE COULD YOU WRITE A MESSAGE OF ABSENCE ON HIS OUTLOOK EMAIL IN FRENCH BONJOUR JE SUIS ACTUELLEMENT ABSENTE ET SERAI DE RETOUR LE 18 SEPTEMBRE EN CAS DURGENCE VOUS POUVEZ CONTACTER  COMPTAFOURNISSEURTECHNOALPINCOM BIEN CORDIALEMENT BEST REGARDS',
 'HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022 MESSAGES THANK YOUHI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE IS EVEN A NEW FAULT\xa0 THE MAILBOX IS SHOWING ME MORE UNREAD MESSAGES THAN I CAN\xa0SEE IN THE INBOX  COULD YOU PLEASE CHECK THANK YOU IN ADVANCE  DRTHE ',
 'HI I AM VERY SORRY BUT OUTLOOK IS STILL CLOSING BY ITS OWN  SINCE TODAY THERE I

In [90]:
!pip install torch
!pip install transformers

In [91]:
import pickle

In [92]:
picklefile = "df_1_email_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block_test = pickle.load(pkl_rb_obj)
print(summ_block_test)

[[{'summary_text': "There is an error message on Surface when opening Outlook Team. Karima Guerba is absent until September 15th. He will send his e-mail in French to his contact in France in order to put a message of absence on his Outlook team's website."}], [{'summary_text': 'The Outlook 2022 is still not closing. There is a new problem with the mailbox showing more messages than in the inbox. The person responsible will check the inbox in order to send it to the Outlook 2022 email in advance. It is not working properly yet. '}], [{'summary_text': "The Outlook is still not closing. There is a new problem with the e-mail. Daniela's employment ends tomorrow, but her company email will still receive the messages we need for accountancy.   It's not clear how it works in other departments. "}], [{'summary_text': "Andres Schwingershack sent a mesage to the office of Lorsquoffery and received a late reply from Manuel. He is a member of the Board of Directors of the Lawyer's Association of 

# df_1_rights

In [93]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_rights[i:i+n] for i in range(0,len(df_1_rights),n)]
    #print(list_df)

In [94]:
len(list_df)

63

In [95]:
list_df[62]

Title  \
372  Accesso a cartelle per Lorenzo Sartori   
373                         PC Alyssa Klotz   
374      Dare accesso di lettura a cartelle   

                                                 Topic  \
372  {"16":"User identity management, Permissions, ...   
373  {"16":"User identity management, Permissions, ...   
374  {"16":"User identity management, Permissions, ...   

                                                  Text  
372  BUONGIORNO CORTESEMENTE  POSSIBILE DARE ACCESS...  
373  CIAO NELL UFFICIO A DENVER C ANCORA IL PC DI A...  
374  BUONGIORNO VI CHIEDO DI DARE ACCESSO A DAVID M...

In [96]:
def put_together():
    list1=[]
    for index in range(0,62):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [97]:
summ_block = put_together()
summ_block

Result 0:
EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADGE N 10147 COME SEGUE ACCESSO SOLO DALLE PORTE DELLOFFICINA NIENTE UFFICIO DA LUNEDI A VENERDI DALLE ORE 530 FINO ALLE 1900 GRAZIE SALUTI HORSTCIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   CON GLI STESSI ACCESSI COME GLI ALTRI SALDATORI   GRAZIE BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO BADGE A TUTTI GLI ACCESSI AUTORIZZAZIONI COME MICHELE VALBUSA IERI NELLA FILIALE DI VIA SIEMENS NON ENTRAVO DALLE PORTECIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV E STANO JURAJ ALLINGRESSO DELLAPPARTAMENTO QUI NEL HQ GRAZIE HANNES  CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO PER ANJAVOLEVO AVVISARVI CHE AVEVAMO GI UN BADGE PER LEI N 10230  VI RIDIAMO IL N 1031 CHE NON CI SERVE LO CONSEGNA LORENZO OGGI A MEZZOGIORNO GRAZIE EGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10149 PERCH OGGI TERMINA IL TIROCINO DI IOLANDO IULIANO GRAZIE SALUTI HORST

Result 1:
EGREGI SIGNORI VI PREGO DI ATTIVARE IL NUOVO BADGE N 10009 DI ANDREY COME SEGUE INGRESSO

['EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADGE N 10147 COME SEGUE ACCESSO SOLO DALLE PORTE DELLOFFICINA NIENTE UFFICIO DA LUNEDI A VENERDI DALLE ORE 530 FINO ALLE 1900 GRAZIE SALUTI HORSTCIAO\xa0  MI SERVE UN BADGE PER\xa0MARTIN GAJDOS\xa0\xa0 CON GLI STESSI ACCESSI COME GLI ALTRI SALDATORI\xa0  GRAZIE\xa0BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO BADGE A TUTTI GLI ACCESSI AUTORIZZAZIONI COME MICHELE VALBUSA IERI NELLA FILIALE DI VIA SIEMENS NON ENTRAVO DALLE PORTECIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV E STANO JURAJ ALLINGRESSO DELLAPPARTAMENTO QUI NEL HQ GRAZIE HANNES \xa0CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO PER ANJAVOLEVO AVVISARVI CHE AVEVAMO GI UN BADGE PER LEI N 10230  VI RIDIAMO IL N 1031 CHE NON CI SERVE LO CONSEGNA LORENZO OGGI A MEZZOGIORNO GRAZIE EGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10149 PERCH OGGI TERMINA IL TIROCINO DI IOLANDO IULIANO GRAZIE SALUTI HORST',
 'EGREGI SIGNORI VI PREGO DI ATTIVARE IL NUOVO BADGE N 10009 DI ANDREY COME SEGUE IN

In [98]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 62):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [99]:
blocks_to_skip = [12,16,39,43,51,58,61]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADGE N 10147 COME SEGUE ACCESSO SOLO DALLE PORTE DELLOFFICINA NIENTE UFFICIO DA LUNEDI A VENERDI DALLE ORE 530 FINO ALLE 1900 GRAZIE SALUTI HORSTCIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   CON GLI STESSI ACCESSI COME GLI ALTRI SALDATORI   GRAZIE BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO BADGE A TUTTI GLI ACCESSI AUTORIZZAZIONI COME MICHELE VALBUSA IERI NELLA FILIALE DI VIA SIEMENS NON ENTRAVO DALLE PORTECIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV E STANO JURAJ ALLINGRESSO DELLAPPARTAMENTO QUI NEL HQ GRAZIE HANNES  CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO PER ANJAVOLEVO AVVISARVI CHE AVEVAMO GI UN BADGE PER LEI N 10230  VI RIDIAMO IL N 1031 CHE NON CI SERVE LO CONSEGNA LORENZO OGGI A MEZZOGIORNO GRAZIE EGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10149 PERCH OGGI TERMINA IL TIROCINO DI IOLANDO IULIANO GRAZIE SALUTI HORST

Result 1:
EGREGI SIGNORI VI PREGO DI ATTIVARE IL NUOVO BADGE N 10009 DI ANDREY COME SEGUE INGRESSO

In [100]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADGE N 10147 COME SEGUE ACCESSO SOLO DALLE PORTE DELLOFFICINA NIENTE UFFICIO DA LUNEDI A VENERDI DALLE ORE 530 FINO ALLE 1900 GRAZIE SALUTI HORSTCIAO   MI SERVE UN BADGE PER MARTIN GAJDOS   CON GLI STESSI ACCESSI COME GLI ALTRI SALDATORI   GRAZIE BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO BADGE A TUTTI GLI ACCESSI AUTORIZZAZIONI COME MICHELE VALBUSA IERI NELLA FILIALE DI VIA SIEMENS NON ENTRAVO DALLE PORTECIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV E STANO JURAJ ALLINGRESSO DELLAPPARTAMENTO QUI NEL HQ GRAZIE HANNES  CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO PER ANJAVOLEVO AVVISARVI CHE AVEVAMO GI UN BADGE PER LEI N 10230  VI RIDIAMO IL N 1031 CHE NON CI SERVE LO CONSEGNA LORENZO OGGI A MEZZOGIORNO GRAZIE EGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10149 PERCH OGGI TERMINA IL TIROCINO DI IOLANDO IULIANO GRAZIE SALUTI HORST

Result 1:
EGREGI SIGNORI VI PREGO DI ATTIVARE IL NUOVO BADGE N 10009 DI ANDREY COME SEGUE INGRESSO

['EGREGI SIGNORI VI PREGO DI PROGRAMMARE IL BADGE N 10147 COME SEGUE ACCESSO SOLO DALLE PORTE DELLOFFICINA NIENTE UFFICIO DA LUNEDI A VENERDI DALLE ORE 530 FINO ALLE 1900 GRAZIE SALUTI HORSTCIAO\xa0  MI SERVE UN BADGE PER\xa0MARTIN GAJDOS\xa0\xa0 CON GLI STESSI ACCESSI COME GLI ALTRI SALDATORI\xa0  GRAZIE\xa0BUONGIORNO AVREI BISOGNO DI ABILITARE IL MIO BADGE A TUTTI GLI ACCESSI AUTORIZZAZIONI COME MICHELE VALBUSA IERI NELLA FILIALE DI VIA SIEMENS NON ENTRAVO DALLE PORTECIAO PREGO ABILITARE I BADGE DI NOSAL MIROSLAV E STANO JURAJ ALLINGRESSO DELLAPPARTAMENTO QUI NEL HQ GRAZIE HANNES \xa0CIAO A TUTTI GRAZIE PER AVER IMPOSTATO TUTTO PER ANJAVOLEVO AVVISARVI CHE AVEVAMO GI UN BADGE PER LEI N 10230  VI RIDIAMO IL N 1031 CHE NON CI SERVE LO CONSEGNA LORENZO OGGI A MEZZOGIORNO GRAZIE EGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10149 PERCH OGGI TERMINA IL TIROCINO DI IOLANDO IULIANO GRAZIE SALUTI HORST',
 'EGREGI SIGNORI VI PREGO DI ATTIVARE IL NUOVO BADGE N 10009 DI ANDREY COME SEGUE IN

In [101]:
picklefile = "df_1_rights_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block_test = pickle.load(pkl_rb_obj)
print(summ_block_test)

[[{'summary_text': 'E.G. SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10147 is a GRAZIE SALUTI HORSTCIAO and IL MIO BADGE is a TUTTI GLI ACCESSI AUTORIZZAZIONI. '}], [{'summary_text': 'GRAZIE SALUTI HORSTEGREGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10004 PERCH MESSNER LUKAS AVEVA IERI IL SUO ULTIMO GIORNO DI LAVORO GRAZie SALUTi HORTPREGO FARE NUOVO PER MICHELE MARSONET.'}], [{'summary_text': 'EGI SIGNORI VI PREGO DI DISATTIVARE IL BADGE N 10150 PERCH ALEX GASSER TERMINA OGGI IL SUO TIROCINO IN ANTICIPO GRAZIE SALUTI HORSTCIAO RAGAZZI. '}], [{'summary_text': 'Clemens Pintt, ACCESSO GARAGE, ABILITARE BADGECIAO VI PREGO DI CREARE, UN BADGE PER JONSTON DARREN IN CASA FINO 010923 MENSA PAGATA PROFILO, IL BADGE N 10050 PERCH OGGI TERMINA, IL TIROCINIO DI GAMPER SIMON GRAZIE SALUTI HORST PREGO DISATTIVARE, IL Badge ADESSO PERCH HA LAVORATO SOLO FINO ALLE 1200, IL GOODGE A CASA POTETE PREPARARE UNO'}], [{'summary_text': 'CIAO PREGO VI CHIEDERE DI PREPARARE UN BADGE PER FELIX DILGER PER 170

# df_1_computer


In [102]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_computer[i:i+n] for i in range(0,len(df_1_computer),n)]
    #print(list_df)

In [103]:
len(list_df)

23

In [104]:
list_df[22]

Title                                              Topic  \
132  TechnoAlpin Cloud  {"16":"User identity management, Permissions, ...   

                                                  Text  
132  I AM SELECTING TO RESET THE PASSWORD BUT IT DO...

In [105]:
def put_together():
    list1=[]
    for index in range(0,22):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [106]:
summ_block = put_together()
summ_block

Result 0:
CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA PASSWORD IN TEMPO ED  BLOCCATA POTRESTI SBLOCCARE IL PC MFL0228 PER FAVORE GRAZIECIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUTLOOK CHE DOPO IL CAMBIO PC NON C PIGRZCIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRANET PER VISUALIZZARE MATERIALI COME MANUALI PRODOTTI ECC COME FACCIO 2 VORREI ACCEDERE A PROTIME COME FACCIO HO CERCATO MA NON VEDO IL PROGRAMMA SUL PC 3 MI HANNO DI CHIEDERVI DI ABILITARE IL MIO BADGE PER ACCEDERE ALLA PRODUZIONE IN VIA SIEMENSI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABHELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO NON RIESCO PI A CONNETTERMI A INTERNET CON IL MIO PC HO AVUTO QUESTO PROBLEMA QUALCHE SETTIMANA FA POTRESTI PER FAVORE CONTROLLARLO IL PRIMA POSSIBILE SALUTI HANS

Result 1:
HALLO BITTE DEN ORDNER  GPRODUKTIONPRODUKTIONSLEITUNG FR   PC C247ALPINL

['CIAO PENSO CHE\xa0LE YU YANG NON HA CAMBIATO LA PASSWORD IN TEMPO ED  BLOCCATA POTRESTI SBLOCCARE IL PC MFL0228\xa0PER FAVORE GRAZIECIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUTLOOK CHE DOPO IL CAMBIO PC NON C PIGRZCIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRANET PER VISUALIZZARE MATERIALI COME MANUALI PRODOTTI ECC COME FACCIO 2 VORREI ACCEDERE A PROTIME COME FACCIO HO CERCATO MA NON VEDO IL PROGRAMMA SUL PC 3 MI HANNO DI CHIEDERVI DI ABILITARE IL MIO BADGE PER ACCEDERE ALLA PRODUZIONE IN VIA SIEMENSI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABHELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO NON RIESCO PI A CONNETTERMI A INTERNET CON IL MIO PC HO AVUTO QUESTO PROBLEMA QUALCHE SETTIMANA FA POTRESTI PER FAVORE CONTROLLARLO IL PRIMA POSSIBILE SALUTI HANS',
 'HALLO BITTE DEN ORDNER\xa0\xa0GPRODUKTIONPRODUKTIONSLEITUNG FR\xa0 \xa0PC C247ALP

In [107]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 22):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [108]:
blocks_to_skip = [2,4,12]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA PASSWORD IN TEMPO ED  BLOCCATA POTRESTI SBLOCCARE IL PC MFL0228 PER FAVORE GRAZIECIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUTLOOK CHE DOPO IL CAMBIO PC NON C PIGRZCIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRANET PER VISUALIZZARE MATERIALI COME MANUALI PRODOTTI ECC COME FACCIO 2 VORREI ACCEDERE A PROTIME COME FACCIO HO CERCATO MA NON VEDO IL PROGRAMMA SUL PC 3 MI HANNO DI CHIEDERVI DI ABILITARE IL MIO BADGE PER ACCEDERE ALLA PRODUZIONE IN VIA SIEMENSI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABHELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO NON RIESCO PI A CONNETTERMI A INTERNET CON IL MIO PC HO AVUTO QUESTO PROBLEMA QUALCHE SETTIMANA FA POTRESTI PER FAVORE CONTROLLARLO IL PRIMA POSSIBILE SALUTI HANS

Result 1:
HALLO BITTE DEN ORDNER  GPRODUKTIONPRODUKTIONSLEITUNG FR   PC C247ALPINL

In [109]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA PASSWORD IN TEMPO ED  BLOCCATA POTRESTI SBLOCCARE IL PC MFL0228 PER FAVORE GRAZIECIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUTLOOK CHE DOPO IL CAMBIO PC NON C PIGRZCIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRANET PER VISUALIZZARE MATERIALI COME MANUALI PRODOTTI ECC COME FACCIO 2 VORREI ACCEDERE A PROTIME COME FACCIO HO CERCATO MA NON VEDO IL PROGRAMMA SUL PC 3 MI HANNO DI CHIEDERVI DI ABILITARE IL MIO BADGE PER ACCEDERE ALLA PRODUZIONE IN VIA SIEMENSI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABHELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO NON RIESCO PI A CONNETTERMI A INTERNET CON IL MIO PC HO AVUTO QUESTO PROBLEMA QUALCHE SETTIMANA FA POTRESTI PER FAVORE CONTROLLARLO IL PRIMA POSSIBILE SALUTI HANS

Result 1:
HALLO BITTE DEN ORDNER  GPRODUKTIONPRODUKTIONSLEITUNG FR   PC C247ALPINL

['CIAO PENSO CHE\xa0LE YU YANG NON HA CAMBIATO LA PASSWORD IN TEMPO ED  BLOCCATA POTRESTI SBLOCCARE IL PC MFL0228\xa0PER FAVORE GRAZIECIAOMI POTETE AGGIUNGERE MIA SIGNATURA NELLOUTLOOK CHE DOPO IL CAMBIO PC NON C PIGRZCIAO RAGAZZI 1 VORREI ACCEDERE ALLA RETE INTRANET PER VISUALIZZARE MATERIALI COME MANUALI PRODOTTI ECC COME FACCIO 2 VORREI ACCEDERE A PROTIME COME FACCIO HO CERCATO MA NON VEDO IL PROGRAMMA SUL PC 3 MI HANNO DI CHIEDERVI DI ABILITARE IL MIO BADGE PER ACCEDERE ALLA PRODUZIONE IN VIA SIEMENSI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABHELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO NON RIESCO PI A CONNETTERMI A INTERNET CON IL MIO PC HO AVUTO QUESTO PROBLEMA QUALCHE SETTIMANA FA POTRESTI PER FAVORE CONTROLLARLO IL PRIMA POSSIBILE SALUTI HANS',
 'HALLO BITTE DEN ORDNER\xa0\xa0GPRODUKTIONPRODUKTIONSLEITUNG FR\xa0 \xa0PC C247ALP

In [110]:
picklefile = "df_1_computer_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "A new PC is not connected to the internet and I can't log in to my SAPCONCUR because I forgot my password. I have a new PC but can't connect it to the Internet because it's not connected with the Internet.   "}], [{'summary_text': 'HALLO BITTE DEN ORDNER: GPRODUKTION PRODUKTIONSLEITUNG FR, PC C247ALPIN LOCAL, FREIGEBEN NUR LESERECHTE DANKECIAO, HO CONTATTATO, STEPHANE, GRAZIEDANIELE MICHEL, FATTO LAGGIORNAMENTO, CHIESTO DAL, POI HA SPENTO E RIACCESO PERO ADESSO C QUESTO COSA DEVE FARENON CI SONO NELLA CARTELLA SPAM. '}], [{'summary_text': "There will be a new technician in France on May 15th. Her PC will be MFL0197, the same rightsprofile as SEBASTIEN COQUET's PC C235. It's not possible to connect DMS or NAVHLLO to the SVN server."}], [{'summary_text': 'All TAFR COLLABORATORS have signed a document in agreement with Human Resources Society to prevent the use of personal mobiles. The LAPTOP app does not work on the Laptop, so Daniele needs to find a solution for the 

# df_1_software

In [111]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_software[i:i+n] for i in range(0,len(df_1_software),n)]
    #print(list_df)

In [112]:
len(list_df)

29

In [113]:
list_df[28]

Title                                              Topic  \
168  Sap Concur Login   {"16":"User identity management, Permissions, ...   

                                                  Text  
168  CIAO MANUEL MI SPIACE DISTURBARTI MA TI CONFER...

In [114]:
def put_together():
    list1=[]
    for index in range(0,28):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [115]:
summ_block = put_together()
summ_block

Result 0:
HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN FUER NEUE KOLEGIN LENKA SEVCIKOVA  SIE WIRD EIN TEAMVIEWER SCHICKEN  UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE KOENNEN SIE DAS AUCH SCHAUEN   DANKE ZUZANAOK ABER WIR KOENNEN NICHT SERVER FINDEN UND OFFNENI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABCIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE MI HA DATO I DIRITTI PER QUEI SERVERIO NON LI VEDO ANCORA DEVO FARE QUALCOSA SUL MIO PCDOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSIBILE MANDARE EMAIL DALLINDIRIZZO INFOEPOWERTRACCOM MA IN AUTOMATICO UTILIZZA LINDIRIZZO DELLUSER CHE STA SCRIVENDO  SALVANDO NELLUSCITA OUTLOOK DELLA PERSONA  NECESSERIO RIPRISTINARE   GRAZIE HELLO  ITS IMPOSSIBLE FOR ME TO CONNECT TO MN OR S SERVER IN BUILDING PRODUCTION  VIA SIEMENS BY WIFI IN VIA AGOSTINI ITS OK   MY TEAMVIEWER BR VINCENT BAUDOUIN

Result 1:
CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI COLLEGHI CHE INIZIERANNO LA PROSSIMA SETTIMANA LUNED  1 JOHANNES RIEDERI DIRITTI LACCES

['HALLO\xa0 KOENNEN SIE BITTE LSERVER INSTALLIEREN FUER NEUE KOLEGIN LENKA SEVCIKOVA\xa0 SIE WIRD EIN TEAMVIEWER SCHICKEN\xa0 UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE KOENNEN SIE DAS AUCH SCHAUEN \xa0 DANKE ZUZANAOK ABER WIR KOENNEN NICHT SERVER FINDEN UND\xa0OFFNENI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABCIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE MI HA DATO I DIRITTI PER QUEI SERVERIO NON LI VEDO ANCORA DEVO FARE QUALCOSA SUL MIO PCDOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSIBILE MANDARE EMAIL DALLINDIRIZZO INFOEPOWERTRACCOM MA IN AUTOMATICO UTILIZZA LINDIRIZZO DELLUSER CHE STA SCRIVENDO  SALVANDO NELLUSCITA OUTLOOK DELLA PERSONA  NECESSERIO RIPRISTINARE\xa0  GRAZIE\xa0HELLO\xa0 ITS IMPOSSIBLE FOR ME TO CONNECT TO MN OR S SERVER IN BUILDING PRODUCTION  VIA SIEMENS BY WIFI IN VIA AGOSTINI ITS OK   MY TEAMVIEWER BR VINCENT BAUDOUIN',
 'CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI COLLEGHI CHE INIZIERANNO LA PROSSIMA SETTIMANA LUNED\xa0 1 JOHANNES RIEDERI DI

In [116]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 28):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [117]:
blocks_to_skip = [3,4,12]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN FUER NEUE KOLEGIN LENKA SEVCIKOVA  SIE WIRD EIN TEAMVIEWER SCHICKEN  UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE KOENNEN SIE DAS AUCH SCHAUEN   DANKE ZUZANAOK ABER WIR KOENNEN NICHT SERVER FINDEN UND OFFNENI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABCIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE MI HA DATO I DIRITTI PER QUEI SERVERIO NON LI VEDO ANCORA DEVO FARE QUALCOSA SUL MIO PCDOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSIBILE MANDARE EMAIL DALLINDIRIZZO INFOEPOWERTRACCOM MA IN AUTOMATICO UTILIZZA LINDIRIZZO DELLUSER CHE STA SCRIVENDO  SALVANDO NELLUSCITA OUTLOOK DELLA PERSONA  NECESSERIO RIPRISTINARE   GRAZIE HELLO  ITS IMPOSSIBLE FOR ME TO CONNECT TO MN OR S SERVER IN BUILDING PRODUCTION  VIA SIEMENS BY WIFI IN VIA AGOSTINI ITS OK   MY TEAMVIEWER BR VINCENT BAUDOUIN

Result 1:
CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI COLLEGHI CHE INIZIERANNO LA PROSSIMA SETTIMANA LUNED  1 JOHANNES RIEDERI DIRITTI LACCES

In [118]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
HALLO  KOENNEN SIE BITTE LSERVER INSTALLIEREN FUER NEUE KOLEGIN LENKA SEVCIKOVA  SIE WIRD EIN TEAMVIEWER SCHICKEN  UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE KOENNEN SIE DAS AUCH SCHAUEN   DANKE ZUZANAOK ABER WIR KOENNEN NICHT SERVER FINDEN UND OFFNENI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABCIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE MI HA DATO I DIRITTI PER QUEI SERVERIO NON LI VEDO ANCORA DEVO FARE QUALCOSA SUL MIO PCDOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSIBILE MANDARE EMAIL DALLINDIRIZZO INFOEPOWERTRACCOM MA IN AUTOMATICO UTILIZZA LINDIRIZZO DELLUSER CHE STA SCRIVENDO  SALVANDO NELLUSCITA OUTLOOK DELLA PERSONA  NECESSERIO RIPRISTINARE   GRAZIE HELLO  ITS IMPOSSIBLE FOR ME TO CONNECT TO MN OR S SERVER IN BUILDING PRODUCTION  VIA SIEMENS BY WIFI IN VIA AGOSTINI ITS OK   MY TEAMVIEWER BR VINCENT BAUDOUIN

Result 1:
CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI COLLEGHI CHE INIZIERANNO LA PROSSIMA SETTIMANA LUNED  1 JOHANNES RIEDERI DIRITTI LACCES

['HALLO\xa0 KOENNEN SIE BITTE LSERVER INSTALLIEREN FUER NEUE KOLEGIN LENKA SEVCIKOVA\xa0 SIE WIRD EIN TEAMVIEWER SCHICKEN\xa0 UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE KOENNEN SIE DAS AUCH SCHAUEN \xa0 DANKE ZUZANAOK ABER WIR KOENNEN NICHT SERVER FINDEN UND\xa0OFFNENI HAVE A NEW PC BUT I CANT CONNECT SERVERS TAFR ET TABCIAO HO CONTATTATO STEPHANE E MI HA DETTO CHE MI HA DATO I DIRITTI PER QUEI SERVERIO NON LI VEDO ANCORA DEVO FARE QUALCOSA SUL MIO PCDOPO IL CAMBIAMENTO SERVER SU TA NON  PI POSSIBILE MANDARE EMAIL DALLINDIRIZZO INFOEPOWERTRACCOM MA IN AUTOMATICO UTILIZZA LINDIRIZZO DELLUSER CHE STA SCRIVENDO  SALVANDO NELLUSCITA OUTLOOK DELLA PERSONA  NECESSERIO RIPRISTINARE\xa0  GRAZIE\xa0HELLO\xa0 ITS IMPOSSIBLE FOR ME TO CONNECT TO MN OR S SERVER IN BUILDING PRODUCTION  VIA SIEMENS BY WIFI IN VIA AGOSTINI ITS OK   MY TEAMVIEWER BR VINCENT BAUDOUIN',
 'CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI COLLEGHI CHE INIZIERANNO LA PROSSIMA SETTIMANA LUNED\xa0 1 JOHANNES RIEDERI DI

In [119]:
picklefile = "df_1_software_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'HALLO, KOENEN SIE BITTE, FUER NEUE, LENKA SEVCIKOVA, SIE WIRD EIN TEAMVIEWER SCHICKEN, UND DRUCKER FUNKCIONIERT ABER SCANER GEHT NICHT BITTE and DANKE ZUZANAOK ABER WIR.'}], [{'summary_text': 'There are 2 accounts to choose from: JOHANNES RIEDERI, DIRITTI LACCESSO SERVER EMAILSEGNATURA and LUKAS MESSNER. IM MISSING ACCESS TO THE CARQUEFOU SERVER MFS MPLEASE, I need to work. '}], [{'summary_text': "I don't have an access to the servers. I am looking for information on how to access them. I also need to contact the service provider.    The information on the services I need can be found on the following websites: \xa0http://www.servicom.com,  "}], [{'summary_text': 'Laccasso has set up a MySpace server. He has also set it up in UFFICIO SENZA HOTSPOT. His NAV licence is still not active, so he needs to find a solution for that. He needs to solve the issue with his NAV licence.'}], [{'summary_text': "I am still having problems getting access to the network. I can't chan

# df_2_pc

In [120]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_pc[i:i+n] for i in range(0,len(df_2_pc),n)]
    #print(list_df)

In [121]:
len(list_df)

40

In [122]:
list_df[39]

Title  \
273        Accesso VPN e verifica collegamenti disco L   
274  Accesso http://web01/erticket/scp/login.php pe...   
275       Installare accesso VPN/CITRIX sul mio Laptop   
276                       nuovo accesi radix su citrix   

                                                 Topic  \
273  {"12":"Standard Software: Operating systems, M...   
274  {"12":"Standard Software: Operating systems, M...   
275  {"12":"Standard Software: Operating systems, M...   
276  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
273  BUONGIORNO NECESSITO DI CONFIGURARE IL MIO LAP...  
274  DEVO CHIEDERE A VOI LACCESSO AL TICKETING SYST...  
275  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...  
276  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...

In [123]:
def put_together():
    list1=[]
    for index in range(0,39):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [124]:
summ_block = put_together()
summ_block

Result 0:
CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANHALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEINT PROCALL NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLERMELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN   SIEHE SCREENSHOT HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTRIA DOESNT WORK COULD YOU HELP ME  BEST REGARDSSERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN PC TEAMVIEWER QUI 396 743 870YEB2GFNDCIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC ED ORA FUNZIONA BOH PER ME  RISOLTO GRAZIESALVEIN OUTLOOK DAL MIO LAPTOP LA FIRMA MANCA SE SCRIVO DAL MIO PC DEL FOYER INVECE LA FIRMA APPARE  GRAZIE DOPO AVER SPENTO IL PC C138 SETTIMANA SCORSA PER I LAVORI IN TA E RIACCESSO OGGI HO QUESTO BLUESCREEN 

Result 1:
ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VENDITORE MACCHINE AGRICOLE E COME CONCORDATO CON MARTIN E PRENDER IL SUO HARDWARE PC MONITOR CELLULARE ECC

['CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANHALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEINT PROCALL NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLERMELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN   SIEHE SCREENSHOT HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTRIA DOESNT WORK COULD YOU HELP ME  BEST REGARDSSERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN PC TEAMVIEWER QUI 396 743 870YEB2GFNDCIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC ED ORA FUNZIONA BOH PER ME  RISOLTO GRAZIESALVEIN OUTLOOK DAL MIO LAPTOP\xa0LA FIRMA MANCA\xa0SE SCRIVO DAL MIO PC DEL FOYER INVECE LA FIRMA APPARE  GRAZIE DOPO AVER SPENTO IL PC\xa0C138 SETTIMANA SCORSA PER I LAVORI IN TA E RIACCESSO OGGI HO QUESTO BLUESCREEN\xa0',
 'ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VENDITORE MACCHINE AGRICOLE E COME CONCORDATO CON MARTIN E PRENDER IL SUO HARDWARE PC MONITOR CELLULARE ECC\xa

In [125]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 39):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [126]:
blocks_to_skip = [16]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANHALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEINT PROCALL NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLERMELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN   SIEHE SCREENSHOT HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTRIA DOESNT WORK COULD YOU HELP ME  BEST REGARDSSERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN PC TEAMVIEWER QUI 396 743 870YEB2GFNDCIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC ED ORA FUNZIONA BOH PER ME  RISOLTO GRAZIESALVEIN OUTLOOK DAL MIO LAPTOP LA FIRMA MANCA SE SCRIVO DAL MIO PC DEL FOYER INVECE LA FIRMA APPARE  GRAZIE DOPO AVER SPENTO IL PC C138 SETTIMANA SCORSA PER I LAVORI IN TA E RIACCESSO OGGI HO QUESTO BLUESCREEN 

Result 1:
ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VENDITORE MACCHINE AGRICOLE E COME CONCORDATO CON MARTIN E PRENDER IL SUO HARDWARE PC MONITOR CELLULARE ECC

In [127]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANHALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEINT PROCALL NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLERMELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN   SIEHE SCREENSHOT HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTRIA DOESNT WORK COULD YOU HELP ME  BEST REGARDSSERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN PC TEAMVIEWER QUI 396 743 870YEB2GFNDCIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC ED ORA FUNZIONA BOH PER ME  RISOLTO GRAZIESALVEIN OUTLOOK DAL MIO LAPTOP LA FIRMA MANCA SE SCRIVO DAL MIO PC DEL FOYER INVECE LA FIRMA APPARE  GRAZIE DOPO AVER SPENTO IL PC C138 SETTIMANA SCORSA PER I LAVORI IN TA E RIACCESSO OGGI HO QUESTO BLUESCREEN 

Result 1:
ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VENDITORE MACCHINE AGRICOLE E COME CONCORDATO CON MARTIN E PRENDER IL SUO HARDWARE PC MONITOR CELLULARE ECC

['CIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANHALLO AUCH NACH EINEM NEUSTART MEINES PC SCHEINT PROCALL NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLERMELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN   SIEHE SCREENSHOT HI I HAVE A NEW PC NAV FR AND ITALIE AND AUSTRIA DOESNT WORK COULD YOU HELP ME  BEST REGARDSSERVIREBBE LINSTALLAZIONE DI WINDOWS 10 SU UN PC TEAMVIEWER QUI 396 743 870YEB2GFNDCIAO ARASHDEEP SCUSAMI MA HO RIAVVIATO IL PC ED ORA FUNZIONA BOH PER ME  RISOLTO GRAZIESALVEIN OUTLOOK DAL MIO LAPTOP\xa0LA FIRMA MANCA\xa0SE SCRIVO DAL MIO PC DEL FOYER INVECE LA FIRMA APPARE  GRAZIE DOPO AVER SPENTO IL PC\xa0C138 SETTIMANA SCORSA PER I LAVORI IN TA E RIACCESSO OGGI HO QUESTO BLUESCREEN\xa0',
 'ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VENDITORE MACCHINE AGRICOLE E COME CONCORDATO CON MARTIN E PRENDER IL SUO HARDWARE PC MONITOR CELLULARE ECC\xa

In [128]:
import pickle

In [129]:
picklefile = "df_2_pc_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'CIAO POTETE INSTALLARE DYNAMICS, E ANCHE IL VPN, QUANDO SONO SU UNA MESSA, SERVIZIO GRAZIE IVANHALLO, NACH EINEM NEUSTART MEINES, SCHEINT PROCALL, NICHT RICHTIG ZU FUNKTIONIEREN ES TAUCHEN IMMER WIEDER FEHLER, MELDUNGEN AUF AUCH EINE MASKE BEI DER ICH AUFGEFORDERT WERDE MEIN PASSWORT EINZUGEBEN.'}], [{'summary_text': 'Arnold has installed the new software for the project. He would like to have the English and Spanish versions of the software installed with all Macros and Printers as well as PDF LowPC3. The phase 2 of the maintenance of the project is almost over.'}], [{'summary_text': 'AGGIORNAMENTO PCSOFTWARE is not working. There are problems with the VPN network. Francisco will fix it for his colleague. He will also help his colleague with printing from PDF LowPC3 without the lines going through the slops. '}], [{'summary_text': 'HALLO KNNTEST DU MIR, EINE FREIGABE FR EINE REMOTEDESKTOPVERBINDUNG, GEBEN BRAUCHE ICH UM AUF DEM PRFSTAND ECOSNOW WO DER PC STEHT ZUZU

# df_2_email

In [130]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [df_2_email[i:i+n] for i in range(0,len(df_2_email),n)]
    #print(list_df)

In [131]:
len(list_df)

94

In [132]:
list_df[93]

Title  \
465  Installare accesso VPN/CITRIX sul mio Laptop   
466                  nuovo accesi radix su citrix   

                                                 Topic  \
465  {"12":"Standard Software: Operating systems, M...   
466  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
465  INSTALLARE ACCESSO VPNCITRIX SUL MIO LAPTOP UR...  
466  CIAOMI SERVE LACCESSO DI RADIX SU CITRIX PER S...

In [133]:
def put_together():
    list1=[]
    for index in range(0,93):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [134]:
summ_block = put_together()
summ_block

Result 0:
 BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN WICHTIG DANKE  FEHLERMELDUNG VOM VERSENDER SIEHE UNTEN    MAG MATTHIAS ILLMER GESCHFTSFHRER  MANAGING DIRECTOR TECHNOALPIN AUSTRIA GMBH  AT  6111  VOLDERS  JOHANNESKAPELLENWEG 2 T 43 5224 209 09 322  M 43 664 8844 9700  F 43 5224 209 09 350  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE VON BARENTH  PARTNER  HUSC  GESENDET MONTAG 21 AUGUST 2023 1003 AN MATTHIAS ILLMER  BETREFF FEHLERMELDUNG     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT         SEHR GEEHRTER HR ILLMER   WIE SOEBEN TEL BESPROCHEN HIER DIE FEHLERMELDUNG DIE WIR ERHALTEN HABEN MIT DER BITTE UM FEHLERPRFUNG BZW WHITELISTEN DER SENDEADRESSEN WACHSTEUERBERATUNGAT   FEHLER BEI DER NACHRICHTENZUSTELLUNG AN FOLGENDE EMPFNGER ODER GRUPPEN MATTHIASILLMERTECHNOALPINAT IHRE NACHRICHT WURDE AUFGRUND EINES BERECHTIGUNGS ODER SICHERHEITSPROBLEMS NICHT ZUGESTELLT SIE WURDE MG

[' BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN WICHTIG DANKE  FEHLERMELDUNG VOM VERSENDER SIEHE UNTEN  \xa0 MAG MATTHIAS ILLMER GESCHFTSFHRER  MANAGING DIRECTOR TECHNOALPIN AUSTRIA GMBH  AT  6111  VOLDERS  JOHANNESKAPELLENWEG 2 T 43 5224 209 09 322  M 43 664 8844 9700  F 43 5224 209 09 350  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE VON BARENTH  PARTNER  HUSC  GESENDET MONTAG 21 AUGUST 2023 1003 AN MATTHIAS ILLMER  BETREFF FEHLERMELDUNG   \xa0 CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT       \xa0 SEHR GEEHRTER HR ILLMER \xa0 WIE SOEBEN TEL BESPROCHEN HIER DIE FEHLERMELDUNG DIE WIR ERHALTEN HABEN MIT DER BITTE UM FEHLERPRFUNG BZW WHITELISTEN DER SENDEADRESSEN WACHSTEUERBERATUNGAT \xa0 FEHLER BEI DER NACHRICHTENZUSTELLUNG AN FOLGENDE EMPFNGER ODER GRUPPEN MATTHIASILLMERTECHNOALPINAT IHRE NACHRICHT WURDE AUFGRUND EINES BERECHTIGUNGS ODER SICHERHEITSPROBLEMS NICHT ZUGESTELLT SIE W

In [135]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 93):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [136]:
blocks_to_skip = [0,1,3,4,12,14,22,25,27,29,47,62,63,66,67,69,70,77]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 2:
HALLO ZUSAMMEN WIR HABEN GESTERN DIE MITTEILUNG ERHALTEN DASS SMTLICHE EMAILS ACCOUNTS UNSERER FILIALE IN CANADA NICHT FUNKTIONIEREN DIE EMAIL ACCOUNTS SIND FOLGENDE DAVIDSTEWARTENGOICECOM  DAVID HAT ZB TELEFONATE ERHALTEN DASS DIE AN IHN GESENDETEN EMAILS MIT DER RCKANTWORT ZURCKKAMEN DASS SIE AN DEN EMPFNGER NICHT ZUGESTELLT WERDEN KONNTEN STEVEDAVEENGOICECOM TODDLANGERENGOICECOM  DA ES SICH UM OFFIZIELLE EMAILS ACCOUNTS HANDELT AUCH FR DIE EINGABE VON ANGEBOTEN IN BEZUG AUF AUSSCHREIBUNGEN BITTE ICH EUCH DAS PROBLEM SO SCHNELL WIE MGLICH ZU BEHEBEN  VIELEN DANK FR DIE SCHNELLE ERLEDIGUNG UND MIT BESTEN GREN MARKUS PROFANTER BEIM VERSUCH EINE EMAIL AN GEORGENGLENGOICECOM ZU SCHICKENLA COLLEGA LEA ALBER NON RICEVE EMAIL E NON RICEVE NE MANDA MESSAGGI SU TEAMSHII CANT GET BY MY OUTLOOK TO OPEN ON MY COMPUTER SO I AM HAVING TROUBLE WITH EMAILSCAN SOMEONE FROM IT LOG ON TO MY COMPUTER AND SEE WHAT IS HAPPENING MY ID IS 1 594 117 172 TEAM VIEWER PASSWORD BJYUQGIJ THANKS DAVESENT

In [137]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 2:
HALLO ZUSAMMEN WIR HABEN GESTERN DIE MITTEILUNG ERHALTEN DASS SMTLICHE EMAILS ACCOUNTS UNSERER FILIALE IN CANADA NICHT FUNKTIONIEREN DIE EMAIL ACCOUNTS SIND FOLGENDE DAVIDSTEWARTENGOICECOM  DAVID HAT ZB TELEFONATE ERHALTEN DASS DIE AN IHN GESENDETEN EMAILS MIT DER RCKANTWORT ZURCKKAMEN DASS SIE AN DEN EMPFNGER NICHT ZUGESTELLT WERDEN KONNTEN STEVEDAVEENGOICECOM TODDLANGERENGOICECOM  DA ES SICH UM OFFIZIELLE EMAILS ACCOUNTS HANDELT AUCH FR DIE EINGABE VON ANGEBOTEN IN BEZUG AUF AUSSCHREIBUNGEN BITTE ICH EUCH DAS PROBLEM SO SCHNELL WIE MGLICH ZU BEHEBEN  VIELEN DANK FR DIE SCHNELLE ERLEDIGUNG UND MIT BESTEN GREN MARKUS PROFANTER BEIM VERSUCH EINE EMAIL AN GEORGENGLENGOICECOM ZU SCHICKENLA COLLEGA LEA ALBER NON RICEVE EMAIL E NON RICEVE NE MANDA MESSAGGI SU TEAMSHII CANT GET BY MY OUTLOOK TO OPEN ON MY COMPUTER SO I AM HAVING TROUBLE WITH EMAILSCAN SOMEONE FROM IT LOG ON TO MY COMPUTER AND SEE WHAT IS HAPPENING MY ID IS 1 594 117 172 TEAM VIEWER PASSWORD BJYUQGIJ THANKS DAVESENT

['HALLO ZUSAMMEN WIR HABEN GESTERN DIE MITTEILUNG ERHALTEN DASS SMTLICHE EMAILS ACCOUNTS UNSERER FILIALE IN CANADA NICHT FUNKTIONIEREN DIE EMAIL ACCOUNTS SIND FOLGENDE DAVIDSTEWARTENGOICECOM\xa0 DAVID HAT ZB TELEFONATE ERHALTEN DASS DIE AN IHN GESENDETEN EMAILS MIT DER RCKANTWORT ZURCKKAMEN DASS SIE AN DEN EMPFNGER NICHT ZUGESTELLT WERDEN KONNTEN STEVEDAVEENGOICECOM TODDLANGERENGOICECOM\xa0 DA ES SICH UM OFFIZIELLE EMAILS ACCOUNTS HANDELT AUCH FR DIE EINGABE VON ANGEBOTEN IN BEZUG AUF AUSSCHREIBUNGEN BITTE ICH EUCH DAS PROBLEM SO SCHNELL WIE MGLICH ZU BEHEBEN\xa0 VIELEN DANK FR DIE SCHNELLE ERLEDIGUNG UND MIT BESTEN GREN MARKUS PROFANTER BEIM VERSUCH EINE EMAIL AN GEORGENGLENGOICECOM ZU SCHICKENLA COLLEGA LEA ALBER NON RICEVE EMAIL E NON RICEVE NE MANDA MESSAGGI SU TEAMSHII CANT GET BY MY OUTLOOK TO OPEN ON MY COMPUTER SO I AM HAVING TROUBLE WITH EMAILSCAN SOMEONE FROM IT LOG ON TO MY COMPUTER AND SEE WHAT IS HAPPENING MY ID IS 1 594 117 172 TEAM VIEWER PASSWORD BJYUQGIJ THANKS DAVESEN

In [138]:
picklefile = "df_2_email_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'HALLO ZUSAMMEN WIR HABEN GESTERN, MIT TELEFONATE ERHALTEN DASS SMTLICHE EMAILS ACCOUNTS UNSERER FILIALE IN CANADA, SIND FOLGENDE, DAVIDSTEWARTENGOICECOM, MIT RCKANTWORT, ZURCKKAMEN, ZUGESTELLT, WERDEN KONNTEN, STEVEDAVEEN GOICECOME, DA ES SICH UM OFFIZIELLE, SCHNELL WIE MGLICH, VIELEN DANK FR, SCHNELLE'}], [{'summary_text': "A lot of Mike's e-mails are going directly into his junk e-mail account. He is having an issue with the recipient not having an attached attachment. He might be blocked if he doesn't have an attached link.    Michael is a criminal. "}], [{'summary_text': "The team leader of the German football team is sick and needs to be contacted by e-mail to get the team's approval. The team leader needs to approve the email before it can be sent. The e-mails will be sent by the team leader. "}], [{'summary_text': " HELLOSINCE needs help with updating Windows or Office. He has problems with VPN and the CITRIX Inlogger. He can't reach the Internet. He leaves h

# df_2_access

In [139]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_access[i:i+n] for i in range(0,len(df_2_access),n)]
    #print(list_df)

In [140]:
len(list_df)

28

In [141]:
list_df[27]

Title                                              Topic  \
189  Setup nuovo PC  {"12":"Standard Software: Operating systems, M...   
190  Update Windows  {"12":"Standard Software: Operating systems, M...   
191         Mapedit  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
189  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...  
190  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...  
191  CAN YOU ALSO GIVE ME SIGNING DETAILS USERNAME ...

In [142]:
def put_together():
    list1=[]
    for index in range(0,27):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE SALUTIALEXABUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO AD APRIRE OUTLOOK E SU TEAMS COMPARE IL MESSAGGIO DI ACCEDERE GRAZIE MILLEHALLO BITTE AUF GERT L295 MICROSOFT DYNAMICS NAVISION UND TEAMS INSTALLIEREN DANKE UND GRU LUKASLA COLLEGA LEA ALBER NON RICEVE EMAIL E

['CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0 GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE SALUTIALEXABUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO AD APRIRE OUTLOOK E SU TEAMS COMPARE IL MESSAGGIO DI ACCEDERE GRAZIE MILLEHALLO BITTE AUF GERT L295 MICROSOFT DYNAMICS NAVISION UND TEAMS INSTALLIEREN DANKE UND GRU LUKASLA COLLEGA LEA ALBER NON RICEVE EMAIL E NON 

In [143]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 27):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [144]:
blocks_to_skip = [17]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE SALUTIALEXABUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO AD APRIRE OUTLOOK E SU TEAMS COMPARE IL MESSAGGIO DI ACCEDERE GRAZIE MILLEHALLO BITTE AUF GERT L295 MICROSOFT DYNAMICS NAVISION UND TEAMS INSTALLIEREN DANKE UND GRU LUKASLA COLLEGA LEA ALBER NON RICEVE EMAIL E

In [145]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE SALUTIALEXABUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO AD APRIRE OUTLOOK E SU TEAMS COMPARE IL MESSAGGIO DI ACCEDERE GRAZIE MILLEHALLO BITTE AUF GERT L295 MICROSOFT DYNAMICS NAVISION UND TEAMS INSTALLIEREN DANKE UND GRU LUKASLA COLLEGA LEA ALBER NON RICEVE EMAIL E

['CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0 GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE SALUTIALEXABUONGIORNO IL PRESENTE TICKET PERCH NON RIESCO AD APRIRE OUTLOOK E SU TEAMS COMPARE IL MESSAGGIO DI ACCEDERE GRAZIE MILLEHALLO BITTE AUF GERT L295 MICROSOFT DYNAMICS NAVISION UND TEAMS INSTALLIEREN DANKE UND GRU LUKASLA COLLEGA LEA ALBER NON RICEVE EMAIL E NON 

In [146]:
picklefile = "df_2_access_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "Teams are meeting in Italy. The agenda for the meeting is due to a new program. There is a link to the meeting's website and an out-of-the-box outlook for the upcoming year. The out-to-date outlook is compared to the previous year."}], [{'summary_text': 'HALLO ICH KANN IM WLAN VON TECHNOALPIN AUSTRIA GMBH KEINE VERBINDUNG ZU OFFICE UND TEAMS AUFBAUEN BITTE BEI BEHEBUNG AUCH GLEICH DRUCKER VON TUNISIA. '}], [{'summary_text': 'Teams per funzioni compete in the following games: AQUANDO APRO UNA NUOVA RIUNIONE AUTOMATICAMENTE, SI IMPOSTA SU TEAMS ANCHE SE DEVE ESSERE IN PRESENZACIAOPREGO VERIFICARE PERCH, LA MAIL E. GABRIELE CLOCH\xa0SEMBRA CHE C UN PROBLEMA CON SUO UTENTEGRAZIESALUTIHANNES CIAO STA MATTINA HO CAMBIATO LA MIA PASSWORT, RIESCO ANTHE A ENTRARE NEL'}], [{'summary_text': 'Teams.co.uk has created a website with a lookalike of the games they play. The website is available in Italian, German, Spanish, Italian, and in English. It is available on the following p

# df_2_software 

In [147]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_software[i:i+n] for i in range(0,len(df_2_software),n)]
    #print(list_df)

In [148]:
len(list_df)

30

In [149]:
list_df[29]

Title  \
203                     Setup nuovo PC   
204                 Solide Edge Lizenz   
205           Aggiornamento Docfinance   
206  Indirizzo E-Mail per l'utente NDF   
207  Indirizzo E-Mail per l'utente NDF   
208          Unable to log in on mail.   
209  Excel per Server profile-app-prod   

                                                 Topic  \
203  {"12":"Standard Software: Operating systems, M...   
204  {"12":"Standard Software: Operating systems, M...   
205  {"12":"Standard Software: Operating systems, M...   
206  {"12":"Standard Software: Operating systems, M...   
207  {"12":"Standard Software: Operating systems, M...   
208  {"12":"Standard Software: Operating systems, M...   
209  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
203  UPDATE NON DOBBIAMO INSTALLARLO MA C DA SISTEM...  
204  ERA IL SERVER DI LICENZA GRAZIE ADESSA FUNZION...  
205  CIAO LA MIGRAZIONE SUL NUOVO SERVER SEMBRA AND...  
206  VOGLIAMO CHE LNDF CI MANDA UN EMAIL NEL CASO Q...  
207  SERVONO PER UN SERVIZIO DI TRISOFT CHE DEVE MA...  
208  OUR SERVICE TECHNICAN IS UNABLE TO RECIVE MAIL...  
209  CI SERVIREBBE EXCEL SUL SERVER PROFILEAPPPROD ...

In [150]:
def put_together():
    list1=[]
    for index in range(0,29):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA MACCHINA C255  LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANCIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO SERVICE PACK DI SOLID EDGE SP7GRAZIECIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT  IMPORTANTE  COME PARLATO CON MANUEL FURLOTTI METTERE NEL SILENT INSTALLER LA VERSIONE 64BIT E TOGLIERE LA 32 BIT CHE  OBOLETA DA MO E CREA PROBLEMI POTETE INSTALLARE ACROBAT 64 BIT DA  DAVID TSCHAGER JANEZ ZGAGACIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  IT DEPARTMENT INSTALLARE IL SOFTWARE PROFILE SUL LAPTOP L482 ASSEGNATO A FELIX LOCHMANN   ALEX BORGIA CREARE UNA USER IN GRADO DI SCRIVERE UPLOADING DI FILE DI DISEGNO FELIX LOCHMANN FELIXLOCHMANNTECHNOALPINCOM A DISPOSIZIONE PER CHIARIMENTI GRAZIE IN ANTICIPO LORENZOCIAO MI POTETE PER FAVORE INSTALLARE IL D3 EXPLORER GRAZIECIAO DA OLEOMEC CE UN PC CHE NON E ANCOR

['PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA MACCHINA C255  LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANCIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO SERVICE PACK DI SOLID EDGE SP7GRAZIECIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT  IMPORTANTE  COME PARLATO CON MANUEL FURLOTTI METTERE NEL SILENT INSTALLER LA VERSIONE 64BIT E TOGLIERE LA 32 BIT CHE  OBOLETA DA MO E CREA PROBLEMI POTETE INSTALLARE ACROBAT 64 BIT DA  DAVID TSCHAGER JANEZ ZGAGACIAO COME DISCUSSO A VOCE\xa0CHIEDO PER FAVORE  IT DEPARTMENT\xa0INSTALLARE IL SOFTWARE PROFILE SUL LAPTOP L482 ASSEGNATO A FELIX LOCHMANN  \xa0ALEX BORGIA\xa0CREARE UNA USER IN GRADO DI SCRIVERE UPLOADING DI FILE DI DISEGNO FELIX LOCHMANN FELIXLOCHMANNTECHNOALPINCOM A DISPOSIZIONE PER CHIARIMENTI GRAZIE IN ANTICIPO LORENZOCIAO MI POTETE PER FAVORE INSTALLARE IL D3 EXPLORER GRAZIECIAO DA OLEOMEC CE UN PC CHE NON E A

In [151]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 29):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [152]:
blocks_to_skip = [15,27,28]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)


Result 0:
PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA MACCHINA C255  LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANCIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO SERVICE PACK DI SOLID EDGE SP7GRAZIECIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT  IMPORTANTE  COME PARLATO CON MANUEL FURLOTTI METTERE NEL SILENT INSTALLER LA VERSIONE 64BIT E TOGLIERE LA 32 BIT CHE  OBOLETA DA MO E CREA PROBLEMI POTETE INSTALLARE ACROBAT 64 BIT DA  DAVID TSCHAGER JANEZ ZGAGACIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  IT DEPARTMENT INSTALLARE IL SOFTWARE PROFILE SUL LAPTOP L482 ASSEGNATO A FELIX LOCHMANN   ALEX BORGIA CREARE UNA USER IN GRADO DI SCRIVERE UPLOADING DI FILE DI DISEGNO FELIX LOCHMANN FELIXLOCHMANNTECHNOALPINCOM A DISPOSIZIONE PER CHIARIMENTI GRAZIE IN ANTICIPO LORENZOCIAO MI POTETE PER FAVORE INSTALLARE IL D3 EXPLORER GRAZIECIAO DA OLEOMEC CE UN PC CHE NON E ANCOR

In [153]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA MACCHINA C255  LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANCIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO SERVICE PACK DI SOLID EDGE SP7GRAZIECIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT  IMPORTANTE  COME PARLATO CON MANUEL FURLOTTI METTERE NEL SILENT INSTALLER LA VERSIONE 64BIT E TOGLIERE LA 32 BIT CHE  OBOLETA DA MO E CREA PROBLEMI POTETE INSTALLARE ACROBAT 64 BIT DA  DAVID TSCHAGER JANEZ ZGAGACIAO COME DISCUSSO A VOCE CHIEDO PER FAVORE  IT DEPARTMENT INSTALLARE IL SOFTWARE PROFILE SUL LAPTOP L482 ASSEGNATO A FELIX LOCHMANN   ALEX BORGIA CREARE UNA USER IN GRADO DI SCRIVERE UPLOADING DI FILE DI DISEGNO FELIX LOCHMANN FELIXLOCHMANNTECHNOALPINCOM A DISPOSIZIONE PER CHIARIMENTI GRAZIE IN ANTICIPO LORENZOCIAO MI POTETE PER FAVORE INSTALLARE IL D3 EXPLORER GRAZIECIAO DA OLEOMEC CE UN PC CHE NON E ANCOR

['PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA MACCHINA C255  LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN PER ACCEDERE AGLI DRIVE QUANDO SONO SU UNA MESSA IN SERVIZIO GRAZIE IVANCIAOMI POTETE PER FAVORE INSTALLARE IL NUOVO SERVICE PACK DI SOLID EDGE SP7GRAZIECIAO RIAPRO LA QUESTIONE ACROBAT READER 64BIT  IMPORTANTE  COME PARLATO CON MANUEL FURLOTTI METTERE NEL SILENT INSTALLER LA VERSIONE 64BIT E TOGLIERE LA 32 BIT CHE  OBOLETA DA MO E CREA PROBLEMI POTETE INSTALLARE ACROBAT 64 BIT DA  DAVID TSCHAGER JANEZ ZGAGACIAO COME DISCUSSO A VOCE\xa0CHIEDO PER FAVORE  IT DEPARTMENT\xa0INSTALLARE IL SOFTWARE PROFILE SUL LAPTOP L482 ASSEGNATO A FELIX LOCHMANN  \xa0ALEX BORGIA\xa0CREARE UNA USER IN GRADO DI SCRIVERE UPLOADING DI FILE DI DISEGNO FELIX LOCHMANN FELIXLOCHMANNTECHNOALPINCOM A DISPOSIZIONE PER CHIARIMENTI GRAZIE IN ANTICIPO LORENZOCIAO MI POTETE PER FAVORE INSTALLARE IL D3 EXPLORER GRAZIECIAO DA OLEOMEC CE UN PC CHE NON E A

In [154]:
picklefile = "df_2_software_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "Installing the software is easy. It's recommended to install the following files:    Excel EDGEL ED OUTLOOK SU LA MACCHINA C255, LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN. "}], [{'summary_text': 'Team Viewer 1 895 609 981 PSW CF99MA4U,   GRAZIE MILLECIAO, MI POTETE INSTALLARE, IL PACHETTO OFFICE WORD EXCEL, DOPO LO SPOSTAMENTO, DELLA MIA UTENZA SU TA NON FUNZIONA PI LACROBAT WRITER PER MODIFICAREELABORARE PDF, GPRODUCT COMPLIANCEMANAGEMENT08.08.'}], [{'summary_text': 'There are ten ways to install a program on a computer. The program is called BUONGIORNO,    NUOVA STAMPANTE EPOWERTRAC GENTILMENTE RIPRISTINARE INOLTRE,  GRAZIE MILLE, '}], [{'summary_text': "POTETE INSTALLARE,  GPRODUCT COMPLIANCEMANAGEMENT and Project MANAGEMENT are installed.  The project manager is called Project Management and the project manager's is called Purchasing and Research. The project management is called Procrastination. 

# df_3

# df_3_printer 

In [155]:
#specify number of rows in each chunk
n=9
#split DataFrame into chunks
list_df = [df_3_printer[i:i+n] for i in range(0,len(df_3_printer),n)]
    #print(list_df)

In [156]:
len(list_df)

37

In [157]:
list_df[36]

Title  \
324                                    Stampante   
325                                      Plotter   
326                             Printer in error   
327                       Stampante non funziona   
328  Problema accesso cartella \\Controller-TX30   
329        Installation SECURE PRINTER (GANG VK)   
330                                    Stampante   
331           RE: Ticket #513035 Assigned to you   
332                       stampante non funziona   

                                                 Topic  \
324  {"11":"Hardware, Telephony, Smartphones, Monit...   
325  {"11":"Hardware, Telephony, Smartphones, Monit...   
326  {"11":"Hardware, Telephony, Smartphones, Monit...   
327  {"11":"Hardware, Telephony, Smartphones, Monit...   
328  {"11":"Hardware, Telephony, Smartphones, Monit...   
329  {"11":"Hardware, Telephony, Smartphones, Monit...   
330  {"11":"Hardware, Telephony, Smartphones, Monit...   
331  {"11":"Hardware, Telephony, Smartphones, Monit...   
332  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
324                      LA MIA STAMPANTE NON MI PIACE  
325  NON RIESCO PIU A STAMPARE DIRETTAMENTE SUL PLO...  
326        NON STAMPA QUANDO PROVA DI PREMERE IL TASTO  
327  CIAO  DURA SEMPRE CA 20 SEC PER OGNI STAMPANTE...  
328  CIAO A TUTTI NON RIUSCIAMO AD ACCEDERE ALLA CA...  
329  CIAO PREGO INSTALLARE LA POSSIBILITA DI STAMPA...  
330     CIAO LA STAMPANTE HP2891F8 NON FUNZIONA GRAZIE  
331   CIAO   BASTA CHE RIAVVIA IL PC DA DOVE VUOLE ...  
332  CIAO FRANCESCO LA STAMPANTE DI ERNESTO ANCORA ...

In [158]:
def put_together():
    list1=[]
    for index in range(0,36):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block


Result 0:
CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZIONA E VENUTO FUORI CHE MANCA LA CARTA MA NON FUNZIONA COMUNQUE GRAZIESALUTICIAO MI POETE COLLEGARE PER FAVORE QUESTA STAMPANTE  GRAZIE MILLE  SALUTICIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BLOCCATA SAREBBE ANCHE DA DARE ACCESSO ALLA STAMPANTE CHE ABBIAMO IN UFFICIO GRAZIELA STAMPANTE SERVICE SECONDO PIANO NON ULTIMA I LAVORI E D COME MESSAGGIO RIORDINARE TONER GIALLO   HO LANCAITA DELLE STAMPE DA 45 PAGINE E SI FERMA A MET STAMPA SOLO LE PRIME 10  ACS 1280080 SERVE ALTROSTAMPANTE ZEBRA NON STAMPA DA NAVISIONCIAO IO E JOHANNES CI SIAMO SPOSTATI NELLUFFICIO CHE ERA DI STAUDER  BISOGNA RIMETTERE I TELEFONI E CONFIGURARE LA STAMPANTE CHE C QUI NEL CORRIDOIOLA STAMPANTE QUANDO STAMPA FA UN RUMORE STRANOCODICE STAMPANTE D1280080 DEL SECONDO PIANO DE SERVICE QUELLA CHE QUANDO BISOGNA SELEZIONARE ESCE SOTTO SERVICE E1GRAZIESTAMPANTE XEROX BLOCCATA VICINO SALA RIUNIONE 7STAMPANTE BLOCCOTA

Result 1:
CIAO  LA STAMPANTE AL SECONDO PIANO  

['CIAO LA STAMPANTE NEL NOSTRO UFFICIO NON FUNZIONA E VENUTO FUORI CHE MANCA LA CARTA MA NON FUNZIONA COMUNQUE GRAZIESALUTICIAO MI POETE COLLEGARE\xa0PER FAVORE QUESTA STAMPANTE  GRAZIE MILLE  SALUTICIAO LA STAMPANTE VERKAUF PCV ON PRTSERV01  BLOCCATA SAREBBE ANCHE DA DARE ACCESSO ALLA STAMPANTE CHE ABBIAMO IN UFFICIO GRAZIELA STAMPANTE SERVICE SECONDO PIANO NON ULTIMA I LAVORI E D COME MESSAGGIO RIORDINARE TONER GIALLO   HO LANCAITA DELLE STAMPE DA 45 PAGINE E SI FERMA A MET STAMPA SOLO LE PRIME 10  ACS 1280080 SERVE ALTROSTAMPANTE ZEBRA NON STAMPA DA NAVISIONCIAO IO E JOHANNES CI SIAMO SPOSTATI NELLUFFICIO CHE ERA DI STAUDER\xa0 BISOGNA RIMETTERE I TELEFONI E CONFIGURARE LA STAMPANTE CHE C QUI NEL CORRIDOIOLA STAMPANTE QUANDO STAMPA FA UN RUMORE STRANOCODICE STAMPANTE D1280080 DEL SECONDO PIANO DE SERVICE QUELLA CHE QUANDO BISOGNA SELEZIONARE ESCE SOTTO SERVICE E1GRAZIESTAMPANTE XEROX BLOCCATA VICINO SALA RIUNIONE 7STAMPANTE BLOCCOTA',
 'CIAO\xa0 LA STAMPANTE AL SECONDO PIANO  FUORI 

In [159]:
picklefile = "df_3_printer_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "Installing the software is easy. It's recommended to install the following files:    Excel EDGEL ED OUTLOOK SU LA MACCHINA C255, LNDF PER LAMBIENTE TEST DI PROFILE NEXT GRAZIECIAO POTETE INSTALLARE DYNAMICS NAV SUL MIO PC E ANCHE IL VPN. "}], [{'summary_text': 'Team Viewer 1 895 609 981 PSW CF99MA4U,   GRAZIE MILLECIAO, MI POTETE INSTALLARE, IL PACHETTO OFFICE WORD EXCEL, DOPO LO SPOSTAMENTO, DELLA MIA UTENZA SU TA NON FUNZIONA PI LACROBAT WRITER PER MODIFICAREELABORARE PDF, GPRODUCT COMPLIANCEMANAGEMENT08.08.'}], [{'summary_text': 'There are ten ways to install a program on a computer. The program is called BUONGIORNO,    NUOVA STAMPANTE EPOWERTRAC GENTILMENTE RIPRISTINARE INOLTRE,  GRAZIE MILLE, '}], [{'summary_text': "POTETE INSTALLARE,  GPRODUCT COMPLIANCEMANAGEMENT and Project MANAGEMENT are installed.  The project manager is called Project Management and the project manager's is called Purchasing and Research. The project management is called Procrastination. 

# df_3_docking

In [160]:
#specify number of rows in each chunk
n=4
#split DataFrame into chunks
list_df = [df_3_docking[i:i+n] for i in range(0,len(df_3_docking),n)]
    #print(list_df)

In [161]:
len(list_df)

42

In [162]:
list_df[41]

Title                                              Topic  \
164  Nuovo posto PLC  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
164  CIAO MI POTETE INSTALLARE DOMANI PER STEFANIE ...

In [163]:
def put_together():
    list1=[]
    for index in range(0,41):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN SE NE AVETE UNO DOVREI RITIRARLO OGGI PERCH MI SERVE DOMANI PER UNA MESSA IN SERVIZIO HO ANCHE UN SECONDO CAVO PER LA NUOVA DOCKING STATION CHE NON MI SERVE E CHE VI POSSO RIDARE SALUTI IVAN BERGAMOCIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTIBUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO CON UN PORTATILE  DOCKING STATION UTILIZZO GI LA VDI DAL PC FISSO QUINDI NON SERVONO ULTERIORI LICENZE GERNOT NISCHLER E FLORIAN SCHWALT MI HANNO GI DATO LOK DA PARTE LORO SAREBBE POSSIBILE AVER IL PORTATILE  GRAZIE STEFANOBUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409 DEVO SPOSTARMI DI UFFICIO IL MIO NUOVO UFFICIO SAR IN LOGISTICA CONTRASSEGNATO DAL CARTELLO LOGISTICS 212B  NECESSARIO SPOSTARE LA DOCKING 

['CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN SE NE AVETE UNO DOVREI RITIRARLO OGGI PERCH MI SERVE DOMANI PER UNA MESSA IN SERVIZIO HO ANCHE UN SECONDO CAVO PER LA NUOVA DOCKING STATION CHE NON MI SERVE E CHE VI POSSO RIDARE SALUTI IVAN BERGAMOCIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA\xa0DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA\xa0DOCKING STATION NON VENGONO VISTI TUTTAVIA LA\xa0DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA\xa0DOCKING STATION SALUTIBUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO CON UN PORTATILE  DOCKING STATION UTILIZZO GI LA VDI DAL PC FISSO QUINDI NON SERVONO ULTERIORI LICENZE GERNOT NISCHLER\xa0E FLORIAN SCHWALT MI HANNO GI DATO LOK DA PARTE LORO SAREBBE POSSIBILE AVER IL PORTATILE  GRAZIE STEFANOBUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409 DEVO SPOSTARMI DI UFFICIO IL MIO NUOVO UFFICIO SAR IN LOGISTICA CONTRASSEGNATO DAL CARTELLO LOGISTICS 212B  NECESSARIO\xa0SPOSTARE L

In [168]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 41):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [169]:
blocks_to_skip = [27,28]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN SE NE AVETE UNO DOVREI RITIRARLO OGGI PERCH MI SERVE DOMANI PER UNA MESSA IN SERVIZIO HO ANCHE UN SECONDO CAVO PER LA NUOVA DOCKING STATION CHE NON MI SERVE E CHE VI POSSO RIDARE SALUTI IVAN BERGAMOCIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTIBUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO CON UN PORTATILE  DOCKING STATION UTILIZZO GI LA VDI DAL PC FISSO QUINDI NON SERVONO ULTERIORI LICENZE GERNOT NISCHLER E FLORIAN SCHWALT MI HANNO GI DATO LOK DA PARTE LORO SAREBBE POSSIBILE AVER IL PORTATILE  GRAZIE STEFANOBUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409 DEVO SPOSTARMI DI UFFICIO IL MIO NUOVO UFFICIO SAR IN LOGISTICA CONTRASSEGNATO DAL CARTELLO LOGISTICS 212B  NECESSARIO SPOSTARE LA DOCKING 

In [170]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN SE NE AVETE UNO DOVREI RITIRARLO OGGI PERCH MI SERVE DOMANI PER UNA MESSA IN SERVIZIO HO ANCHE UN SECONDO CAVO PER LA NUOVA DOCKING STATION CHE NON MI SERVE E CHE VI POSSO RIDARE SALUTI IVAN BERGAMOCIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTIBUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO CON UN PORTATILE  DOCKING STATION UTILIZZO GI LA VDI DAL PC FISSO QUINDI NON SERVONO ULTERIORI LICENZE GERNOT NISCHLER E FLORIAN SCHWALT MI HANNO GI DATO LOK DA PARTE LORO SAREBBE POSSIBILE AVER IL PORTATILE  GRAZIE STEFANOBUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409 DEVO SPOSTARMI DI UFFICIO IL MIO NUOVO UFFICIO SAR IN LOGISTICA CONTRASSEGNATO DAL CARTELLO LOGISTICS 212B  NECESSARIO SPOSTARE LA DOCKING 

['CIAO MI MANCA ANCORA UN ADATTATORE USB PER LAN SE NE AVETE UNO DOVREI RITIRARLO OGGI PERCH MI SERVE DOMANI PER UNA MESSA IN SERVIZIO HO ANCHE UN SECONDO CAVO PER LA NUOVA DOCKING STATION CHE NON MI SERVE E CHE VI POSSO RIDARE SALUTI IVAN BERGAMOCIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA\xa0DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA\xa0DOCKING STATION NON VENGONO VISTI TUTTAVIA LA\xa0DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA\xa0DOCKING STATION SALUTIBUONGIORNO VORREI SOSTITUIRE IL MIO PC FISSO CON UN PORTATILE  DOCKING STATION UTILIZZO GI LA VDI DAL PC FISSO QUINDI NON SERVONO ULTERIORI LICENZE GERNOT NISCHLER\xa0E FLORIAN SCHWALT MI HANNO GI DATO LOK DA PARTE LORO SAREBBE POSSIBILE AVER IL PORTATILE  GRAZIE STEFANOBUONGIORNO CON LARRIVO DI TERESA BUFFA IL 0409 DEVO SPOSTARMI DI UFFICIO IL MIO NUOVO UFFICIO SAR IN LOGISTICA CONTRASSEGNATO DAL CARTELLO LOGISTICS 212B  NECESSARIO\xa0SPOSTARE L

In [175]:
picklefile = "df_3_docking_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "Docking Station is located in Riga, Italy. The USB is used to connect the station to the Internet. It is possible to connect to it via USB. The station is connected to the internet via a cable and a phone line. It's also connected to a radio and a television."}], [{'summary_text': 'After 3 weeks of using USBC HDMI DP, CIAO LA DOCKING CHE MI AVETE CONSEGNATO IERI NON FUNZIONA O MEGLIO MI DICE CHE non  QUELLA GIUSTA VI POTETE COLLEGARE TRAMITE TEAM VIEVER. '}], [{'summary_text': "The USB cable on the Docking Station is not working. The network cable is plugged into the office at 232 and the USB cable is on the dock. The dock station is located in Mezzohi, but I don't know where to find the address."}], [{'summary_text': ' USB VON DOCKING STATION FUNKTIONIEREN NICHTLENOVO Docking Station is not working anymore. The second monitor is not able to change the resolution of the first monitor. The left USBC port is working, but the right port is not.'}], [{'summary_text': 'D

# df_3_tcp

In [201]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_tcp[i:i+n] for i in range(0,len(df_3_tcp),n)]
    #print(list_df)

In [202]:
len(list_df)

4

In [207]:
list_df[3]

Title                                              Topic  \
9  Printer out of order  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...

In [208]:
def put_together():
    list1=[]
    for index in range(0,4):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 1:
HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDOWS 11 NICHT KOMPATIBEL IST DANKE INZWISCHEN

['SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIE',
 'HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL\xa0KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDOWS 11 NICHT KOMPATIBEL IST DANKE INZWISCHEN ANNAL

In [209]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 4):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [210]:
blocks_to_skip = [1]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 2:
CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A C

In [211]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 2:
CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A C

['SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIE',
 'CIAO CON IL TICKET\xa0473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A CAMBIAR

In [215]:
picklefile = "df_1_computer_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "A new PC is not connected to the internet and I can't log in to my SAPCONCUR because I forgot my password. I have a new PC but can't connect it to the Internet because it's not connected with the Internet.   "}], [{'summary_text': 'HALLO BITTE DEN ORDNER: GPRODUKTION PRODUKTIONSLEITUNG FR, PC C247ALPIN LOCAL, FREIGEBEN NUR LESERECHTE DANKECIAO, HO CONTATTATO, STEPHANE, GRAZIEDANIELE MICHEL, FATTO LAGGIORNAMENTO, CHIESTO DAL, POI HA SPENTO E RIACCESO PERO ADESSO C QUESTO COSA DEVE FARENON CI SONO NELLA CARTELLA SPAM. '}], [{'summary_text': "There will be a new technician in France on May 15th. Her PC will be MFL0197, the same rightsprofile as SEBASTIEN COQUET's PC C235. It's not possible to connect DMS or NAVHLLO to the SVN server."}], [{'summary_text': 'All TAFR COLLABORATORS have signed a document in agreement with Human Resources Society to prevent the use of personal mobiles. The LAPTOP app does not work on the Laptop, so Daniele needs to find a solution for the 

# df_3_db

In [239]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_db[i:i+n] for i in range(0,len(df_3_db),n)]
    #print(list_df)

In [240]:
len(list_df)

4

In [241]:
list_df[3]

Title                                              Topic  \
9  Printer out of order  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
9  MY LOCAL PRINTER DOESNT WORK PROPERLY SINCE TH...

In [244]:
def put_together():
    list1=[]
    for index in range(0,4):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 1:
HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDOWS 11 NICHT KOMPATIBEL IST DANKE INZWISCHEN

['SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIE',
 'HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL\xa0KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDOWS 11 NICHT KOMPATIBEL IST DANKE INZWISCHEN ANNAL

In [245]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 4):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [246]:
blocks_to_skip = [1]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 2:
CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A C

In [247]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIE

Result 2:
CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A C

['SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIE',
 'CIAO CON IL TICKET\xa0473713 AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE CHE TRAMITE LAPPOSITO PORTALE LENOVO PURTROPPO IL PROBLEMA DELLETHERNET NON FUNZIONANTE CONTINUA AD ESSERCI VI CHIEDO SE POSSIAMO PROVARE A CAMBIAR

In [251]:
picklefile = "df_3_db_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE  GRAZIEA PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE.'}], [{'summary_text': 'CIAO CON IL TICKET is 473713. AVEVAMO AGGIORNATO TUTTI I DRIVER SIA TRAMITE WINDOWS UPDATE. LENOVO THINKPAD X1 CARBON 7TH SYSTEM MODEL 20QES1HH00 DOCKING STATION 3 DOCK MODEL NO DBB9003L1 WINDOWS 10019045. '}], [{'summary_text': "The update of Windows 10 on Monday made the local printer not work properly, so it doesn't work properly anymore. It's been broken since Monday this week. It doesn't seem to work properly since the update of WINDOWS 10. It is broken because of a bug."}]]


# df_3_pc

In [265]:
#specify number of rows in each chunk
n=4
#split DataFrame into chunks
list_df = [df_3_pc[i:i+n] for i in range(0,len(df_3_pc),n)]
    #print(list_df)

In [266]:
len(list_df)

97

In [267]:
list_df[96]

Title  \
384   Telefono FISSO non funziona più   
385          Chiamate verso l'esterno   
386                 Telefono Cordless   
387  sostituzione cellulare aziendale   

                                                 Topic  \
384  {"11":"Hardware, Telephony, Smartphones, Monit...   
385  {"11":"Hardware, Telephony, Smartphones, Monit...   
386  {"11":"Hardware, Telephony, Smartphones, Monit...   
387  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
384                     TELEFONO FISSO NON FUNZIONA PI  
385  BUON POMERIGGIO NON RIESCO AD EFFETTURARE CHIA...  
386  BUONGIORNO  ATTUALMENTE MI  STATO FORNITO UN T...  
387  LA BATTERIA DEL TELEFONO NON MANTIENE PI LA CA...

In [268]:
def put_together():
    list1=[]
    for index in range(0,96):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD YOU PLEASE GIVE ME SOME ADVICE WHICH ONE IS SUITABLE I WILL CHECK THE PRICE WITH DATEF AND ALSO HERE IN SLOVAKIA THANK YOU ZUZANA HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SICH MEIN LAPTOP NICHT RICHTIG MIT DEM HOTSPOT DES FIRMENHANDYS VERBINDET ES ZEIGT ZWAR AN DASS ER SICH VERBUNDEN HAT ALLERDINGS HABE ICH KEINEN ZUGRIFF INS INTERNETKNNTE MIR HIER JEMAND HELFENDANKECIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTICIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LENTO SIA IN AVVIO CHE NELLA GESTIONE DELLA VARIE APPLICAZIONI AVETE FATTO QUALCHE TENTATIVO DI PULIZIA MA SENZA GRANDE SUCCESSO RIFERIMENTO LAPTOP L340

Result 1:
HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER HRE BEI TEAMSANRUFEN LEIDER N

['HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD YOU PLEASE GIVE ME SOME ADVICE WHICH ONE IS SUITABLE I WILL CHECK THE PRICE WITH DATEF AND ALSO HERE IN SLOVAKIA THANK YOU ZUZANA\xa0HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SICH MEIN LAPTOP NICHT RICHTIG MIT DEM HOTSPOT DES FIRMENHANDYS VERBINDET ES ZEIGT ZWAR AN DASS ER SICH VERBUNDEN HAT ALLERDINGS HABE ICH KEINEN ZUGRIFF INS INTERNETKNNTE MIR HIER JEMAND HELFENDANKECIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA\xa0DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA\xa0DOCKING STATION NON VENGONO VISTI TUTTAVIA LA\xa0DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA\xa0DOCKING STATION SALUTICIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LENTO SIA IN AVVIO CHE NELLA GESTIONE DELLA VARIE APPLICAZIONI AVETE FATTO QUALCHE TENTATIVO DI PULIZIA MA SENZA GRANDE SUCCESSO RIFERIMENTO LAPTOP L340',
 'HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER HRE BEI TEAMSANRUFEN LEIDER N

In [269]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 96):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [270]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)


Result 0:
HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD YOU PLEASE GIVE ME SOME ADVICE WHICH ONE IS SUITABLE I WILL CHECK THE PRICE WITH DATEF AND ALSO HERE IN SLOVAKIA THANK YOU ZUZANA HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SICH MEIN LAPTOP NICHT RICHTIG MIT DEM HOTSPOT DES FIRMENHANDYS VERBINDET ES ZEIGT ZWAR AN DASS ER SICH VERBUNDEN HAT ALLERDINGS HABE ICH KEINEN ZUGRIFF INS INTERNETKNNTE MIR HIER JEMAND HELFENDANKECIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTICIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LENTO SIA IN AVVIO CHE NELLA GESTIONE DELLA VARIE APPLICAZIONI AVETE FATTO QUALCHE TENTATIVO DI PULIZIA MA SENZA GRANDE SUCCESSO RIFERIMENTO LAPTOP L340

Result 1:
HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER HRE BEI TEAMSANRUFEN LEIDER N

In [271]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test


Result 0:
HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD YOU PLEASE GIVE ME SOME ADVICE WHICH ONE IS SUITABLE I WILL CHECK THE PRICE WITH DATEF AND ALSO HERE IN SLOVAKIA THANK YOU ZUZANA HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SICH MEIN LAPTOP NICHT RICHTIG MIT DEM HOTSPOT DES FIRMENHANDYS VERBINDET ES ZEIGT ZWAR AN DASS ER SICH VERBUNDEN HAT ALLERDINGS HABE ICH KEINEN ZUGRIFF INS INTERNETKNNTE MIR HIER JEMAND HELFENDANKECIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA DOCKING STATION NON VENGONO VISTI TUTTAVIA LA DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA DOCKING STATION SALUTICIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LENTO SIA IN AVVIO CHE NELLA GESTIONE DELLA VARIE APPLICAZIONI AVETE FATTO QUALCHE TENTATIVO DI PULIZIA MA SENZA GRANDE SUCCESSO RIFERIMENTO LAPTOP L340

Result 1:
HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER HRE BEI TEAMSANRUFEN LEIDER N

['HI I NEED TO ORDER A NEW LAPTOP FOR ME COULD YOU PLEASE GIVE ME SOME ADVICE WHICH ONE IS SUITABLE I WILL CHECK THE PRICE WITH DATEF AND ALSO HERE IN SLOVAKIA THANK YOU ZUZANA\xa0HALLO SEIT KURZEM IST MIR AUFGEFALLEN DASS SICH MEIN LAPTOP NICHT RICHTIG MIT DEM HOTSPOT DES FIRMENHANDYS VERBINDET ES ZEIGT ZWAR AN DASS ER SICH VERBUNDEN HAT ALLERDINGS HABE ICH KEINEN ZUGRIFF INS INTERNETKNNTE MIR HIER JEMAND HELFENDANKECIAO DA QUESTA MATTINA NON HO COMUNICAZIONE TRA\xa0DOCKING STATION E LATPOT NON MI FUNZIONANO I MONITOR E GLI ATTACCHI USB SULLA\xa0DOCKING STATION NON VENGONO VISTI TUTTAVIA LA\xa0DOCKING STATION RICARICA IL LAPTOP HO PROVATO A RIAVVIARE IL PC E A TOGLIERE LALIMENTAZIONE ALLA\xa0DOCKING STATION SALUTICIAO DA VALUTARE LA SOSTITUZIONE IN QUANTO LENTO SIA IN AVVIO CHE NELLA GESTIONE DELLA VARIE APPLICAZIONI AVETE FATTO QUALCHE TENTATIVO DI PULIZIA MA SENZA GRANDE SUCCESSO RIFERIMENTO LAPTOP L340',
 'HABE DEN LAPTOP MIT DEN AIRPODS VERBUNDEN ABER HRE BEI TEAMSANRUFEN LEIDER N

In [275]:
picklefile = "df_3_pc_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'Zuzana needs to buy a new laptop. She will check the price with DATEF and also here in SLOVAKIA. She is looking for advice on which laptop is suitable for her. Zuzana thanks Zuza for her advice. '}], [{'summary_text': "After 3 weeks of using USBC HDMI DP, the screen on Brian's laptop was blacked out. He re-attached the screen to the laptop and it worked fine again. Brian tried to fix the problem by connecting the USB to the HDMI but it didn't work."}], [{'summary_text': 'The connection between the screen and the laptop didn\'t work at Allciao\'s laptop, so he couldn\'t connect the screen to the other one. The screen is connected to the laptop via an app called "Cancun".    It\'s a free app.  '}], [{'summary_text': 'LAPTOP DI RAMEEZ HA PROBLEMI DI CARICARE SEMBRA CHE, LA PRESA DEL LAPTOP VI PORTO, MI SERVE DI NUOVO FINO VENERD SERA, GRAZIE CIAO MI POTETE PREGO PREPARARE ANCHE UN LAP TOP CON DOCKING. '}], [{'summary_text': 'Mattias will help Vincenca and dovremmo with

# df_3_vulnerabilities

In [288]:
#empty

# df_3_email

In [290]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_3_email[i:i+n] for i in range(0,len(df_3_email),n)]
    #print(list_df)

In [291]:
len(list_df)

6

In [293]:
list_df[5]

Title  \
30              Stampante non funziona   
31  RE: Ticket #513035 Assigned to you   

                                                Topic  \
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
30  CIAO  DURA SEMPRE CA 20 SEC PER OGNI STAMPANTE...  
31   CIAO   BASTA CHE RIAVVIA IL PC DA DOVE VUOLE ...

In [295]:
def put_together():
    list1=[]
    for index in range(0,5):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block


Result 0:
BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NON SIA COLLEGATO CON LA MIA MAIL COSI I MIEI COLLEGHI NON SONO IN GRADO DI CHIAMARMI SUL TELEFONO AZIENDALE NR CEL 39 331 687 2780 SALUTI PATRICK ZINGERLESALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO CHE SI VEDE NELLA SIGNATURA DELLE MIE EMAIL DA 0417 550 550 A 0471 550 447 COSI CHE POSSO ESSERE CONTATTATO DIRETTAMENTE  GRAZIE SALUTIHELLO FRANCESCO THX NOW WORK FOR MY  I WILL MAKE A MAIL TO MY COLLEGS HERE IN SAVISE AND INFORM THEM THEY HAVE TO MAKE A NEW TICKET AND PUT THIS REF CONCERN TICKET 582224 448213 THX PATRICKI CALLED HIM AND SENT A MAIL WITH PHOTO THE SCREEN IS NOT WORKING WITH ANY PC  THANK YOU FOR YOUR HELPBUONGIORNO  FINITO IL TONER DELLA STAMPANTE XEROX AL SECONDO PIANO CON CODICE ACS 1247109  GRAZIE  SALUTI SARA LOREFICE PS LA MIA EMAIL ATTUALE  SARALOREFICETECHNOALPINCOM  CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA SPAZIAN DOPO AVER INVIATO LOK PER MAIL ANCHE CONFERMATO DI GIORGIO IL 2707 PER MAIL AD ARASHDEEP GRA

['BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NON SIA COLLEGATO CON LA MIA MAIL COSI I MIEI COLLEGHI NON SONO IN GRADO DI CHIAMARMI SUL TELEFONO AZIENDALE NR CEL 39 331 687 2780 SALUTI PATRICK ZINGERLESALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO CHE SI VEDE\xa0NELLA SIGNATURA DELLE MIE\xa0EMAIL DA 0417 550 550 A 0471 550 447 COSI CHE\xa0POSSO ESSERE CONTATTATO DIRETTAMENTE  GRAZIE SALUTIHELLO FRANCESCO THX NOW WORK FOR MY\xa0 I WILL MAKE A MAIL TO MY COLLEGS HERE IN SAVISE\xa0AND INFORM THEM THEY HAVE TO MAKE A NEW TICKET AND PUT THIS REF\xa0CONCERN\xa0TICKET 582224\xa0448213 THX PATRICKI CALLED HIM AND SENT A MAIL WITH PHOTO THE SCREEN IS NOT WORKING WITH ANY PC\xa0 THANK YOU FOR YOUR HELPBUONGIORNO  FINITO IL TONER DELLA STAMPANTE XEROX AL SECONDO PIANO CON CODICE ACS 1247109\xa0 GRAZIE  SALUTI SARA LOREFICE PS LA MIA EMAIL ATTUALE  SARALOREFICETECHNOALPINCOM\xa0 CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA SPAZIAN DOPO AVER INVIATO LOK PER MAIL ANCHE CONFERMATO DI GIORGIO IL 2707 

In [296]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 5):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [297]:
blocks_to_skip = [2]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NON SIA COLLEGATO CON LA MIA MAIL COSI I MIEI COLLEGHI NON SONO IN GRADO DI CHIAMARMI SUL TELEFONO AZIENDALE NR CEL 39 331 687 2780 SALUTI PATRICK ZINGERLESALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO CHE SI VEDE NELLA SIGNATURA DELLE MIE EMAIL DA 0417 550 550 A 0471 550 447 COSI CHE POSSO ESSERE CONTATTATO DIRETTAMENTE  GRAZIE SALUTIHELLO FRANCESCO THX NOW WORK FOR MY  I WILL MAKE A MAIL TO MY COLLEGS HERE IN SAVISE AND INFORM THEM THEY HAVE TO MAKE A NEW TICKET AND PUT THIS REF CONCERN TICKET 582224 448213 THX PATRICKI CALLED HIM AND SENT A MAIL WITH PHOTO THE SCREEN IS NOT WORKING WITH ANY PC  THANK YOU FOR YOUR HELPBUONGIORNO  FINITO IL TONER DELLA STAMPANTE XEROX AL SECONDO PIANO CON CODICE ACS 1247109  GRAZIE  SALUTI SARA LOREFICE PS LA MIA EMAIL ATTUALE  SARALOREFICETECHNOALPINCOM  CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA SPAZIAN DOPO AVER INVIATO LOK PER MAIL ANCHE CONFERMATO DI GIORGIO IL 2707 PER MAIL AD ARASHDEEP GRA

In [298]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NON SIA COLLEGATO CON LA MIA MAIL COSI I MIEI COLLEGHI NON SONO IN GRADO DI CHIAMARMI SUL TELEFONO AZIENDALE NR CEL 39 331 687 2780 SALUTI PATRICK ZINGERLESALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO CHE SI VEDE NELLA SIGNATURA DELLE MIE EMAIL DA 0417 550 550 A 0471 550 447 COSI CHE POSSO ESSERE CONTATTATO DIRETTAMENTE  GRAZIE SALUTIHELLO FRANCESCO THX NOW WORK FOR MY  I WILL MAKE A MAIL TO MY COLLEGS HERE IN SAVISE AND INFORM THEM THEY HAVE TO MAKE A NEW TICKET AND PUT THIS REF CONCERN TICKET 582224 448213 THX PATRICKI CALLED HIM AND SENT A MAIL WITH PHOTO THE SCREEN IS NOT WORKING WITH ANY PC  THANK YOU FOR YOUR HELPBUONGIORNO  FINITO IL TONER DELLA STAMPANTE XEROX AL SECONDO PIANO CON CODICE ACS 1247109  GRAZIE  SALUTI SARA LOREFICE PS LA MIA EMAIL ATTUALE  SARALOREFICETECHNOALPINCOM  CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA SPAZIAN DOPO AVER INVIATO LOK PER MAIL ANCHE CONFERMATO DI GIORGIO IL 2707 PER MAIL AD ARASHDEEP GRA

['BUON GIORNO IL MIO NUMERO TELEFONICE SEMBRA NON SIA COLLEGATO CON LA MIA MAIL COSI I MIEI COLLEGHI NON SONO IN GRADO DI CHIAMARMI SUL TELEFONO AZIENDALE NR CEL 39 331 687 2780 SALUTI PATRICK ZINGERLESALVE POTRESTE CAMBIARE IL NUMERO DI TELEFONO CHE SI VEDE\xa0NELLA SIGNATURA DELLE MIE\xa0EMAIL DA 0417 550 550 A 0471 550 447 COSI CHE\xa0POSSO ESSERE CONTATTATO DIRETTAMENTE  GRAZIE SALUTIHELLO FRANCESCO THX NOW WORK FOR MY\xa0 I WILL MAKE A MAIL TO MY COLLEGS HERE IN SAVISE\xa0AND INFORM THEM THEY HAVE TO MAKE A NEW TICKET AND PUT THIS REF\xa0CONCERN\xa0TICKET 582224\xa0448213 THX PATRICKI CALLED HIM AND SENT A MAIL WITH PHOTO THE SCREEN IS NOT WORKING WITH ANY PC\xa0 THANK YOU FOR YOUR HELPBUONGIORNO  FINITO IL TONER DELLA STAMPANTE XEROX AL SECONDO PIANO CON CODICE ACS 1247109\xa0 GRAZIE  SALUTI SARA LOREFICE PS LA MIA EMAIL ATTUALE  SARALOREFICETECHNOALPINCOM\xa0 CIAO PREGO PROCEDERE CON LA RICHIESTA A LAURA SPAZIAN DOPO AVER INVIATO LOK PER MAIL ANCHE CONFERMATO DI GIORGIO IL 2707 

In [302]:
picklefile = "df_3_email_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': "Pater sent a photo to a colleague because the screen wasn't working with his PC. He called him and sent him a new ticket with the code for the ticket 582224-448213. The ticket is valid for the following dates: 1st January 2014. "}], [{'summary_text': 'HALLO, BITTE DAS THINKPAD, BIANCA ZANONA, NAV ATITDE, OFFICE, VPN,   TEAMVIEWER ID  1626243248. PW  TECHNOALPIN1, USER TAATBIANCAZ, SONNENSCHEIN23, DANKEBUONGIORNO PER LUTILIZZO DI MAIL, TELEFONATE FUORI ORARIO, CHIEDO DI RICEVERE, UNO SMARTPHONE DUAL SIM GRAZIECIAO and DANIELE VEDI LO SCREEN DE'}], [{'summary_text': "This is an external e-mail account. It is not recommended to open links or open attachments. It's possible to contact your IT department in case of emergency. It has different versions for Italian, Spanish, German, French, Italian and Spanish.  "}], [{'summary_text': 'Christina is having issues with the Postage Meter. She would like to have her PC scannelled for potential viruses. She sent the files to Ag

### df_3_software

In [ ]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_software[i:i+n] for i in range(0,len(df_3_software),n)]
    #print(list_df)

In [ ]:
len(list_df)

In [ ]:
list_df[11]

In [ ]:
def put_together():
    list1=[]
    for index in range(0,12):
        res = ''.join(map(str,list_df[index]['Text']))
        print('Result:\n',res,'\n')
        list1.append(res)
    return list1

In [ ]:
summ_block = put_together()
summ_block

In [ ]:
import pickle

In [289]:
picklefile = "df_3_software_summ.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

[[{'summary_text': 'My PC has been running very slow for the past few weeks because of a software update. The Internet connection is also not working properly. I would like to know if there is anything you can do to help me.   i.a. 39 349 785 7499. '}], [{'summary_text': 'Paraforma IL Software is a tool for installing software on a PC. It is available in Italian, Spanish, Italian, German, Polish and Italian. It can be downloaded from the following sites: iTunes, Amazon, Google Play, Bittigte Software, Microsoft, and Play Store. '}], [{'summary_text': 'Naviision is a teamviewer, a software developer, a printer and a software installer. The software is available in English, German, Finnish, Italian and Spanish. It is available on the following platforms: Windows, Mac OS X, Android, iOS and Windows Phone.'}], [{'summary_text': 'Gli scanner needs a USB RS845 CONVERTER and a 24V power supply. He will send him SCHEMATICS soon.    i.e. the program is written in C without PYTHON and has his ow